In [2]:
import os
import numpy as np
import pandas as pd
from dataclasses import dataclass
from datetime import timedelta

# ============================================================
# PURPOSE
# ============================================================
"""
CAPPED trailing stop-loss backtest using M5 candles.

Key assumptions:
1) Trades are entered at end-of-day (EOD) on EntryDate, so trailing logic starts from next day (configurable).
2) Trades are NOT allowed to extend beyond the original exit date (CAPPED).
   - If the trailing stop triggers before the original exit date => we exit early at the stop.
   - If it never triggers within the window => we exit at the original scheduled exit date price.
3) Only market-session M5 bars are used (pre/post market excluded).
   - Market session filter: 14:30 to 21:00 (inclusive), based on M5 timestamps.
4) Direction handling:
   - Direction may be "LONG"/"SHORT" or numeric (1, -1). We normalize it robustly.

Outputs:
- trade_summary_extracted.csv: 1 row per TradeID (entry/exit pulled from trade file)
- trades_trailing_capped_market_only.csv: per-trade trailing results (exit time/price/reason + analytics)
- summary_trailing_capped_market_only.csv: high-level summary
- coverage_report.csv: coverage checks
- m5_market_hours_filter_stats.csv: per-ticker M5 filtering stats
"""

# ============================================================
# CONFIG (EDIT THESE PATHS)
# ============================================================

TRADE_XLSX_PATH      = r"D:/work/Client/Maatra/Trade Level Data/3 Month vol 14 data with sharpe prob Fnl.xlsx"
M5_DIR               = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data"
M5_FILE_LIST_PATH    = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data/m5_file_list.csv"
MAPPING_XLSX_PATH    = r"D:/work/Client/Maatra/Trade Level Data/Instrument Mapping.xlsx"

OUT_DIR = os.path.join(os.path.dirname(TRADE_XLSX_PATH), "TrailingSL_CAPPED_ONLY_MKT1430_2100_FIXEDDIR")
os.makedirs(OUT_DIR, exist_ok=True)

RUN_ALL_TRADES = True
N_SAMPLE_TRADES = 2000
RANDOM_SEED = 42

# ============================================================
# MARKET HOURS FILTER (ONLY USE 14:30 to 21:00)
# ============================================================
MARKET_START = "14:30"
MARKET_END   = "21:00"   # inclusive

# ============================================================
# TRAILING STOP PARAMETERS (your approach)
# ============================================================
ATR_WINDOW = 14
ATR_MULT = 3.0

SLOPE_WINDOW = 12
SLOPE_METHOD = "regression"   # "regression" or "polyfit"
USE_TIME_AWARE_SLOPE = True

# slope_norm = slope / ATR
SLOPE_UPPER = 0.30
SLOPE_LOWER = 0.10

ACCEL_FACTOR = 1.0
MIN_MULT = 0.5

# Since entry is at EOD, apply trailing from next day
APPLY_FROM_NEXT_DAY = True

# ============================================================
# HELPERS: normalization + direction parsing + mapping
# ============================================================

def normalize_ticker(x: str) -> str:
    """Uppercase alnum-only ticker key."""
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return ""
    x = str(x).strip().upper()
    return "".join([ch for ch in x if ch.isalnum()])

def trade_base_from_currency(currency: str) -> str:
    """
    Trade file may have Currency like 'AAPL/USD' or just 'AAPL'.
    We extract the base and normalize.
    """
    if currency is None or (isinstance(currency, float) and np.isnan(currency)):
        return ""
    s = str(currency).strip().upper()
    base = s.split("/")[0].strip() if "/" in s else s
    return normalize_ticker(base)

def normalize_direction(x) -> str:
    """
    Normalizes direction to 'LONG' or 'SHORT'.

    Handles cases:
      - 'LONG'/'SHORT'
      - 'BUY'/'SELL'
      - 1 / -1 (or '1', '-1', 1.0, -1.0)
    """
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return "UNKNOWN"

    s = str(x).strip().upper()

    if s in ["LONG", "BUY", "B", "1", "1.0", "+1", "+1.0"]:
        return "LONG"
    if s in ["SHORT", "SELL", "S", "-1", "-1.0"]:
        return "SHORT"

    # Try numeric parsing
    try:
        v = float(s)
        if v > 0:
            return "LONG"
        if v < 0:
            return "SHORT"
    except Exception:
        pass

    return "UNKNOWN"

def load_trade_to_m5_mapping(mapping_xlsx_path: str) -> dict:
    """
    Uses Instrument Mapping.xlsx to map trade instrument -> M5 file ticker.
    Expected columns: org_symbol (M5 ticker), Symbol (trade symbol like AAPL/USD).
    """
    mp = pd.read_excel(mapping_xlsx_path)
    mp.columns = [c.strip() for c in mp.columns]
    if "org_symbol" not in mp.columns or "Symbol" not in mp.columns:
        raise ValueError("Mapping file must contain columns: org_symbol, Symbol")

    mp["m5_ticker"] = mp["org_symbol"].apply(normalize_ticker)
    mp["trade_base"] = mp["Symbol"].astype(str).str.upper().str.strip().str.split("/").str[0].apply(normalize_ticker)
    mp = mp[(mp["trade_base"] != "") & (mp["m5_ticker"] != "")]
    mp = mp.drop_duplicates(subset=["trade_base"], keep="first")
    return dict(zip(mp["trade_base"], mp["m5_ticker"]))

TRADE_TO_M5 = load_trade_to_m5_mapping(MAPPING_XLSX_PATH)

def map_trade_base_to_m5(trade_base: str) -> str:
    """Map trade base ticker to M5 ticker using mapping. If not found, fallback to itself."""
    t = normalize_ticker(trade_base)
    return TRADE_TO_M5.get(t, t)

# ============================================================
# M5 FILE MAP
# ============================================================

def load_m5_file_map(m5_dir: str, file_list_path: str) -> dict:
    """
    Reads m5_file_list.csv, expected columns: ticker, filename
    and returns dict: ticker_norm -> full filepath
    """
    fl = pd.read_csv(file_list_path)
    fl["ticker_norm"] = fl["ticker"].apply(normalize_ticker)
    fl["path"] = fl["filename"].apply(lambda f: os.path.join(m5_dir, f))
    return dict(zip(fl["ticker_norm"], fl["path"]))

M5_MAP = load_m5_file_map(M5_DIR, M5_FILE_LIST_PATH)
M5_TICKERS = set(M5_MAP.keys())

# ============================================================
# INDICATORS: ATR + SLOPE
# ============================================================

def compute_atr(df: pd.DataFrame, window: int) -> pd.Series:
    """
    ATR using simple rolling mean of True Range.
    True Range = max(high-low, abs(high-prev_close), abs(low-prev_close))
    """
    high = df["high"]
    low = df["low"]
    close = df["close"]
    tr = pd.concat([
        high - low,
        (high - close.shift(1)).abs(),
        (low - close.shift(1)).abs()
    ], axis=1).max(axis=1)
    return tr.rolling(window, min_periods=window).mean()

def rolling_slope(y: pd.Series, tmin: pd.Series | None, method: str) -> float:
    """
    Computes slope of y vs x where x is time (minutes) or simple index.
    - regression: OLS slope
    - polyfit: np.polyfit slope
    """
    yy = y.values.astype(float)
    if len(yy) < 2 or np.all(np.isnan(yy)):
        return np.nan

    if tmin is None:
        xx = np.arange(len(yy), dtype=float)
    else:
        xx = tmin.values.astype(float)
        xx = xx - xx[0]

    mask = ~np.isnan(xx) & ~np.isnan(yy)
    xx = xx[mask]; yy = yy[mask]
    if len(yy) < 2:
        return np.nan

    if method == "polyfit":
        return np.polyfit(xx, yy, 1)[0]

    xm = xx.mean(); ym = yy.mean()
    denom = ((xx - xm) ** 2).sum()
    if denom == 0:
        return np.nan
    return (((xx - xm) * (yy - ym)).sum()) / denom

# ============================================================
# MARKET HOURS FILTER
# ============================================================

def filter_market_hours(df: pd.DataFrame) -> pd.DataFrame:
    """
    Keep only rows with time between MARKET_START and MARKET_END (inclusive),
    based on df['_dt'].
    """
    if df.empty:
        return df

    dfi = df.set_index("_dt", drop=False).sort_index()
    try:
        dfi = dfi.between_time(MARKET_START, MARKET_END, inclusive="both")
    except TypeError:
        # older pandas fallback
        idx = dfi.index.indexer_between_time(
            pd.to_datetime(MARKET_START).time(),
            pd.to_datetime(MARKET_END).time(),
            include_start=True,
            include_end=True
        )
        dfi = dfi.iloc[idx]
    return dfi.reset_index(drop=True)

# ============================================================
# TRADE EXTRACTION: 1 ROW PER TRADEID
# ============================================================

def build_trade_summary(raw: pd.DataFrame):
    """
    From the trade-level file (multiple rows per TradeID across days),
    we extract:
      - EntryDate: DayStatus == OPEN else earliest date
      - ExitDate_Original: Closing Date (scheduled exit date)
      - EntryPrice: last trade-file price on EntryDate
      - ExitPrice_Original: last trade-file price on ExitDate
      - Direction normalized to LONG/SHORT
      - Currency -> TradeBase -> TickerNorm (using mapping)
    """
    df = raw.copy()
    df.columns = [c.strip() for c in df.columns]

    required = ["TradeID", "Currency", "Direction", "date", "price", "Closing Date", "DayStatus"]
    missing = [c for c in required if c not in df.columns]
    if missing:
        raise ValueError(f"Trade file missing required columns: {missing}")

    df["date"] = pd.to_datetime(df["date"], errors="coerce")
    df["Closing Date"] = pd.to_datetime(df["Closing Date"], errors="coerce")
    df["price"] = pd.to_numeric(df["price"], errors="coerce")
    df["DayStatusU"] = df["DayStatus"].astype(str).str.upper().str.strip()

    df["TradeBase"] = df["Currency"].apply(trade_base_from_currency)
    df["TickerNorm"] = df["TradeBase"].apply(map_trade_base_to_m5)
    df["DirectionNorm"] = df["Direction"].apply(normalize_direction)

    rows = []
    reasons = []

    for tid, g in df.groupby("TradeID", dropna=True):
        g = g.sort_values("date")

        currency = g["Currency"].dropna().iloc[0] if g["Currency"].notna().any() else np.nan
        direction = g["DirectionNorm"].dropna().iloc[0] if g["DirectionNorm"].notna().any() else "UNKNOWN"
        trade_base = g["TradeBase"].dropna().iloc[0] if g["TradeBase"].notna().any() else ""
        ticker = g["TickerNorm"].dropna().iloc[0] if g["TickerNorm"].notna().any() else ""

        open_mask = g["DayStatusU"].eq("OPEN")
        entry_date = g.loc[open_mask, "date"].dropna().min() if open_mask.any() else g["date"].dropna().min()
        exit_date = g["Closing Date"].dropna().max()

        # Entry price: last trade-file price on entry date
        entry_px = np.nan
        if pd.notna(entry_date):
            day = entry_date.normalize()
            day_rows = g[g["date"].dt.normalize() == day]
            if day_rows["price"].notna().any():
                entry_px = float(day_rows["price"].dropna().iloc[-1])

        # Exit price: last trade-file price on exit date
        exit_px = np.nan
        if pd.notna(exit_date):
            day = exit_date.normalize()
            day_rows = g[g["date"].dt.normalize() == day]
            if day_rows["price"].notna().any():
                exit_px = float(day_rows["price"].dropna().iloc[-1])

        miss = []
        if pd.isna(entry_date): miss.append("MISSING_ENTRY_DATE")
        if pd.isna(exit_date): miss.append("MISSING_EXIT_DATE")
        if pd.isna(entry_px): miss.append("MISSING_ENTRY_PRICE")
        if pd.isna(exit_px): miss.append("MISSING_EXIT_PRICE")
        if not ticker: miss.append("MISSING_TICKER")
        if ticker and (ticker not in M5_TICKERS): miss.append("TICKER_NOT_IN_M5_LIST")
        if direction == "UNKNOWN": miss.append("UNKNOWN_DIRECTION")

        if miss:
            reasons.append({
                "TradeID": tid, "Currency": currency, "TradeBase": trade_base, "TickerNorm": ticker,
                "DirectionNorm": direction, "MissingReasons": ";".join(miss)
            })

        rows.append({
            "TradeID": tid,
            "Currency": currency,
            "TradeBase": trade_base,
            "TickerNorm": ticker,
            "Direction": direction,
            "EntryDate": entry_date,
            "ExitDate_Original": exit_date,
            "EntryPrice": entry_px,
            "ExitPrice_Original": exit_px,
            "HasAllCoreFields": (len(miss) == 0),
            "MissingReasons": ";".join(miss) if miss else ""
        })

    trade_summary = pd.DataFrame(rows)
    missing_df = pd.DataFrame(reasons)

    coverage = pd.DataFrame([{
        "Raw_Unique_TradeIDs": int(df["TradeID"].nunique()),
        "Extracted_Unique_TradeIDs": int(trade_summary["TradeID"].nunique()),
        "Trades_With_All_Core_Fields": int(trade_summary["HasAllCoreFields"].sum()),
        "Trades_Missing_Something": int((~trade_summary["HasAllCoreFields"]).sum()),
        "Trades_Missing_M5": int(trade_summary["MissingReasons"].astype(str).str.contains("TICKER_NOT_IN_M5_LIST", na=False).sum()),
        "Trades_Unknown_Direction": int(trade_summary["MissingReasons"].astype(str).str.contains("UNKNOWN_DIRECTION", na=False).sum()),
        "Unique_M5_Tickers_Available": int(len(M5_TICKERS)),
        "Unique_M5_Tickers_Used": int(trade_summary["TickerNorm"].nunique())
    }])

    return trade_summary, missing_df, coverage

# ============================================================
# TRAILING LOGIC (CAPPED)
# ============================================================

@dataclass
class TrailResult:
    exit_time: pd.Timestamp
    exit_price: float
    exit_reason: str
    best_favorable: float
    max_high: float
    min_low: float

def direction_aware_improvement(direction: str, new_exit: float, old_exit: float) -> float:
    """
    Returns positive if trailing is better.
    LONG: new - old
    SHORT: old - new
    """
    d = normalize_direction(direction)
    if pd.isna(new_exit) or pd.isna(old_exit):
        return np.nan
    return float(new_exit - old_exit) if d == "LONG" else float(old_exit - new_exit)

def prepare_m5_with_indicators_market_only(ticker: str) -> tuple[pd.DataFrame | None, dict]:
    """
    Loads one ticker M5 file, filters market hours only, and computes:
      - ATR
      - slope (rolling)
      - slope_norm = slope / ATR

    Returns (df, stats_dict)
    """
    fp = M5_MAP.get(ticker)
    if not fp or not os.path.exists(fp):
        return None, {"ticker": ticker, "status": "missing_file"}

    df = pd.read_csv(fp)
    df.columns = [c.strip().lower() for c in df.columns]
    needed = ["date", "open", "high", "low", "close"]
    if not all(c in df.columns for c in needed):
        return None, {"ticker": ticker, "status": "bad_columns"}

    df["_dt"] = pd.to_datetime(df["date"], errors="coerce")
    df = df.dropna(subset=["_dt"]).sort_values("_dt").reset_index(drop=True)

    for c in ["open", "high", "low", "close"]:
        df[c] = pd.to_numeric(df[c], errors="coerce")
    df = df.dropna(subset=["open", "high", "low", "close"])

    total_rows = len(df)

    # Market hours only (remove pre/post market)
    df = filter_market_hours(df)
    kept_rows = len(df)

    if kept_rows == 0:
        return None, {"ticker": ticker, "status": "no_rows_in_market_hours", "total_rows": total_rows, "kept_rows": 0}

    # Indicators on market-only data
    df["ATR"] = compute_atr(df, ATR_WINDOW)

    if USE_TIME_AWARE_SLOPE:
        df["_tmin"] = (df["_dt"] - df["_dt"].iloc[0]).dt.total_seconds() / 60.0
        df["slope"] = df["close"].rolling(SLOPE_WINDOW, min_periods=SLOPE_WINDOW).apply(
            lambda s: rolling_slope(s, tmin=df.loc[s.index, "_tmin"], method=SLOPE_METHOD),
            raw=False
        )
    else:
        df["slope"] = df["close"].rolling(SLOPE_WINDOW, min_periods=SLOPE_WINDOW).apply(
            lambda s: rolling_slope(s, tmin=None, method=SLOPE_METHOD),
            raw=False
        )

    df["slope_norm"] = df["slope"] / df["ATR"]

    info = {
        "ticker": ticker,
        "status": "ok",
        "total_rows": total_rows,
        "kept_rows": kept_rows,
        "kept_pct": (kept_rows / total_rows) if total_rows else np.nan
    }
    return df, info

def simulate_trailing_capped(tr: pd.Series, m5: pd.DataFrame) -> TrailResult:
    """
    Simulates trailing stop from (EntryDate+1 day) to ExitDate_Original (inclusive day).
    If stop triggers: exit at stop price at that bar timestamp.
    Else: exit at original scheduled exit price.

    Stop logic:
      - Start with trailing distance = ATR_MULT * ATR
      - Track best favorable excursion:
          LONG  -> running max of high
          SHORT -> running min of low
      - Accelerate (tighten) when slope_norm > SLOPE_UPPER by reducing ATR_MULT
      - If slope_norm < SLOPE_LOWER, keep stop at baseline ATR_MULT
    """
    entry_date = pd.to_datetime(tr["EntryDate"])
    exit_date = pd.to_datetime(tr["ExitDate_Original"])
    entry_price = float(tr["EntryPrice"])
    orig_exit_price = float(tr["ExitPrice_Original"])

    direction = normalize_direction(tr["Direction"])
    is_long = (direction == "LONG")

    start_dt = (entry_date + timedelta(days=1)) if APPLY_FROM_NEXT_DAY else entry_date
    end_dt = exit_date + timedelta(days=1)  # include exit date's session

    window = m5[(m5["_dt"] >= start_dt) & (m5["_dt"] < end_dt)].copy()
    if len(window) == 0:
        return TrailResult(exit_date, orig_exit_price, "NoM5DataInMarketHours", entry_price, np.nan, np.nan)

    max_high = float(window["high"].max())
    min_low = float(window["low"].min())

    best_fav = entry_price
    stop = -np.inf if is_long else np.inf

    for _, row in window.iterrows():
        atr = row["ATR"]
        if pd.isna(atr) or atr <= 0:
            continue

        # Update favorable excursion
        if is_long:
            best_fav = max(best_fav, row["high"])
        else:
            best_fav = min(best_fav, row["low"])

        slope_norm = row["slope_norm"]
        mult = ATR_MULT

        # Acceleration / tightening logic
        if not pd.isna(slope_norm) and slope_norm > SLOPE_UPPER:
            mult = max(MIN_MULT, ATR_MULT - slope_norm * ACCEL_FACTOR)
        elif not pd.isna(slope_norm) and slope_norm < SLOPE_LOWER:
            mult = ATR_MULT

        # Compute / update stop and check hit
        if is_long:
            stop = max(stop, best_fav - mult * atr)
            if row["low"] <= stop:
                return TrailResult(row["_dt"], float(stop), "TrailingSL", float(best_fav), max_high, min_low)
        else:
            stop = min(stop, best_fav + mult * atr)
            if row["high"] >= stop:
                return TrailResult(row["_dt"], float(stop), "TrailingSL", float(best_fav), max_high, min_low)

    # If never triggered, exit at scheduled exit
    return TrailResult(exit_date, orig_exit_price, "OriginalExit", float(best_fav), max_high, min_low)

def summarize(out: pd.DataFrame) -> pd.DataFrame:
    """
    Summarizes:
      - trigger rate
      - improved vs worse vs unchanged
      - sum/avg/median improvement
    """
    df = out.copy()
    df["TriggeredFlag"] = df["ExitReason"].astype(str).eq("TrailingSL")
    df["ImprovedFlag"] = df["PriceImprovement"] > 0
    df["WorseFlag"] = df["PriceImprovement"] < 0
    df["UnchangedFlag"] = (df["PriceImprovement"] == 0) | df["PriceImprovement"].isna()

    def agg(g: pd.DataFrame) -> dict:
        n = len(g)
        trig = int(g["TriggeredFlag"].sum())
        return {
            "Trades": n,
            "TrailingTriggered": trig,
            "TrailingNotTriggered": int((~g["TriggeredFlag"]).sum()),
            "PctTriggered": trig / n if n else np.nan,
            "Improved": int(g["ImprovedFlag"].sum()),
            "Worse": int(g["WorseFlag"].sum()),
            "Unchanged": int(g["UnchangedFlag"].sum()),
            "SumPriceImprovement": float(g["PriceImprovement"].sum(skipna=True)),
            "AvgPriceImprovement": float(g["PriceImprovement"].mean(skipna=True)),
            "MedianPriceImprovement": float(g["PriceImprovement"].median(skipna=True)),
            "AvgPctImprovement": float(g["PctImprovement_vs_OriginalExit"].mean(skipna=True)),
            "MedianPctImprovement": float(g["PctImprovement_vs_OriginalExit"].median(skipna=True)),
        }

    rows = [{"Group": "ALL", **agg(df)}]
    for d, g in df.groupby(df["Direction"].astype(str).str.upper().str.strip()):
        rows.append({"Group": f"Direction={d}", **agg(g)})

    return pd.DataFrame(rows)

# ============================================================
# MAIN
# ============================================================

def main():
    print("Running: CAPPED ONLY + MARKET HOURS ONLY")
    print("Market session:", MARKET_START, "to", MARKET_END)
    print("Output:", OUT_DIR)

    raw = pd.read_excel(TRADE_XLSX_PATH)
    trade_summary, missing_df, coverage_df = build_trade_summary(raw)

    # Save audits / coverage
    trade_summary.to_csv(os.path.join(OUT_DIR, "trade_summary_extracted.csv"), index=False)
    missing_df.to_csv(os.path.join(OUT_DIR, "trade_summary_missing_reasons.csv"), index=False)
    coverage_df.to_csv(os.path.join(OUT_DIR, "coverage_report.csv"), index=False)

    print("\nCoverage:")
    print(coverage_df.to_string(index=False))

    # Trade selection
    if RUN_ALL_TRADES:
        sample = trade_summary.copy()
    else:
        sample = trade_summary.sample(n=min(N_SAMPLE_TRADES, len(trade_summary)), random_state=RANDOM_SEED).copy()

    # Use only fully valid trades
    sample = sample[sample["HasAllCoreFields"]].reset_index(drop=True)
    print("\nTrades to evaluate:", len(sample))

    # Speed: group by ticker -> load M5 once per ticker
    out_rows = []
    m5_stats = []
    total = len(sample)

    for tkr, grp in sample.groupby("TickerNorm"):
        if tkr not in M5_TICKERS:
            continue

        m5, info = prepare_m5_with_indicators_market_only(tkr)
        m5_stats.append(info)

        if m5 is None:
            continue

        grp = grp.sort_values("EntryDate")
        for _, tr in grp.iterrows():
            res = simulate_trailing_capped(tr, m5)

            old_exit = float(tr["ExitPrice_Original"])
            new_exit = float(res.exit_price)
            impr = direction_aware_improvement(tr["Direction"], new_exit, old_exit)

            orig_exit_date = pd.to_datetime(tr["ExitDate_Original"])
            new_exit_time = pd.to_datetime(res.exit_time)
            new_exit_date = new_exit_time.normalize() if pd.notna(new_exit_time) else pd.NaT

            out_rows.append({
                "TradeID": tr["TradeID"],
                "Currency": tr["Currency"],
                "TradeBase": tr["TradeBase"],
                "TickerNorm": tr["TickerNorm"],
                "Direction": tr["Direction"],

                "EntryDate": tr["EntryDate"],
                "EntryPrice": float(tr["EntryPrice"]),

                "ExitDate_Original": orig_exit_date,
                "ExitPrice_Original": old_exit,

                "ExitTime_Trailing": new_exit_time,
                "ExitDate_Trailing": new_exit_date,
                "ExitPrice_Trailing": new_exit,
                "ExitReason": res.exit_reason,

                "MaxHigh_InWindow": res.max_high,
                "MinLow_InWindow": res.min_low,
                "BestFavorable_InWindow": res.best_favorable,

                "PriceImprovement": impr,
                "PctImprovement_vs_OriginalExit": (impr / old_exit) if old_exit != 0 else np.nan,

                "ClosedEarlier": (new_exit_date < orig_exit_date) if (pd.notna(new_exit_date) and pd.notna(orig_exit_date)) else np.nan
            })

        print(f"Processed ticker {tkr} | trades: {len(grp)} | total done: {len(out_rows)}/{total}")

    out = pd.DataFrame(out_rows)
    summ = summarize(out)

    # Save outputs
    out_path = os.path.join(OUT_DIR, "trades_trailing_capped_market_only.csv")
    summ_path = os.path.join(OUT_DIR, "summary_trailing_capped_market_only.csv")
    m5_stats_path = os.path.join(OUT_DIR, "m5_market_hours_filter_stats.csv")

    out.to_csv(out_path, index=False)
    summ.to_csv(summ_path, index=False)
    pd.DataFrame(m5_stats).to_csv(m5_stats_path, index=False)

    print("\nSaved:")
    print(out_path)
    print(summ_path)
    print(m5_stats_path)

    print("\n=== SUMMARY ===")
    print(summ.to_string(index=False))

if __name__ == "__main__":
    main()


Running: CAPPED ONLY + MARKET HOURS ONLY
Market session: 14:30 to 21:00
Output: D:/work/Client/Maatra/Trade Level Data\TrailingSL_CAPPED_ONLY_MKT1430_2100_FIXEDDIR

Coverage:
 Raw_Unique_TradeIDs  Extracted_Unique_TradeIDs  Trades_With_All_Core_Fields  Trades_Missing_Something  Trades_Missing_M5  Trades_Unknown_Direction  Unique_M5_Tickers_Available  Unique_M5_Tickers_Used
               14002                      14002                        11578                      2424               2174                         0                          131                     160

Trades to evaluate: 11578
Processed ticker ACN | trades: 7 | total done: 7/11578
Processed ticker ADBE | trades: 83 | total done: 90/11578
Processed ticker ADI | trades: 273 | total done: 363/11578
Processed ticker ADP | trades: 124 | total done: 487/11578
Processed ticker ADSK | trades: 94 | total done: 581/11578
Processed ticker AG | trades: 11 | total done: 592/11578
Processed ticker AJG | trades: 230 | total done: 

In [3]:
import pandas as pd
import numpy as np

FILE = r"D:/work/Client/Maatra/Trade Level Data/TrailingSL_CAPPED_ONLY_MKT1430_2100_FIXEDDIR/trades_trailing_capped_market_only.csv"

df = pd.read_csv(FILE)

# keep valid percentage rows
df = df[df["PctImprovement_vs_OriginalExit"].notna()]

improved = df[df["PctImprovement_vs_OriginalExit"] > 0]
worse    = df[df["PctImprovement_vs_OriginalExit"] < 0]

summary = {
    "Total_Trades": len(df),

    "Improved_Trades": len(improved),
    "Worse_Trades": len(worse),

    "Pct_Improved": len(improved) / len(df),
    "Pct_Worse": len(worse) / len(df),

    # headline number
    "Avg_Pct_Impact_All_Trades": df["PctImprovement_vs_OriginalExit"].mean(),

    # payoff asymmetry
    "Avg_Pct_Gain_Improved_Trades": improved["PctImprovement_vs_OriginalExit"].mean(),
    "Avg_Pct_Loss_Worse_Trades": worse["PctImprovement_vs_OriginalExit"].mean(),

    # robustness check
    "Median_Pct_Impact_All_Trades": df["PctImprovement_vs_OriginalExit"].median(),

    "Payoff_Ratio_(AvgGain/AvgLoss)": (
        improved["PctImprovement_vs_OriginalExit"].mean()
        / abs(worse["PctImprovement_vs_OriginalExit"].mean())
        if len(worse) > 0 else np.nan
    )
}

pd.DataFrame([summary]).T


0
Total_Trades                    11578.000000
Improved_Trades                  5212.000000
Worse_Trades                     5386.000000
Pct_Improved                        0.450164
Pct_Worse                           0.465193
Avg_Pct_Impact_All_Trades           0.000850
Avg_Pct_Gain_Improved_Trades        0.012044
Avg_Pct_Loss_Worse_Trades          -0.009827
Median_Pct_Impact_All_Trades        0.000000
Payoff_Ratio_(AvgGain/AvgLoss)      1.225528

In [6]:
"""
Trailing Stop-Loss (CAPPED) — Market Hours Only — STEP 3 (Regime-Gated Trailing)

WHAT THIS VERSION DOES (vs your current baseline):
1) Uses ONLY regular market hours M5 bars (14:30–21:00).
2) CAPPED exit: trade can exit early ONLY if trailing stop hits; otherwise it exits at the original scheduled exit.
3) Regime-GATED trailing: trailing is enabled ONLY if the trade enters a "trend regime".
   - This is meant to improve the "improved vs worse" ratio by not trailing range/chop trades.

Trend regime definition (simple + defensible):
- Favorable move from entry >= REGIME_ATR_MULT * ATR_ref
- Directional persistence: mean slope_norm over last REGIME_SLOPE_BARS bars has correct sign (LONG>0, SHORT<0)

OUTPUTS:
- trades_trailing_capped_market_only_step3.csv  (trade-level results)
- summary_trailing_capped_market_only_step3.csv (aggregate stats, incl. how often trailing enabled)
- trade_summary_extracted.csv                   (one row per TradeID)
- trade_summary_missing_reasons.csv             (reasons for missing)
- coverage_report.csv                           (coverage stats)
- m5_market_hours_filter_stats.csv              (how many M5 rows kept after market-hours filter)
"""

import os
import numpy as np
import pandas as pd
from dataclasses import dataclass
from datetime import timedelta

# ============================================================
# CONFIG (EDIT PATHS)
# ============================================================

TRADE_XLSX_PATH      = r"D:/work/Client/Maatra/Trade Level Data/3 Month vol 14 data with sharpe prob Fnl.xlsx"
M5_DIR               = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data"
M5_FILE_LIST_PATH    = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data/m5_file_list.csv"
MAPPING_XLSX_PATH    = r"D:/work/Client/Maatra/Trade Level Data/Instrument Mapping.xlsx"

OUT_DIR = os.path.join(os.path.dirname(TRADE_XLSX_PATH), "TrailingSL_CAPPED_MKT1430_2100_STEP3_REGIME_GATED")
os.makedirs(OUT_DIR, exist_ok=True)

RUN_ALL_TRADES = True
N_SAMPLE_TRADES = 2000
RANDOM_SEED = 42

# ============================================================
# MARKET HOURS ONLY
# ============================================================
MARKET_START = "14:30"
MARKET_END   = "21:00"   # inclusive

# ============================================================
# TRAILING BASELINE PARAMETERS
# ============================================================
ATR_WINDOW = 14
ATR_MULT = 3.0

SLOPE_WINDOW = 12
SLOPE_METHOD = "regression"     # "regression" or "polyfit"
USE_TIME_AWARE_SLOPE = True

# IMPORTANT: This version does NOT rely on slope thresholds for tightening.
# It uses slope ONLY for regime detection (directional persistence).

APPLY_FROM_NEXT_DAY = True  # entry happens at EOD of EntryDate, so start trailing next day

# ============================================================
# STEP-3 (REGIME GATE) PARAMETERS  <-- TUNE THESE FIRST
# ============================================================
REGIME_ATR_MULT = 1.0        # require favorable move >= 1.0 * ATR_ref to enable trailing
REGIME_SLOPE_BARS = 6        # lookback for slope sign persistence (6 bars ~ 30 minutes)
REQUIRE_TREND = True         # if False, behaves closer to baseline (always trail)

# ============================================================
# Helpers
# ============================================================

def normalize_ticker(x: str) -> str:
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return ""
    x = str(x).strip().upper()
    return "".join([ch for ch in x if ch.isalnum()])

def trade_base_from_currency(currency: str) -> str:
    if currency is None or (isinstance(currency, float) and np.isnan(currency)):
        return ""
    s = str(currency).strip().upper()
    base = s.split("/")[0].strip() if "/" in s else s
    return normalize_ticker(base)

def normalize_direction(x) -> str:
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return "UNKNOWN"
    s = str(x).strip().upper()
    if s in ["LONG", "BUY", "B", "1", "1.0", "+1", "+1.0"]:
        return "LONG"
    if s in ["SHORT", "SELL", "S", "-1", "-1.0"]:
        return "SHORT"
    try:
        v = float(s)
        if v > 0: return "LONG"
        if v < 0: return "SHORT"
    except Exception:
        pass
    return "UNKNOWN"

def load_trade_to_m5_mapping(mapping_xlsx_path: str) -> dict:
    mp = pd.read_excel(mapping_xlsx_path)
    mp.columns = [c.strip() for c in mp.columns]
    if "org_symbol" not in mp.columns or "Symbol" not in mp.columns:
        raise ValueError("Mapping file must contain columns: org_symbol, Symbol")
    mp["m5_ticker"] = mp["org_symbol"].apply(normalize_ticker)
    mp["trade_base"] = mp["Symbol"].astype(str).str.upper().str.strip().str.split("/").str[0].apply(normalize_ticker)
    mp = mp[(mp["trade_base"] != "") & (mp["m5_ticker"] != "")]
    mp = mp.drop_duplicates(subset=["trade_base"], keep="first")
    return dict(zip(mp["trade_base"], mp["m5_ticker"]))

TRADE_TO_M5 = load_trade_to_m5_mapping(MAPPING_XLSX_PATH)

def map_trade_base_to_m5(trade_base: str) -> str:
    t = normalize_ticker(trade_base)
    return TRADE_TO_M5.get(t, t)

def load_m5_file_map(m5_dir: str, file_list_path: str) -> dict:
    fl = pd.read_csv(file_list_path)
    fl.columns = [c.strip().lower() for c in fl.columns]
    if "ticker" not in fl.columns or "filename" not in fl.columns:
        raise ValueError("m5_file_list.csv must have columns: ticker, filename")
    fl["ticker_norm"] = fl["ticker"].apply(normalize_ticker)
    fl["path"] = fl["filename"].apply(lambda f: os.path.join(m5_dir, f))
    return dict(zip(fl["ticker_norm"], fl["path"]))

M5_MAP = load_m5_file_map(M5_DIR, M5_FILE_LIST_PATH)
M5_TICKERS = set(M5_MAP.keys())

def filter_market_hours(df: pd.DataFrame) -> pd.DataFrame:
    if df.empty:
        return df
    dfi = df.set_index("_dt", drop=False).sort_index()
    dfi = dfi.between_time(MARKET_START, MARKET_END, inclusive="both")
    return dfi.reset_index(drop=True)

# ============================================================
# Indicators
# ============================================================

def compute_atr(df: pd.DataFrame, window: int) -> pd.Series:
    high = df["high"]
    low = df["low"]
    close = df["close"]
    tr = pd.concat([
        high - low,
        (high - close.shift(1)).abs(),
        (low - close.shift(1)).abs()
    ], axis=1).max(axis=1)
    return tr.rolling(window, min_periods=window).mean()

def rolling_slope(y: pd.Series, tmin: pd.Series | None, method: str) -> float:
    yy = y.values.astype(float)
    if len(yy) < 2 or np.all(np.isnan(yy)):
        return np.nan

    if tmin is None:
        xx = np.arange(len(yy), dtype=float)
    else:
        xx = tmin.values.astype(float)
        xx = xx - xx[0]

    mask = ~np.isnan(xx) & ~np.isnan(yy)
    xx = xx[mask]; yy = yy[mask]
    if len(yy) < 2:
        return np.nan

    if method == "polyfit":
        return np.polyfit(xx, yy, 1)[0]

    xm = xx.mean(); ym = yy.mean()
    denom = ((xx - xm) ** 2).sum()
    if denom == 0:
        return np.nan
    return (((xx - xm) * (yy - ym)).sum()) / denom

def prepare_m5_with_indicators_market_only(ticker: str) -> tuple[pd.DataFrame | None, dict]:
    fp = M5_MAP.get(ticker)
    if not fp or not os.path.exists(fp):
        return None, {"ticker": ticker, "status": "missing_file"}

    df = pd.read_csv(fp)
    df.columns = [c.strip().lower() for c in df.columns]
    needed = ["date", "open", "high", "low", "close"]
    if not all(c in df.columns for c in needed):
        return None, {"ticker": ticker, "status": "bad_columns"}

    df["_dt"] = pd.to_datetime(df["date"], errors="coerce")
    df = df.dropna(subset=["_dt"]).sort_values("_dt").reset_index(drop=True)

    for c in ["open", "high", "low", "close"]:
        df[c] = pd.to_numeric(df[c], errors="coerce")
    df = df.dropna(subset=["open", "high", "low", "close"])

    total_rows = len(df)

    df = filter_market_hours(df)
    kept_rows = len(df)
    if kept_rows == 0:
        return None, {"ticker": ticker, "status": "no_rows_in_market_hours", "total_rows": total_rows, "kept_rows": 0}

    df["ATR"] = compute_atr(df, ATR_WINDOW)

    if USE_TIME_AWARE_SLOPE:
        df["_tmin"] = (df["_dt"] - df["_dt"].iloc[0]).dt.total_seconds() / 60.0
        df["slope"] = df["close"].rolling(SLOPE_WINDOW, min_periods=SLOPE_WINDOW).apply(
            lambda s: rolling_slope(s, tmin=df.loc[s.index, "_tmin"], method=SLOPE_METHOD),
            raw=False
        )
    else:
        df["slope"] = df["close"].rolling(SLOPE_WINDOW, min_periods=SLOPE_WINDOW).apply(
            lambda s: rolling_slope(s, tmin=None, method=SLOPE_METHOD),
            raw=False
        )

    df["slope_norm"] = df["slope"] / df["ATR"]

    return df, {
        "ticker": ticker, "status": "ok",
        "total_rows": total_rows, "kept_rows": kept_rows,
        "kept_pct": (kept_rows / total_rows) if total_rows else np.nan
    }

# ============================================================
# Trade extraction (1 row per TradeID)
# ============================================================

def build_trade_summary(raw: pd.DataFrame):
    df = raw.copy()
    df.columns = [c.strip() for c in df.columns]

    required = ["TradeID", "Currency", "Direction", "date", "price", "Closing Date", "DayStatus"]
    missing = [c for c in required if c not in df.columns]
    if missing:
        raise ValueError(f"Trade file missing required columns: {missing}")

    df["date"] = pd.to_datetime(df["date"], errors="coerce")
    df["Closing Date"] = pd.to_datetime(df["Closing Date"], errors="coerce")
    df["price"] = pd.to_numeric(df["price"], errors="coerce")
    df["DayStatusU"] = df["DayStatus"].astype(str).str.upper().str.strip()

    df["TradeBase"] = df["Currency"].apply(trade_base_from_currency)
    df["TickerNorm"] = df["TradeBase"].apply(map_trade_base_to_m5)
    df["DirectionNorm"] = df["Direction"].apply(normalize_direction)

    rows, reasons = [], []

    for tid, g in df.groupby("TradeID", dropna=True):
        g = g.sort_values("date")

        currency = g["Currency"].dropna().iloc[0] if g["Currency"].notna().any() else np.nan
        direction = g["DirectionNorm"].dropna().iloc[0] if g["DirectionNorm"].notna().any() else "UNKNOWN"
        trade_base = g["TradeBase"].dropna().iloc[0] if g["TradeBase"].notna().any() else ""
        ticker = g["TickerNorm"].dropna().iloc[0] if g["TickerNorm"].notna().any() else ""

        open_mask = g["DayStatusU"].eq("OPEN")
        entry_date = g.loc[open_mask, "date"].dropna().min() if open_mask.any() else g["date"].dropna().min()
        exit_date = g["Closing Date"].dropna().max()

        # Entry price: last available 'price' on entry day in trade-level file (EOD entry)
        entry_px = np.nan
        if pd.notna(entry_date):
            day = entry_date.normalize()
            day_rows = g[g["date"].dt.normalize() == day]
            if day_rows["price"].notna().any():
                entry_px = float(day_rows["price"].dropna().iloc[-1])

        # Original exit price: last available 'price' on exit day in trade-level file
        exit_px = np.nan
        if pd.notna(exit_date):
            day = exit_date.normalize()
            day_rows = g[g["date"].dt.normalize() == day]
            if day_rows["price"].notna().any():
                exit_px = float(day_rows["price"].dropna().iloc[-1])

        miss = []
        if pd.isna(entry_date): miss.append("MISSING_ENTRY_DATE")
        if pd.isna(exit_date): miss.append("MISSING_EXIT_DATE")
        if pd.isna(entry_px): miss.append("MISSING_ENTRY_PRICE")
        if pd.isna(exit_px): miss.append("MISSING_EXIT_PRICE")
        if not ticker: miss.append("MISSING_TICKER")
        if ticker and (ticker not in M5_TICKERS): miss.append("TICKER_NOT_IN_M5_LIST")
        if direction == "UNKNOWN": miss.append("UNKNOWN_DIRECTION")

        if miss:
            reasons.append({
                "TradeID": tid, "Currency": currency,
                "TradeBase": trade_base, "TickerNorm": ticker,
                "Direction": direction, "MissingReasons": ";".join(miss)
            })

        rows.append({
            "TradeID": tid,
            "Currency": currency,
            "TradeBase": trade_base,
            "TickerNorm": ticker,
            "Direction": direction,
            "EntryDate": entry_date,
            "ExitDate_Original": exit_date,
            "EntryPrice": entry_px,
            "ExitPrice_Original": exit_px,
            "HasAllCoreFields": (len(miss) == 0),
            "MissingReasons": ";".join(miss) if miss else ""
        })

    trade_summary = pd.DataFrame(rows)
    missing_df = pd.DataFrame(reasons)
    coverage = pd.DataFrame([{
        "Raw_Unique_TradeIDs": int(df["TradeID"].nunique()),
        "Extracted_Unique_TradeIDs": int(trade_summary["TradeID"].nunique()),
        "Trades_With_All_Core_Fields": int(trade_summary["HasAllCoreFields"].sum()),
        "Trades_Missing_Something": int((~trade_summary["HasAllCoreFields"]).sum()),
        "Unique_M5_Tickers_Available": int(len(M5_TICKERS)),
        "Unique_M5_Tickers_Used": int(trade_summary["TickerNorm"].nunique()),
    }])
    return trade_summary, missing_df, coverage

# ============================================================
# Regime gate + trailing simulation (CAPPED)
# ============================================================

def direction_aware_improvement(direction: str, new_exit: float, old_exit: float) -> float:
    if pd.isna(new_exit) or pd.isna(old_exit):
        return np.nan
    d = normalize_direction(direction)
    return float(new_exit - old_exit) if d == "LONG" else float(old_exit - new_exit)

def in_trend_regime(is_long: bool,
                    entry_price: float,
                    best_fav: float,
                    atr_ref: float,
                    slope_norm_series: pd.Series) -> bool:
    """
    Returns True if trade is deemed to be in a trend regime.
    - needs a minimum favorable excursion
    - and directional persistence in slope_norm
    """
    if not REQUIRE_TREND:
        return True

    if pd.isna(atr_ref) or atr_ref <= 0:
        return False

    # favorable move condition
    if is_long:
        favorable = (best_fav - entry_price) >= REGIME_ATR_MULT * atr_ref
    else:
        favorable = (entry_price - best_fav) >= REGIME_ATR_MULT * atr_ref
    if not favorable:
        return False

    # slope persistence condition
    recent = slope_norm_series.dropna().tail(REGIME_SLOPE_BARS)
    if len(recent) < REGIME_SLOPE_BARS:
        return False

    return (recent.mean() > 0) if is_long else (recent.mean() < 0)

@dataclass
class TrailResult:
    exit_time: pd.Timestamp
    exit_price: float
    exit_reason: str
    best_favorable: float
    max_high: float
    min_low: float
    trailing_enabled: bool

def simulate_trailing_capped_step3(tr: pd.Series, m5: pd.DataFrame) -> TrailResult:
    """
    CAPPED: if stop never hits within [start_dt, exit_date], exit at original scheduled exit.
    """
    entry_date = pd.to_datetime(tr["EntryDate"])
    exit_date  = pd.to_datetime(tr["ExitDate_Original"])
    entry_price = float(tr["EntryPrice"])
    orig_exit_price = float(tr["ExitPrice_Original"])

    direction = normalize_direction(tr["Direction"])
    is_long = (direction == "LONG")

    start_dt = (entry_date + timedelta(days=1)) if APPLY_FROM_NEXT_DAY else entry_date
    end_dt   = exit_date + timedelta(days=1)

    window = m5[(m5["_dt"] >= start_dt) & (m5["_dt"] < end_dt)].copy()
    if len(window) == 0:
        return TrailResult(exit_date, orig_exit_price, "NoM5DataInMarketHours",
                           entry_price, np.nan, np.nan, False)

    max_high = float(window["high"].max())
    min_low = float(window["low"].min())

    best_fav = entry_price
    stop = -np.inf if is_long else np.inf

    atr_ref = np.nan
    trailing_enabled = False

    for i, row in window.iterrows():
        atr = row["ATR"]
        if pd.isna(atr) or atr <= 0:
            continue

        if pd.isna(atr_ref):
            atr_ref = atr

        # update favorable excursion
        if is_long:
            best_fav = max(best_fav, row["high"])
        else:
            best_fav = min(best_fav, row["low"])

        # gate: decide whether trailing is enabled
        if not trailing_enabled:
            trailing_enabled = in_trend_regime(
                is_long=is_long,
                entry_price=entry_price,
                best_fav=best_fav,
                atr_ref=atr_ref,
                slope_norm_series=window.loc[:i, "slope_norm"]
            )
            if not trailing_enabled:
                continue

            # initialize stop once enabled
            if is_long:
                stop = best_fav - ATR_MULT * atr
            else:
                stop = best_fav + ATR_MULT * atr

        # update stop + check hit (baseline trailing)
        if is_long:
            stop = max(stop, best_fav - ATR_MULT * atr)
            if row["low"] <= stop:
                return TrailResult(row["_dt"], float(stop), "TrailingSL",
                                   float(best_fav), max_high, min_low, True)
        else:
            stop = min(stop, best_fav + ATR_MULT * atr)
            if row["high"] >= stop:
                return TrailResult(row["_dt"], float(stop), "TrailingSL",
                                   float(best_fav), max_high, min_low, True)

    return TrailResult(exit_date, orig_exit_price, "OriginalExit",
                       float(best_fav), max_high, min_low, trailing_enabled)

# ============================================================
# Summary
# ============================================================

def summarize(out: pd.DataFrame) -> pd.DataFrame:
    df = out.copy()
    df["TriggeredFlag"] = df["ExitReason"].astype(str).eq("TrailingSL")
    df["EnabledFlag"] = df["TrailingEnabled"].astype(bool)

    df["ImprovedFlag"] = df["PriceImprovement"] > 0
    df["WorseFlag"] = df["PriceImprovement"] < 0
    df["UnchangedFlag"] = (df["PriceImprovement"] == 0) | df["PriceImprovement"].isna()

    def agg(g: pd.DataFrame) -> dict:
        n = len(g)
        enabled = int(g["EnabledFlag"].sum())
        trig = int(g["TriggeredFlag"].sum())
        return {
            "Trades": n,

            "TrailingEnabled": enabled,
            "PctEnabled": enabled / n if n else np.nan,

            "TrailingTriggered": trig,
            "TrailingNotTriggered": int((~g["TriggeredFlag"]).sum()),
            "PctTriggered": trig / n if n else np.nan,

            "Improved": int(g["ImprovedFlag"].sum()),
            "Worse": int(g["WorseFlag"].sum()),
            "Unchanged": int(g["UnchangedFlag"].sum()),

            "AvgPctImprovement": float(g["PctImprovement_vs_OriginalExit"].mean(skipna=True)),
            "MedianPctImprovement": float(g["PctImprovement_vs_OriginalExit"].median(skipna=True)),

            # Among TRIGGERED trades only (this is what you asked for)
            "Triggered_Trades": trig,
            "Triggered_Improved": int(g.loc[g["TriggeredFlag"], "ImprovedFlag"].sum()),
            "Triggered_Worse": int(g.loc[g["TriggeredFlag"], "WorseFlag"].sum()),
            "Triggered_Unchanged": int(g.loc[g["TriggeredFlag"], "UnchangedFlag"].sum()),
            "Triggered_PctImproved": (
                float(g.loc[g["TriggeredFlag"], "ImprovedFlag"].mean())
                if trig else np.nan
            ),
            "Triggered_AvgPctImprovement": (
                float(g.loc[g["TriggeredFlag"], "PctImprovement_vs_OriginalExit"].mean(skipna=True))
                if trig else np.nan
            ),
        }

    rows = [{"Group": "ALL", **agg(df)}]
    for d, g in df.groupby(df["Direction"].astype(str).str.upper().str.strip()):
        rows.append({"Group": f"Direction={d}", **agg(g)})

    return pd.DataFrame(rows)

# ============================================================
# MAIN
# ============================================================

def main():
    print("STEP-3 (Regime-gated trailing) | CAPPED | Market-hours only")
    print("Market hours:", MARKET_START, "to", MARKET_END)
    print("REGIME_ATR_MULT:", REGIME_ATR_MULT, "| REGIME_SLOPE_BARS:", REGIME_SLOPE_BARS, "| REQUIRE_TREND:", REQUIRE_TREND)
    print("Output folder:", OUT_DIR)

    raw = pd.read_excel(TRADE_XLSX_PATH)
    trade_summary, missing_df, coverage_df = build_trade_summary(raw)

    trade_summary.to_csv(os.path.join(OUT_DIR, "trade_summary_extracted.csv"), index=False)
    missing_df.to_csv(os.path.join(OUT_DIR, "trade_summary_missing_reasons.csv"), index=False)
    coverage_df.to_csv(os.path.join(OUT_DIR, "coverage_report.csv"), index=False)

    print("\nCoverage report:")
    print(coverage_df.to_string(index=False))

    if RUN_ALL_TRADES:
        sample = trade_summary.copy()
    else:
        sample = trade_summary.sample(n=min(N_SAMPLE_TRADES, len(trade_summary)),
                                      random_state=RANDOM_SEED).copy()

    sample = sample[sample["HasAllCoreFields"]].reset_index(drop=True)
    print("\nTrades to evaluate:", len(sample))

    out_rows = []
    m5_stats = []

    total = len(sample)

    for tkr, grp in sample.groupby("TickerNorm"):
        if tkr not in M5_TICKERS:
            continue

        m5, info = prepare_m5_with_indicators_market_only(tkr)
        m5_stats.append(info)
        if m5 is None:
            continue

        grp = grp.sort_values("EntryDate")
        for _, tr in grp.iterrows():
            res = simulate_trailing_capped_step3(tr, m5)

            old_exit = float(tr["ExitPrice_Original"])
            new_exit = float(res.exit_price)
            impr = direction_aware_improvement(tr["Direction"], new_exit, old_exit)

            out_rows.append({
                "TradeID": tr["TradeID"],
                "Currency": tr["Currency"],
                "TradeBase": tr["TradeBase"],
                "TickerNorm": tr["TickerNorm"],
                "Direction": tr["Direction"],

                "EntryDate": tr["EntryDate"],
                "EntryPrice": float(tr["EntryPrice"]),

                "ExitDate_Original": tr["ExitDate_Original"],
                "ExitPrice_Original": old_exit,

                "ExitTime_Trailing": res.exit_time,
                "ExitPrice_Trailing": new_exit,
                "ExitReason": res.exit_reason,

                "TrailingEnabled": bool(res.trailing_enabled),

                "MaxHigh_InWindow": res.max_high,
                "MinLow_InWindow": res.min_low,
                "BestFavorable_InWindow": res.best_favorable,

                "PriceImprovement": impr,
                "PctImprovement_vs_OriginalExit": (impr / old_exit) if old_exit != 0 else np.nan,
            })

        print(f"Processed ticker {tkr} | trades: {len(grp)} | total done: {len(out_rows)}/{total}")

    out = pd.DataFrame(out_rows)
    summ = summarize(out)

    out_path = os.path.join(OUT_DIR, "trades_trailing_capped_market_only_step3.csv")
    summ_path = os.path.join(OUT_DIR, "summary_trailing_capped_market_only_step3.csv")
    stats_path = os.path.join(OUT_DIR, "m5_market_hours_filter_stats.csv")

    out.to_csv(out_path, index=False)
    summ.to_csv(summ_path, index=False)
    pd.DataFrame(m5_stats).to_csv(stats_path, index=False)

    print("\nSaved:")
    print(out_path)
    print(summ_path)
    print(stats_path)

    print("\n=== SUMMARY (STEP-3) ===")
    print(summ.to_string(index=False))

if __name__ == "__main__":
    main()


STEP-3 (Regime-gated trailing) | CAPPED | Market-hours only
Market hours: 14:30 to 21:00
REGIME_ATR_MULT: 1.0 | REGIME_SLOPE_BARS: 6 | REQUIRE_TREND: True
Output folder: D:/work/Client/Maatra/Trade Level Data\TrailingSL_CAPPED_MKT1430_2100_STEP3_REGIME_GATED

Coverage report:
 Raw_Unique_TradeIDs  Extracted_Unique_TradeIDs  Trades_With_All_Core_Fields  Trades_Missing_Something  Unique_M5_Tickers_Available  Unique_M5_Tickers_Used
               14002                      14002                        11578                      2424                          131                     160

Trades to evaluate: 11578
Processed ticker ACN | trades: 7 | total done: 7/11578
Processed ticker ADBE | trades: 83 | total done: 90/11578
Processed ticker ADI | trades: 273 | total done: 363/11578
Processed ticker ADP | trades: 124 | total done: 487/11578
Processed ticker ADSK | trades: 94 | total done: 581/11578
Processed ticker AG | trades: 11 | total done: 592/11578
Processed ticker AJG | trades: 230 | 

In [7]:
import os
import numpy as np
import pandas as pd
from dataclasses import dataclass
from datetime import timedelta

# ============================================================
# PATHS (EDIT)
# ============================================================
TRADE_XLSX_PATH      = r"D:/work/Client/Maatra/Trade Level Data/3 Month vol 14 data with sharpe prob Fnl.xlsx"
M5_DIR               = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data"
M5_FILE_LIST_PATH    = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data/m5_file_list.csv"
MAPPING_XLSX_PATH    = r"D:/work/Client/Maatra/Trade Level Data/Instrument Mapping.xlsx"

OUT_DIR = os.path.join(os.path.dirname(TRADE_XLSX_PATH), "TrailingSL_CAPPED_MKT1430_2100_STEP4_DELAY_CHAN_CLOSE")
os.makedirs(OUT_DIR, exist_ok=True)

# ============================================================
# RUN MODE
# ============================================================
RUN_ALL_TRADES = True     # set False for quick tuning
N_SAMPLE_TRADES = 3000
RANDOM_SEED = 42

# ============================================================
# MARKET HOURS ONLY
# ============================================================
MARKET_START = "14:30"
MARKET_END   = "21:00"

# ============================================================
# ENTRY/EXIT RULES
# ============================================================
APPLY_FROM_NEXT_DAY = True   # entry is at EOD of EntryDate; start evaluation next day
CAPPED = True                # do NOT extend beyond scheduled exit date

# ============================================================
# INDICATORS
# ============================================================
ATR_WINDOW = 14

# ============================================================
# STEP-4 PARAMETERS (TUNE THESE)
# ============================================================
DELAY_MINUTES_AFTER_OPEN = 60     # 0 / 30 / 60 / 90 are sensible
ATR_MULT = 3.0                    # try 3.0, 3.5, 4.0
USE_HIGHEST_CLOSE = True          # chandelier based on CLOSE (recommended)
TRIGGER_ON_CLOSE = True           # exit on close cross (recommended)

# Optional quick sweep (set True if you want a leaderboard)
RUN_GRID = False

GRID = {
    "DELAY_MINUTES_AFTER_OPEN": [0, 30, 60, 90],
    "ATR_MULT": [2.5, 3.0, 3.5, 4.0],
}

# ============================================================
# Helpers
# ============================================================

def normalize_ticker(x: str) -> str:
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return ""
    x = str(x).strip().upper()
    return "".join([ch for ch in x if ch.isalnum()])

def trade_base_from_currency(currency: str) -> str:
    if currency is None or (isinstance(currency, float) and np.isnan(currency)):
        return ""
    s = str(currency).strip().upper()
    base = s.split("/")[0].strip() if "/" in s else s
    return normalize_ticker(base)

def normalize_direction(x) -> str:
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return "UNKNOWN"
    s = str(x).strip().upper()
    if s in ["LONG", "BUY", "B", "1", "1.0", "+1", "+1.0"]:
        return "LONG"
    if s in ["SHORT", "SELL", "S", "-1", "-1.0"]:
        return "SHORT"
    try:
        v = float(s)
        if v > 0: return "LONG"
        if v < 0: return "SHORT"
    except Exception:
        pass
    return "UNKNOWN"

def load_trade_to_m5_mapping(mapping_xlsx_path: str) -> dict:
    mp = pd.read_excel(mapping_xlsx_path)
    mp.columns = [c.strip() for c in mp.columns]
    if "org_symbol" not in mp.columns or "Symbol" not in mp.columns:
        raise ValueError("Mapping file must contain columns: org_symbol, Symbol")
    mp["m5_ticker"] = mp["org_symbol"].apply(normalize_ticker)
    mp["trade_base"] = mp["Symbol"].astype(str).str.upper().str.strip().str.split("/").str[0].apply(normalize_ticker)
    mp = mp[(mp["trade_base"] != "") & (mp["m5_ticker"] != "")]
    mp = mp.drop_duplicates(subset=["trade_base"], keep="first")
    return dict(zip(mp["trade_base"], mp["m5_ticker"]))

TRADE_TO_M5 = load_trade_to_m5_mapping(MAPPING_XLSX_PATH)

def map_trade_base_to_m5(trade_base: str) -> str:
    t = normalize_ticker(trade_base)
    return TRADE_TO_M5.get(t, t)

def load_m5_file_map(m5_dir: str, file_list_path: str) -> dict:
    fl = pd.read_csv(file_list_path)
    fl.columns = [c.strip().lower() for c in fl.columns]
    if "ticker" not in fl.columns or "filename" not in fl.columns:
        raise ValueError("m5_file_list.csv must have columns: ticker, filename")
    fl["ticker_norm"] = fl["ticker"].apply(normalize_ticker)
    fl["path"] = fl["filename"].apply(lambda f: os.path.join(m5_dir, f))
    return dict(zip(fl["ticker_norm"], fl["path"]))

M5_MAP = load_m5_file_map(M5_DIR, M5_FILE_LIST_PATH)
M5_TICKERS = set(M5_MAP.keys())

def filter_market_hours(df: pd.DataFrame) -> pd.DataFrame:
    if df.empty:
        return df
    dfi = df.set_index("_dt", drop=False).sort_index()
    dfi = dfi.between_time(MARKET_START, MARKET_END, inclusive="both")
    return dfi.reset_index(drop=True)

def compute_atr(df: pd.DataFrame, window: int) -> pd.Series:
    high = df["high"]
    low = df["low"]
    close = df["close"]
    tr = pd.concat([
        high - low,
        (high - close.shift(1)).abs(),
        (low - close.shift(1)).abs()
    ], axis=1).max(axis=1)
    return tr.rolling(window, min_periods=window).mean()

def prepare_m5_market_only(ticker: str):
    fp = M5_MAP.get(ticker)
    if not fp or not os.path.exists(fp):
        return None, {"ticker": ticker, "status": "missing_file"}
    df = pd.read_csv(fp)
    df.columns = [c.strip().lower() for c in df.columns]
    needed = ["date", "open", "high", "low", "close"]
    if not all(c in df.columns for c in needed):
        return None, {"ticker": ticker, "status": "bad_columns"}

    df["_dt"] = pd.to_datetime(df["date"], errors="coerce")
    df = df.dropna(subset=["_dt"]).sort_values("_dt").reset_index(drop=True)

    for c in ["open", "high", "low", "close"]:
        df[c] = pd.to_numeric(df[c], errors="coerce")
    df = df.dropna(subset=["open", "high", "low", "close"])

    total_rows = len(df)
    df = filter_market_hours(df)
    kept_rows = len(df)
    if kept_rows == 0:
        return None, {"ticker": ticker, "status": "no_rows_in_market_hours", "total_rows": total_rows, "kept_rows": 0}

    df["ATR"] = compute_atr(df, ATR_WINDOW)
    return df, {"ticker": ticker, "status": "ok", "total_rows": total_rows, "kept_rows": kept_rows}

def build_trade_summary(raw: pd.DataFrame):
    df = raw.copy()
    df.columns = [c.strip() for c in df.columns]

    required = ["TradeID", "Currency", "Direction", "date", "price", "Closing Date", "DayStatus"]
    missing = [c for c in required if c not in df.columns]
    if missing:
        raise ValueError(f"Trade file missing required columns: {missing}")

    df["date"] = pd.to_datetime(df["date"], errors="coerce")
    df["Closing Date"] = pd.to_datetime(df["Closing Date"], errors="coerce")
    df["price"] = pd.to_numeric(df["price"], errors="coerce")
    df["DayStatusU"] = df["DayStatus"].astype(str).str.upper().str.strip()

    df["TradeBase"] = df["Currency"].apply(trade_base_from_currency)
    df["TickerNorm"] = df["TradeBase"].apply(map_trade_base_to_m5)
    df["DirectionNorm"] = df["Direction"].apply(normalize_direction)

    rows, reasons = [], []

    for tid, g in df.groupby("TradeID", dropna=True):
        g = g.sort_values("date")
        currency = g["Currency"].dropna().iloc[0] if g["Currency"].notna().any() else np.nan
        direction = g["DirectionNorm"].dropna().iloc[0] if g["DirectionNorm"].notna().any() else "UNKNOWN"
        trade_base = g["TradeBase"].dropna().iloc[0] if g["TradeBase"].notna().any() else ""
        ticker = g["TickerNorm"].dropna().iloc[0] if g["TickerNorm"].notna().any() else ""

        open_mask = g["DayStatusU"].eq("OPEN")
        entry_date = g.loc[open_mask, "date"].dropna().min() if open_mask.any() else g["date"].dropna().min()
        exit_date = g["Closing Date"].dropna().max()

        entry_px = np.nan
        if pd.notna(entry_date):
            day = entry_date.normalize()
            day_rows = g[g["date"].dt.normalize() == day]
            if day_rows["price"].notna().any():
                entry_px = float(day_rows["price"].dropna().iloc[-1])

        exit_px = np.nan
        if pd.notna(exit_date):
            day = exit_date.normalize()
            day_rows = g[g["date"].dt.normalize() == day]
            if day_rows["price"].notna().any():
                exit_px = float(day_rows["price"].dropna().iloc[-1])

        miss = []
        if pd.isna(entry_date): miss.append("MISSING_ENTRY_DATE")
        if pd.isna(exit_date): miss.append("MISSING_EXIT_DATE")
        if pd.isna(entry_px): miss.append("MISSING_ENTRY_PRICE")
        if pd.isna(exit_px): miss.append("MISSING_EXIT_PRICE")
        if not ticker: miss.append("MISSING_TICKER")
        if ticker and (ticker not in M5_TICKERS): miss.append("TICKER_NOT_IN_M5_LIST")
        if direction == "UNKNOWN": miss.append("UNKNOWN_DIRECTION")

        if miss:
            reasons.append({"TradeID": tid, "TickerNorm": ticker, "MissingReasons": ";".join(miss)})

        rows.append({
            "TradeID": tid,
            "Currency": currency,
            "TradeBase": trade_base,
            "TickerNorm": ticker,
            "Direction": direction,
            "EntryDate": entry_date,
            "ExitDate_Original": exit_date,
            "EntryPrice": entry_px,
            "ExitPrice_Original": exit_px,
            "HasAllCoreFields": (len(miss) == 0),
            "MissingReasons": ";".join(miss) if miss else ""
        })

    trade_summary = pd.DataFrame(rows)
    missing_df = pd.DataFrame(reasons)
    coverage = pd.DataFrame([{
        "Raw_Unique_TradeIDs": int(df["TradeID"].nunique()),
        "Extracted_Unique_TradeIDs": int(trade_summary["TradeID"].nunique()),
        "Trades_With_All_Core_Fields": int(trade_summary["HasAllCoreFields"].sum()),
        "Trades_Missing_Something": int((~trade_summary["HasAllCoreFields"]).sum()),
    }])
    return trade_summary, missing_df, coverage

def direction_aware_improvement(direction: str, new_exit: float, old_exit: float) -> float:
    if pd.isna(new_exit) or pd.isna(old_exit):
        return np.nan
    d = normalize_direction(direction)
    return float(new_exit - old_exit) if d == "LONG" else float(old_exit - new_exit)

@dataclass
class TrailResult:
    exit_time: pd.Timestamp
    exit_price: float
    exit_reason: str
    enabled: bool

def apply_delay_filter(window: pd.DataFrame, delay_minutes: int) -> pd.DataFrame:
    if delay_minutes <= 0 or window.empty:
        return window
    # drop first N minutes from each trading day
    w = window.copy()
    w["d"] = w["_dt"].dt.normalize()
    # compute minutes from day start (market start)
    # we build a day-specific threshold timestamp
    thr = w["d"] + pd.to_timedelta(MARKET_START + ":00")
    w = w[w["_dt"] >= (thr + pd.to_timedelta(delay_minutes, unit="m"))]
    w = w.drop(columns=["d"])
    return w

def simulate_step4(tr: pd.Series, m5: pd.DataFrame, atr_mult: float, delay_minutes: int) -> TrailResult:
    entry_date = pd.to_datetime(tr["EntryDate"])
    exit_date  = pd.to_datetime(tr["ExitDate_Original"])
    entry_price = float(tr["EntryPrice"])
    orig_exit_price = float(tr["ExitPrice_Original"])

    direction = normalize_direction(tr["Direction"])
    is_long = (direction == "LONG")

    start_dt = (entry_date + timedelta(days=1)) if APPLY_FROM_NEXT_DAY else entry_date
    end_dt   = exit_date + timedelta(days=1)

    window = m5[(m5["_dt"] >= start_dt) & (m5["_dt"] < end_dt)].copy()
    if window.empty:
        return TrailResult(exit_date, orig_exit_price, "NoM5DataInMarketHours", False)

    window = apply_delay_filter(window, delay_minutes)
    if window.empty:
        return TrailResult(exit_date, orig_exit_price, "AllBarsFilteredByDelay", False)

    # chandelier tracking
    highest_close = entry_price
    lowest_close = entry_price
    enabled = True

    stop = -np.inf if is_long else np.inf

    for _, row in window.iterrows():
        atr = row["ATR"]
        if pd.isna(atr) or atr <= 0:
            continue

        c = float(row["close"])
        h = float(row["high"])
        l = float(row["low"])

        if is_long:
            if USE_HIGHEST_CLOSE:
                highest_close = max(highest_close, c)
                stop = max(stop, highest_close - atr_mult * atr)
                hit_val = c if TRIGGER_ON_CLOSE else l
                if hit_val <= stop:
                    return TrailResult(row["_dt"], float(stop), "TrailingSL", enabled)
            else:
                # fallback: wick-based highest high (less recommended)
                highest_close = max(highest_close, h)
                stop = max(stop, highest_close - atr_mult * atr)
                hit_val = c if TRIGGER_ON_CLOSE else l
                if hit_val <= stop:
                    return TrailResult(row["_dt"], float(stop), "TrailingSL", enabled)
        else:
            if USE_HIGHEST_CLOSE:
                lowest_close = min(lowest_close, c)
                stop = min(stop, lowest_close + atr_mult * atr)
                hit_val = c if TRIGGER_ON_CLOSE else h
                if hit_val >= stop:
                    return TrailResult(row["_dt"], float(stop), "TrailingSL", enabled)
            else:
                lowest_close = min(lowest_close, l)
                stop = min(stop, lowest_close + atr_mult * atr)
                hit_val = c if TRIGGER_ON_CLOSE else h
                if hit_val >= stop:
                    return TrailResult(row["_dt"], float(stop), "TrailingSL", enabled)

    return TrailResult(exit_date, orig_exit_price, "OriginalExit", enabled)

def summarize(out: pd.DataFrame) -> pd.DataFrame:
    df = out.copy()
    df["TriggeredFlag"] = df["ExitReason"].astype(str).eq("TrailingSL")
    df["ImprovedFlag"] = df["PriceImprovement"] > 0
    df["WorseFlag"] = df["PriceImprovement"] < 0
    df["UnchangedFlag"] = (df["PriceImprovement"] == 0) | df["PriceImprovement"].isna()

    def agg(g):
        n = len(g)
        trig = int(g["TriggeredFlag"].sum())
        return {
            "Trades": n,
            "TrailingTriggered": trig,
            "PctTriggered": trig / n if n else np.nan,
            "Improved": int(g["ImprovedFlag"].sum()),
            "Worse": int(g["WorseFlag"].sum()),
            "Unchanged": int(g["UnchangedFlag"].sum()),
            "AvgPctImprovement": float(g["PctImprovement_vs_OriginalExit"].mean(skipna=True)),
            "Triggered_PctImproved": float(g.loc[g["TriggeredFlag"], "ImprovedFlag"].mean()) if trig else np.nan,
            "Triggered_AvgPctImprovement": float(g.loc[g["TriggeredFlag"], "PctImprovement_vs_OriginalExit"].mean(skipna=True)) if trig else np.nan,
        }

    rows = [{"Group": "ALL", **agg(df)}]
    for d, g in df.groupby(df["Direction"].astype(str).str.upper().str.strip()):
        rows.append({"Group": f"Direction={d}", **agg(g)})

    return pd.DataFrame(rows)

def run_one_config(trades: pd.DataFrame, m5_cache: dict, atr_mult: float, delay_min: int, tag: str):
    out_rows = []
    for tkr, grp in trades.groupby("TickerNorm"):
        m5 = m5_cache.get(tkr)
        if m5 is None:
            continue
        for _, tr in grp.iterrows():
            res = simulate_step4(tr, m5, atr_mult=atr_mult, delay_minutes=delay_min)
            old_exit = float(tr["ExitPrice_Original"])
            new_exit = float(res.exit_price)
            impr = direction_aware_improvement(tr["Direction"], new_exit, old_exit)
            out_rows.append({
                "TradeID": tr["TradeID"],
                "TickerNorm": tr["TickerNorm"],
                "Direction": tr["Direction"],
                "EntryDate": tr["EntryDate"],
                "EntryPrice": float(tr["EntryPrice"]),
                "ExitDate_Original": tr["ExitDate_Original"],
                "ExitPrice_Original": old_exit,
                "ExitTime_Trailing": res.exit_time,
                "ExitPrice_Trailing": new_exit,
                "ExitReason": res.exit_reason,
                "PriceImprovement": impr,
                "PctImprovement_vs_OriginalExit": (impr / old_exit) if old_exit != 0 else np.nan,
                "ConfigTag": tag,
                "ATR_MULT": atr_mult,
                "DELAY_MIN": delay_min,
            })
    out = pd.DataFrame(out_rows)
    summ = summarize(out)
    return out, summ

def main():
    print("STEP-4: Delay-after-open + Chandelier(Close) + Close-trigger | CAPPED | market-hours only")
    print("Output:", OUT_DIR)

    raw = pd.read_excel(TRADE_XLSX_PATH)
    trade_summary, missing_df, coverage_df = build_trade_summary(raw)

    trade_summary.to_csv(os.path.join(OUT_DIR, "trade_summary_extracted.csv"), index=False)
    missing_df.to_csv(os.path.join(OUT_DIR, "trade_summary_missing_reasons.csv"), index=False)
    coverage_df.to_csv(os.path.join(OUT_DIR, "coverage_report.csv"), index=False)

    # choose trades
    if RUN_ALL_TRADES:
        sample = trade_summary.copy()
    else:
        sample = trade_summary.sample(n=min(N_SAMPLE_TRADES, len(trade_summary)), random_state=RANDOM_SEED).copy()

    sample = sample[sample["HasAllCoreFields"]].reset_index(drop=True)
    print("Trades to evaluate:", len(sample))

    # cache M5 per ticker (market-hours + ATR computed)
    m5_cache = {}
    m5_stats = []
    for tkr in sorted(sample["TickerNorm"].unique()):
        if tkr not in M5_TICKERS:
            m5_cache[tkr] = None
            continue
        m5, info = prepare_m5_market_only(tkr)
        m5_cache[tkr] = m5
        m5_stats.append(info)

    pd.DataFrame(m5_stats).to_csv(os.path.join(OUT_DIR, "m5_market_hours_filter_stats.csv"), index=False)

    if not RUN_GRID:
        tag = f"delay{DELAY_MINUTES_AFTER_OPEN}_atr{ATR_MULT}"
        out, summ = run_one_config(sample, m5_cache, ATR_MULT, DELAY_MINUTES_AFTER_OPEN, tag)

        out_path = os.path.join(OUT_DIR, "trades_trailing_capped_market_only_step4.csv")
        summ_path = os.path.join(OUT_DIR, "summary_trailing_capped_market_only_step4.csv")
        out.to_csv(out_path, index=False)
        summ.to_csv(summ_path, index=False)

        print("\nSaved:")
        print(out_path)
        print(summ_path)
        print("\n=== SUMMARY (STEP-4) ===")
        print(summ.to_string(index=False))

    else:
        leaderboard = []
        for dmin in GRID["DELAY_MINUTES_AFTER_OPEN"]:
            for am in GRID["ATR_MULT"]:
                tag = f"delay{dmin}_atr{am}"
                out, summ = run_one_config(sample, m5_cache, am, dmin, tag)

                # take ALL row
                row = summ[summ["Group"] == "ALL"].iloc[0].to_dict()
                row["ConfigTag"] = tag
                leaderboard.append(row)

                # save summary per config (optional)
                summ.to_csv(os.path.join(OUT_DIR, f"summary_{tag}.csv"), index=False)

                print(f"Done {tag} | Triggered_PctImproved={row.get('Triggered_PctImproved'):.4f} | AvgPct={row.get('AvgPctImprovement'):.6f}")

        lb = pd.DataFrame(leaderboard)
        # rank by triggered improved first, then avg pct improvement
        lb = lb.sort_values(["Triggered_PctImproved", "AvgPctImprovement"], ascending=[False, False])
        lb_path = os.path.join(OUT_DIR, "leaderboard_step4.csv")
        lb.to_csv(lb_path, index=False)

        print("\nSaved leaderboard:")
        print(lb_path)
        print("\nTop 10 configs:")
        print(lb.head(10).to_string(index=False))

if __name__ == "__main__":
    main()


STEP-4: Delay-after-open + Chandelier(Close) + Close-trigger | CAPPED | market-hours only
Output: D:/work/Client/Maatra/Trade Level Data\TrailingSL_CAPPED_MKT1430_2100_STEP4_DELAY_CHAN_CLOSE
Trades to evaluate: 11578

Saved:
D:/work/Client/Maatra/Trade Level Data\TrailingSL_CAPPED_MKT1430_2100_STEP4_DELAY_CHAN_CLOSE\trades_trailing_capped_market_only_step4.csv
D:/work/Client/Maatra/Trade Level Data\TrailingSL_CAPPED_MKT1430_2100_STEP4_DELAY_CHAN_CLOSE\summary_trailing_capped_market_only_step4.csv

=== SUMMARY (STEP-4) ===
          Group  Trades  TrailingTriggered  PctTriggered  Improved  Worse  Unchanged  AvgPctImprovement  Triggered_PctImproved  Triggered_AvgPctImprovement
            ALL   11578              10396      0.897910      5238   5158       1182           0.001026               0.503848                     0.001142
 Direction=LONG   10922               9822      0.899286      4931   4891       1100           0.001104               0.502036                     0.001227
Dire

In [8]:
"""
STEP-5: CAPPED trailing stop (market-hours only)
- Uses M5 data filtered to 14:30–21:00
- Applies a delay after open (to avoid open-noise)
- Resamples to 30-minute bars (reduces micro noise)
- Chandelier stop based on Highest CLOSE / Lowest CLOSE
- Exit triggers only after N consecutive CLOSE confirmations
- CAPPED: if no stop hit, exit at original scheduled exit date price

Outputs:
- trades_trailing_capped_market_only_step5.csv
- summary_trailing_capped_market_only_step5.csv
- coverage_report.csv
- trade_summary_missing_reasons.csv
"""

import os
import numpy as np
import pandas as pd
from dataclasses import dataclass
from datetime import timedelta

# ============================================================
# PATHS (EDIT)
# ============================================================
TRADE_XLSX_PATH      = r"D:/work/Client/Maatra/Trade Level Data/3 Month vol 14 data with sharpe prob Fnl.xlsx"
M5_DIR               = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data"
M5_FILE_LIST_PATH    = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data/m5_file_list.csv"
MAPPING_XLSX_PATH    = r"D:/work/Client/Maatra/Trade Level Data/Instrument Mapping.xlsx"

OUT_DIR = os.path.join(os.path.dirname(TRADE_XLSX_PATH), "TrailingSL_CAPPED_MKT1430_2100_STEP5_30MIN_CONFIRM")
os.makedirs(OUT_DIR, exist_ok=True)

RUN_ALL_TRADES = True
N_SAMPLE_TRADES = 3000
RANDOM_SEED = 42

# ============================================================
# MARKET HOURS ONLY (IST times in your data)
# ============================================================
MARKET_START = "14:30"
MARKET_END   = "21:00"   # inclusive

# ============================================================
# INDICATORS
# ============================================================
ATR_WINDOW = 14

# ============================================================
# STEP-5 PARAMETERS (TUNE THESE)
# ============================================================
DELAY_MINUTES_AFTER_OPEN = 60     # try 60 / 90
RESAMPLE_RULE = "30T"             # 30-minute bars; try "15T" if too slow to react
ATR_MULT = 3.0                    # try 3.0 / 3.5 / 4.0
CONFIRM_BARS = 2                  # require 2 consecutive closes beyond stop (try 2 or 3)

APPLY_FROM_NEXT_DAY = True        # entry is at EOD; start next day
USE_HIGHEST_CLOSE = True          # chandelier on close (recommended)

# ============================================================
# Helpers
# ============================================================

def normalize_ticker(x: str) -> str:
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return ""
    x = str(x).strip().upper()
    return "".join([ch for ch in x if ch.isalnum()])

def trade_base_from_currency(currency: str) -> str:
    if currency is None or (isinstance(currency, float) and np.isnan(currency)):
        return ""
    s = str(currency).strip().upper()
    base = s.split("/")[0].strip() if "/" in s else s
    return normalize_ticker(base)

def normalize_direction(x) -> str:
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return "UNKNOWN"
    s = str(x).strip().upper()
    if s in ["LONG", "BUY", "B", "1", "1.0", "+1", "+1.0"]:
        return "LONG"
    if s in ["SHORT", "SELL", "S", "-1", "-1.0"]:
        return "SHORT"
    try:
        v = float(s)
        if v > 0: return "LONG"
        if v < 0: return "SHORT"
    except Exception:
        pass
    return "UNKNOWN"

def load_trade_to_m5_mapping(mapping_xlsx_path: str) -> dict:
    mp = pd.read_excel(mapping_xlsx_path)
    mp.columns = [c.strip() for c in mp.columns]
    if "org_symbol" not in mp.columns or "Symbol" not in mp.columns:
        raise ValueError("Mapping file must contain columns: org_symbol, Symbol")
    mp["m5_ticker"] = mp["org_symbol"].apply(normalize_ticker)
    mp["trade_base"] = mp["Symbol"].astype(str).str.upper().str.strip().str.split("/").str[0].apply(normalize_ticker)
    mp = mp[(mp["trade_base"] != "") & (mp["m5_ticker"] != "")]
    mp = mp.drop_duplicates(subset=["trade_base"], keep="first")
    return dict(zip(mp["trade_base"], mp["m5_ticker"]))

TRADE_TO_M5 = load_trade_to_m5_mapping(MAPPING_XLSX_PATH)

def map_trade_base_to_m5(trade_base: str) -> str:
    t = normalize_ticker(trade_base)
    return TRADE_TO_M5.get(t, t)

def load_m5_file_map(m5_dir: str, file_list_path: str) -> dict:
    fl = pd.read_csv(file_list_path)
    fl.columns = [c.strip().lower() for c in fl.columns]
    if "ticker" not in fl.columns or "filename" not in fl.columns:
        raise ValueError("m5_file_list.csv must have columns: ticker, filename")
    fl["ticker_norm"] = fl["ticker"].apply(normalize_ticker)
    fl["path"] = fl["filename"].apply(lambda f: os.path.join(m5_dir, f))
    return dict(zip(fl["ticker_norm"], fl["path"]))

M5_MAP = load_m5_file_map(M5_DIR, M5_FILE_LIST_PATH)
M5_TICKERS = set(M5_MAP.keys())

def filter_market_hours(df: pd.DataFrame) -> pd.DataFrame:
    if df.empty:
        return df
    dfi = df.set_index("_dt", drop=False).sort_index()
    dfi = dfi.between_time(MARKET_START, MARKET_END, inclusive="both")
    return dfi.reset_index(drop=True)

def apply_delay_filter(window: pd.DataFrame, delay_minutes: int) -> pd.DataFrame:
    if delay_minutes <= 0 or window.empty:
        return window
    w = window.copy()
    w["d"] = w["_dt"].dt.normalize()
    thr = w["d"] + pd.to_timedelta(MARKET_START + ":00")
    w = w[w["_dt"] >= (thr + pd.to_timedelta(delay_minutes, unit="m"))]
    return w.drop(columns=["d"])

def compute_atr(df: pd.DataFrame, window: int) -> pd.Series:
    high = df["high"]
    low = df["low"]
    close = df["close"]
    tr = pd.concat([
        high - low,
        (high - close.shift(1)).abs(),
        (low - close.shift(1)).abs()
    ], axis=1).max(axis=1)
    return tr.rolling(window, min_periods=window).mean()

def resample_ohlc(df: pd.DataFrame, rule: str) -> pd.DataFrame:
    """
    Resample intraday bars to larger timeframe (e.g., 30T).
    Keeps OHLC; last close.
    """
    if df.empty:
        return df
    dfi = df.set_index("_dt").sort_index()
    ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
        "open": "first",
        "high": "max",
        "low": "min",
        "close": "last",
    }).dropna()
    ohlc = ohlc.reset_index()
    return ohlc

def prepare_m5_market_only(ticker: str):
    fp = M5_MAP.get(ticker)
    if not fp or not os.path.exists(fp):
        return None, {"ticker": ticker, "status": "missing_file"}

    df = pd.read_csv(fp)
    df.columns = [c.strip().lower() for c in df.columns]
    needed = ["date", "open", "high", "low", "close"]
    if not all(c in df.columns for c in needed):
        return None, {"ticker": ticker, "status": "bad_columns"}

    df["_dt"] = pd.to_datetime(df["date"], errors="coerce")
    df = df.dropna(subset=["_dt"]).sort_values("_dt").reset_index(drop=True)

    for c in ["open", "high", "low", "close"]:
        df[c] = pd.to_numeric(df[c], errors="coerce")
    df = df.dropna(subset=["open", "high", "low", "close"])

    total_rows = len(df)
    df = filter_market_hours(df)
    kept_rows = len(df)
    if kept_rows == 0:
        return None, {"ticker": ticker, "status": "no_rows_in_market_hours", "total_rows": total_rows, "kept_rows": 0}

    return df, {"ticker": ticker, "status": "ok", "total_rows": total_rows, "kept_rows": kept_rows}

def build_trade_summary(raw: pd.DataFrame):
    df = raw.copy()
    df.columns = [c.strip() for c in df.columns]

    required = ["TradeID", "Currency", "Direction", "date", "price", "Closing Date", "DayStatus"]
    missing = [c for c in required if c not in df.columns]
    if missing:
        raise ValueError(f"Trade file missing required columns: {missing}")

    df["date"] = pd.to_datetime(df["date"], errors="coerce")
    df["Closing Date"] = pd.to_datetime(df["Closing Date"], errors="coerce")
    df["price"] = pd.to_numeric(df["price"], errors="coerce")
    df["DayStatusU"] = df["DayStatus"].astype(str).str.upper().str.strip()

    df["TradeBase"] = df["Currency"].apply(trade_base_from_currency)
    df["TickerNorm"] = df["TradeBase"].apply(map_trade_base_to_m5)
    df["DirectionNorm"] = df["Direction"].apply(normalize_direction)

    rows, reasons = [], []

    for tid, g in df.groupby("TradeID", dropna=True):
        g = g.sort_values("date")
        currency = g["Currency"].dropna().iloc[0] if g["Currency"].notna().any() else np.nan
        direction = g["DirectionNorm"].dropna().iloc[0] if g["DirectionNorm"].notna().any() else "UNKNOWN"
        trade_base = g["TradeBase"].dropna().iloc[0] if g["TradeBase"].notna().any() else ""
        ticker = g["TickerNorm"].dropna().iloc[0] if g["TickerNorm"].notna().any() else ""

        open_mask = g["DayStatusU"].eq("OPEN")
        entry_date = g.loc[open_mask, "date"].dropna().min() if open_mask.any() else g["date"].dropna().min()
        exit_date = g["Closing Date"].dropna().max()

        entry_px = np.nan
        if pd.notna(entry_date):
            day = entry_date.normalize()
            day_rows = g[g["date"].dt.normalize() == day]
            if day_rows["price"].notna().any():
                entry_px = float(day_rows["price"].dropna().iloc[-1])

        exit_px = np.nan
        if pd.notna(exit_date):
            day = exit_date.normalize()
            day_rows = g[g["date"].dt.normalize() == day]
            if day_rows["price"].notna().any():
                exit_px = float(day_rows["price"].dropna().iloc[-1])

        miss = []
        if pd.isna(entry_date): miss.append("MISSING_ENTRY_DATE")
        if pd.isna(exit_date): miss.append("MISSING_EXIT_DATE")
        if pd.isna(entry_px): miss.append("MISSING_ENTRY_PRICE")
        if pd.isna(exit_px): miss.append("MISSING_EXIT_PRICE")
        if not ticker: miss.append("MISSING_TICKER")
        if ticker and (ticker not in M5_TICKERS): miss.append("TICKER_NOT_IN_M5_LIST")
        if direction == "UNKNOWN": miss.append("UNKNOWN_DIRECTION")

        if miss:
            reasons.append({"TradeID": tid, "TickerNorm": ticker, "MissingReasons": ";".join(miss)})

        rows.append({
            "TradeID": tid,
            "Currency": currency,
            "TradeBase": trade_base,
            "TickerNorm": ticker,
            "Direction": direction,
            "EntryDate": entry_date,
            "ExitDate_Original": exit_date,
            "EntryPrice": entry_px,
            "ExitPrice_Original": exit_px,
            "HasAllCoreFields": (len(miss) == 0),
            "MissingReasons": ";".join(miss) if miss else ""
        })

    trade_summary = pd.DataFrame(rows)
    missing_df = pd.DataFrame(reasons)
    coverage = pd.DataFrame([{
        "Raw_Unique_TradeIDs": int(df["TradeID"].nunique()),
        "Extracted_Unique_TradeIDs": int(trade_summary["TradeID"].nunique()),
        "Trades_With_All_Core_Fields": int(trade_summary["HasAllCoreFields"].sum()),
        "Trades_Missing_Something": int((~trade_summary["HasAllCoreFields"]).sum()),
    }])
    return trade_summary, missing_df, coverage

def direction_aware_improvement(direction: str, new_exit: float, old_exit: float) -> float:
    if pd.isna(new_exit) or pd.isna(old_exit):
        return np.nan
    d = normalize_direction(direction)
    return float(new_exit - old_exit) if d == "LONG" else float(old_exit - new_exit)

@dataclass
class TrailResult:
    exit_time: pd.Timestamp
    exit_price: float
    exit_reason: str

def simulate_step5(tr: pd.Series, m5_raw: pd.DataFrame) -> TrailResult:
    entry_date = pd.to_datetime(tr["EntryDate"])
    exit_date  = pd.to_datetime(tr["ExitDate_Original"])
    entry_price = float(tr["EntryPrice"])
    orig_exit_price = float(tr["ExitPrice_Original"])

    direction = normalize_direction(tr["Direction"])
    is_long = (direction == "LONG")

    start_dt = (entry_date + timedelta(days=1)) if APPLY_FROM_NEXT_DAY else entry_date
    end_dt   = exit_date + timedelta(days=1)

    window = m5_raw[(m5_raw["_dt"] >= start_dt) & (m5_raw["_dt"] < end_dt)].copy()
    if window.empty:
        return TrailResult(exit_date, orig_exit_price, "NoM5DataInMarketHours")

    window = apply_delay_filter(window, DELAY_MINUTES_AFTER_OPEN)
    if window.empty:
        return TrailResult(exit_date, orig_exit_price, "AllBarsFilteredByDelay")

    # resample to 30-min OHLC
    window_30 = resample_ohlc(window, RESAMPLE_RULE)
    if window_30.empty:
        return TrailResult(exit_date, orig_exit_price, "NoBarsAfterResample")

    # compute ATR on resampled bars
    window_30["ATR"] = compute_atr(window_30, ATR_WINDOW)

    # chandelier(close) + confirmation
    if is_long:
        extreme = entry_price  # highest close so far
        stop = -np.inf
        confirm = 0
        for _, row in window_30.iterrows():
            atr = row["ATR"]
            if pd.isna(atr) or atr <= 0:
                continue
            c = float(row["close"])
            extreme = max(extreme, c) if USE_HIGHEST_CLOSE else max(extreme, float(row["high"]))
            stop = max(stop, extreme - ATR_MULT * atr)

            if c <= stop:
                confirm += 1
            else:
                confirm = 0

            if confirm >= CONFIRM_BARS:
                return TrailResult(pd.to_datetime(row["_dt"]), float(stop), "TrailingSL")
    else:
        extreme = entry_price  # lowest close so far
        stop = np.inf
        confirm = 0
        for _, row in window_30.iterrows():
            atr = row["ATR"]
            if pd.isna(atr) or atr <= 0:
                continue
            c = float(row["close"])
            extreme = min(extreme, c) if USE_HIGHEST_CLOSE else min(extreme, float(row["low"]))
            stop = min(stop, extreme + ATR_MULT * atr)

            if c >= stop:
                confirm += 1
            else:
                confirm = 0

            if confirm >= CONFIRM_BARS:
                return TrailResult(pd.to_datetime(row["_dt"]), float(stop), "TrailingSL")

    return TrailResult(exit_date, orig_exit_price, "OriginalExit")

def summarize(out: pd.DataFrame) -> pd.DataFrame:
    df = out.copy()
    df["TriggeredFlag"] = df["ExitReason"].astype(str).eq("TrailingSL")
    df["ImprovedFlag"] = df["PriceImprovement"] > 0
    df["WorseFlag"] = df["PriceImprovement"] < 0
    df["UnchangedFlag"] = (df["PriceImprovement"] == 0) | df["PriceImprovement"].isna()

    def agg(g):
        n = len(g)
        trig = int(g["TriggeredFlag"].sum())
        return {
            "Trades": n,
            "TrailingTriggered": trig,
            "PctTriggered": trig / n if n else np.nan,
            "Improved": int(g["ImprovedFlag"].sum()),
            "Worse": int(g["WorseFlag"].sum()),
            "Unchanged": int(g["UnchangedFlag"].sum()),
            "AvgPctImprovement": float(g["PctImprovement_vs_OriginalExit"].mean(skipna=True)),
            "MedianPctImprovement": float(g["PctImprovement_vs_OriginalExit"].median(skipna=True)),
            "Triggered_PctImproved": float(g.loc[g["TriggeredFlag"], "ImprovedFlag"].mean()) if trig else np.nan,
            "Triggered_AvgPctImprovement": float(g.loc[g["TriggeredFlag"], "PctImprovement_vs_OriginalExit"].mean(skipna=True)) if trig else np.nan,
        }

    rows = [{"Group": "ALL", **agg(df)}]
    for d, g in df.groupby(df["Direction"].astype(str).str.upper().str.strip()):
        rows.append({"Group": f"Direction={d}", **agg(g)})
    return pd.DataFrame(rows)

def main():
    print("STEP-5 | 30-min resample + confirm closes | CAPPED | market-hours only")
    print("DELAY:", DELAY_MINUTES_AFTER_OPEN, "| RESAMPLE:", RESAMPLE_RULE, "| ATR_MULT:", ATR_MULT, "| CONFIRM_BARS:", CONFIRM_BARS)
    print("Output:", OUT_DIR)

    raw = pd.read_excel(TRADE_XLSX_PATH)
    trade_summary, missing_df, coverage_df = build_trade_summary(raw)

    coverage_df.to_csv(os.path.join(OUT_DIR, "coverage_report.csv"), index=False)
    missing_df.to_csv(os.path.join(OUT_DIR, "trade_summary_missing_reasons.csv"), index=False)

    if RUN_ALL_TRADES:
        sample = trade_summary.copy()
    else:
        sample = trade_summary.sample(n=min(N_SAMPLE_TRADES, len(trade_summary)), random_state=RANDOM_SEED).copy()

    sample = sample[sample["HasAllCoreFields"]].reset_index(drop=True)
    print("Trades to evaluate:", len(sample))

    # Load M5 once per ticker
    m5_cache = {}
    for tkr in sorted(sample["TickerNorm"].unique()):
        if tkr not in M5_TICKERS:
            m5_cache[tkr] = None
            continue
        m5, _ = prepare_m5_market_only(tkr)
        m5_cache[tkr] = m5

    out_rows = []
    for tkr, grp in sample.groupby("TickerNorm"):
        m5 = m5_cache.get(tkr)
        if m5 is None:
            continue

        for _, tr in grp.iterrows():
            res = simulate_step5(tr, m5)
            old_exit = float(tr["ExitPrice_Original"])
            new_exit = float(res.exit_price)
            impr = direction_aware_improvement(tr["Direction"], new_exit, old_exit)

            out_rows.append({
                "TradeID": tr["TradeID"],
                "TickerNorm": tr["TickerNorm"],
                "Direction": tr["Direction"],
                "EntryDate": tr["EntryDate"],
                "EntryPrice": float(tr["EntryPrice"]),
                "ExitDate_Original": tr["ExitDate_Original"],
                "ExitPrice_Original": old_exit,
                "ExitTime_Trailing": res.exit_time,
                "ExitPrice_Trailing": new_exit,
                "ExitReason": res.exit_reason,
                "PriceImprovement": impr,
                "PctImprovement_vs_OriginalExit": (impr / old_exit) if old_exit != 0 else np.nan,
                "DELAY_MIN": DELAY_MINUTES_AFTER_OPEN,
                "RESAMPLE_RULE": RESAMPLE_RULE,
                "ATR_MULT": ATR_MULT,
                "CONFIRM_BARS": CONFIRM_BARS,
            })

        print(f"Processed {tkr} | trades: {len(grp)} | total so far: {len(out_rows)}")

    out = pd.DataFrame(out_rows)
    summ = summarize(out)

    out_path = os.path.join(OUT_DIR, "trades_trailing_capped_market_only_step5.csv")
    summ_path = os.path.join(OUT_DIR, "summary_trailing_capped_market_only_step5.csv")

    out.to_csv(out_path, index=False)
    summ.to_csv(summ_path, index=False)

    print("\nSaved:")
    print(out_path)
    print(summ_path)

    print("\n=== SUMMARY (STEP-5) ===")
    print(summ.to_string(index=False))

if __name__ == "__main__":
    main()


STEP-5 | 30-min resample + confirm closes | CAPPED | market-hours only
DELAY: 60 | RESAMPLE: 30T | ATR_MULT: 3.0 | CONFIRM_BARS: 2
Output: D:/work/Client/Maatra/Trade Level Data\TrailingSL_CAPPED_MKT1430_2100_STEP5_30MIN_CONFIRM
Trades to evaluate: 11578


C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: 

Processed ACN | trades: 7 | total so far: 7


C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: 

Processed ADBE | trades: 83 | total so far: 90


...

Processed XLK | trades: 155 | total so far: 11338


C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: 

Processed XLY | trades: 53 | total so far: 11391


C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_7024\4161361056.py:157: 

Processed XRAY | trades: 187 | total so far: 11578

Saved:
D:/work/Client/Maatra/Trade Level Data\TrailingSL_CAPPED_MKT1430_2100_STEP5_30MIN_CONFIRM\trades_trailing_capped_market_only_step5.csv
D:/work/Client/Maatra/Trade Level Data\TrailingSL_CAPPED_MKT1430_2100_STEP5_30MIN_CONFIRM\summary_trailing_capped_market_only_step5.csv

=== SUMMARY (STEP-5) ===
          Group  Trades  TrailingTriggered  PctTriggered  Improved  Worse  Unchanged  AvgPctImprovement  MedianPctImprovement  Triggered_PctImproved  Triggered_AvgPctImprovement
            ALL   11578               1651      0.142598      1022    629       9927           0.000899                   0.0               0.619019                     0.006304
 Direction=LONG   10922               1519      0.139077       931    588       9403           0.000938                   0.0               0.612903                     0.006742
Direction=SHORT     656                132      0.201220        91     41        524           0.000254       

Implemented a volatility-based trailing stop-loss using 3×ATR with dynamic behavior (tightening in trending conditions and staying wide in ranging markets), capped at the original exit date.

Restricted the trailing stop-loss logic to regular market hours only (14:30–21:00) to eliminate pre-market and post-market noise.

Added a trend/regime filter to enable trailing only when there was sufficient favorable price movement and directional persistence.

Introduced a delay after market open and switched to a chandelier-style trailing stop based on closing prices, with exits triggered on close rather than intrabar wicks.

Tested a smoothed intraday approach by resampling M5 data to higher timeframes (15–30 minutes) and requiring close-based confirmation before triggering the trailing stop.

####### Trying out Manish IDeas ##### 
Full overall code: SME-style adaptive trailing (CAPPED, market hours, 30-min bars)

In [ ]:
import os
import numpy as np
import pandas as pd
from dataclasses import dataclass
from datetime import timedelta

# ============================================================
# PATHS (EDIT)
# ============================================================
TRADE_XLSX_PATH      = r"D:/work/Client/Maatra/Trade Level Data/3 Month vol 14 data with sharpe prob Fnl.xlsx"
M5_DIR               = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data"
M5_FILE_LIST_PATH    = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data/m5_file_list.csv"
MAPPING_XLSX_PATH    = r"D:/work/Client/Maatra/Trade Level Data/Instrument Mapping.xlsx"

OUT_DIR = os.path.join(os.path.dirname(TRADE_XLSX_PATH), "TrailingSL_CAPPED_MKT1430_2100_SME_ADAPTIVE")
os.makedirs(OUT_DIR, exist_ok=True)

# ============================================================
# RUN MODE
# ============================================================
RUN_ALL_TRADES = True
N_SAMPLE_TRADES = 3000
RANDOM_SEED = 42

# ============================================================
# MARKET HOURS (IST)
# ============================================================
MARKET_START = "14:30"
MARKET_END   = "21:00"

# ============================================================
# TRADE TIMING
# ============================================================
APPLY_FROM_NEXT_DAY = True   # entry at EOD; start from next day
CAPPED = True

# ============================================================
# BAR FREQUENCY FOR STOP CALCS
# ============================================================
RESAMPLE_RULE = "30T"        # 30-min. For multi-day holds, 30T/60T recommended.

# ============================================================
# SME-STYLE ADAPTIVE STOP PARAMETERS (TUNE)
# ============================================================
# Regression window on resampled closes
REG_WINDOW = 20              # SME default ~20. On 30T, that's ~10 hours of bars.

# ATR period on resampled bars
ATR_PERIOD = 20              # SME default ~20. On 30T, ~10 hours. Try 14/20/30.

# Trend threshold using atan(slope_norm)
# slope_norm = slope / price => unitless. atan(slope_norm) ~ slope_norm for small slopes.
ATAN_THRESHOLD = 0.0020      # SME slope threshold; keep similar scale for small-angle approx.
SENSITIVITY = 1.0            # scales trend-based stop distance

# ATR% fallback parameters
ATR_FALLBACK_MULT = 4.0      # SME used 4x ATR%
MIN_STOP_PCT = 0.0010        # 0.10%
MAX_STOP_PCT = 0.0150        # 1.50%

# Exit trigger type (reduce noise)
TRIGGER_ON_CLOSE = True      # if False, uses wick lows/highs vs stop

# Optional: delay after open (still useful)
DELAY_MINUTES_AFTER_OPEN = 30

# ============================================================
# Helpers
# ============================================================

def normalize_ticker(x: str) -> str:
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return ""
    x = str(x).strip().upper()
    return "".join([ch for ch in x if ch.isalnum()])

def trade_base_from_currency(currency: str) -> str:
    if currency is None or (isinstance(currency, float) and np.isnan(currency)):
        return ""
    s = str(currency).strip().upper()
    base = s.split("/")[0].strip() if "/" in s else s
    return normalize_ticker(base)

def normalize_direction(x) -> str:
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return "UNKNOWN"
    s = str(x).strip().upper()
    if s in ["LONG", "BUY", "B", "1", "1.0", "+1", "+1.0"]:
        return "LONG"
    if s in ["SHORT", "SELL", "S", "-1", "-1.0"]:
        return "SHORT"
    try:
        v = float(s)
        if v > 0: return "LONG"
        if v < 0: return "SHORT"
    except Exception:
        pass
    return "UNKNOWN"

def load_trade_to_m5_mapping(mapping_xlsx_path: str) -> dict:
    mp = pd.read_excel(mapping_xlsx_path)
    mp.columns = [c.strip() for c in mp.columns]
    if "org_symbol" not in mp.columns or "Symbol" not in mp.columns:
        raise ValueError("Mapping file must contain columns: org_symbol, Symbol")
    mp["m5_ticker"] = mp["org_symbol"].apply(normalize_ticker)
    mp["trade_base"] = mp["Symbol"].astype(str).str.upper().str.strip().str.split("/").str[0].apply(normalize_ticker)
    mp = mp[(mp["trade_base"] != "") & (mp["m5_ticker"] != "")]
    mp = mp.drop_duplicates(subset=["trade_base"], keep="first")
    return dict(zip(mp["trade_base"], mp["m5_ticker"]))

TRADE_TO_M5 = load_trade_to_m5_mapping(MAPPING_XLSX_PATH)

def map_trade_base_to_m5(trade_base: str) -> str:
    t = normalize_ticker(trade_base)
    return TRADE_TO_M5.get(t, t)

def load_m5_file_map(m5_dir: str, file_list_path: str) -> dict:
    fl = pd.read_csv(file_list_path)
    fl.columns = [c.strip().lower() for c in fl.columns]
    if "ticker" not in fl.columns or "filename" not in fl.columns:
        raise ValueError("m5_file_list.csv must have columns: ticker, filename")
    fl["ticker_norm"] = fl["ticker"].apply(normalize_ticker)
    fl["path"] = fl["filename"].apply(lambda f: os.path.join(m5_dir, f))
    return dict(zip(fl["ticker_norm"], fl["path"]))

M5_MAP = load_m5_file_map(M5_DIR, M5_FILE_LIST_PATH)
M5_TICKERS = set(M5_MAP.keys())

def filter_market_hours(df: pd.DataFrame) -> pd.DataFrame:
    if df.empty:
        return df
    dfi = df.set_index("_dt", drop=False).sort_index()
    dfi = dfi.between_time(MARKET_START, MARKET_END, inclusive="both")
    return dfi.reset_index(drop=True)

def apply_delay_filter(window: pd.DataFrame, delay_minutes: int) -> pd.DataFrame:
    if delay_minutes <= 0 or window.empty:
        return window
    w = window.copy()
    w["d"] = w["_dt"].dt.normalize()
    thr = w["d"] + pd.to_timedelta(MARKET_START + ":00")
    w = w[w["_dt"] >= (thr + pd.to_timedelta(delay_minutes, unit="m"))]
    return w.drop(columns=["d"])

def resample_ohlc(df: pd.DataFrame, rule: str) -> pd.DataFrame:
    if df.empty:
        return df
    dfi = df.set_index("_dt").sort_index()
    ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
        "open": "first",
        "high": "max",
        "low": "min",
        "close": "last",
    }).dropna()
    return ohlc.reset_index()

def compute_atr(df: pd.DataFrame, period: int) -> pd.Series:
    high = df["high"]
    low = df["low"]
    close = df["close"]
    tr = pd.concat([
        high - low,
        (high - close.shift(1)).abs(),
        (low - close.shift(1)).abs()
    ], axis=1).max(axis=1)
    return tr.rolling(period, min_periods=period).mean()

def prepare_m5_to_rs_market_only(ticker: str) -> pd.DataFrame | None:
    fp = M5_MAP.get(ticker)
    if not fp or not os.path.exists(fp):
        return None

    df = pd.read_csv(fp)
    df.columns = [c.strip().lower() for c in df.columns]
    needed = ["date", "open", "high", "low", "close"]
    if not all(c in df.columns for c in needed):
        return None

    df["_dt"] = pd.to_datetime(df["date"], errors="coerce")
    df = df.dropna(subset=["_dt"]).sort_values("_dt").reset_index(drop=True)

    for c in ["open", "high", "low", "close"]:
        df[c] = pd.to_numeric(df[c], errors="coerce")
    df = df.dropna(subset=["open", "high", "low", "close"])

    df = filter_market_hours(df)
    if df.empty:
        return None

    rs = resample_ohlc(df, RESAMPLE_RULE)
    if rs.empty:
        return None

    rs = apply_delay_filter(rs, DELAY_MINUTES_AFTER_OPEN)
    if rs.empty:
        return None

    rs["ATR"] = compute_atr(rs, ATR_PERIOD)
    return rs

def build_trade_summary(raw: pd.DataFrame):
    df = raw.copy()
    df.columns = [c.strip() for c in df.columns]

    required = ["TradeID", "Currency", "Direction", "date", "price", "Closing Date", "DayStatus"]
    missing = [c for c in required if c not in df.columns]
    if missing:
        raise ValueError(f"Trade file missing required columns: {missing}")

    df["date"] = pd.to_datetime(df["date"], errors="coerce")
    df["Closing Date"] = pd.to_datetime(df["Closing Date"], errors="coerce")
    df["price"] = pd.to_numeric(df["price"], errors="coerce")
    df["DayStatusU"] = df["DayStatus"].astype(str).str.upper().str.strip()

    df["TradeBase"] = df["Currency"].apply(trade_base_from_currency)
    df["TickerNorm"] = df["TradeBase"].apply(map_trade_base_to_m5)
    df["DirectionNorm"] = df["Direction"].apply(normalize_direction)

    rows, reasons = [], []

    for tid, g in df.groupby("TradeID", dropna=True):
        g = g.sort_values("date")
        currency = g["Currency"].dropna().iloc[0] if g["Currency"].notna().any() else np.nan
        direction = g["DirectionNorm"].dropna().iloc[0] if g["DirectionNorm"].notna().any() else "UNKNOWN"
        trade_base = g["TradeBase"].dropna().iloc[0] if g["TradeBase"].notna().any() else ""
        ticker = g["TickerNorm"].dropna().iloc[0] if g["TickerNorm"].notna().any() else ""

        open_mask = g["DayStatusU"].eq("OPEN")
        entry_date = g.loc[open_mask, "date"].dropna().min() if open_mask.any() else g["date"].dropna().min()
        exit_date = g["Closing Date"].dropna().max()

        entry_px = np.nan
        if pd.notna(entry_date):
            day = entry_date.normalize()
            day_rows = g[g["date"].dt.normalize() == day]
            if day_rows["price"].notna().any():
                entry_px = float(day_rows["price"].dropna().iloc[-1])

        exit_px = np.nan
        if pd.notna(exit_date):
            day = exit_date.normalize()
            day_rows = g[g["date"].dt.normalize() == day]
            if day_rows["price"].notna().any():
                exit_px = float(day_rows["price"].dropna().iloc[-1])

        miss = []
        if pd.isna(entry_date): miss.append("MISSING_ENTRY_DATE")
        if pd.isna(exit_date): miss.append("MISSING_EXIT_DATE")
        if pd.isna(entry_px): miss.append("MISSING_ENTRY_PRICE")
        if pd.isna(exit_px): miss.append("MISSING_EXIT_PRICE")
        if not ticker: miss.append("MISSING_TICKER")
        if ticker and (ticker not in M5_TICKERS): miss.append("TICKER_NOT_IN_M5_LIST")
        if direction == "UNKNOWN": miss.append("UNKNOWN_DIRECTION")

        if miss:
            reasons.append({"TradeID": tid, "TickerNorm": ticker, "MissingReasons": ";".join(miss)})

        rows.append({
            "TradeID": tid,
            "Currency": currency,
            "TradeBase": trade_base,
            "TickerNorm": ticker,
            "Direction": direction,
            "EntryDate": entry_date,
            "ExitDate_Original": exit_date,
            "EntryPrice": entry_px,
            "ExitPrice_Original": exit_px,
            "HasAllCoreFields": (len(miss) == 0),
            "MissingReasons": ";".join(miss) if miss else ""
        })

    trade_summary = pd.DataFrame(rows)
    missing_df = pd.DataFrame(reasons)
    coverage = pd.DataFrame([{
        "Raw_Unique_TradeIDs": int(df["TradeID"].nunique()),
        "Extracted_Unique_TradeIDs": int(trade_summary["TradeID"].nunique()),
        "Trades_With_All_Core_Fields": int(trade_summary["HasAllCoreFields"].sum()),
        "Trades_Missing_Something": int((~trade_summary["HasAllCoreFields"]).sum()),
    }])
    return trade_summary, missing_df, coverage

# ============================================================
# SME adaptive stop distance
# ============================================================

def adaptive_stop_distance_pct(bars: pd.DataFrame, is_long: bool) -> dict:
    """
    Returns stop distance as a percentage of price (unitless),
    using:
      - quadratic fit slope+acceleration if atan(slope_norm) exceeds threshold
      - else ATR% fallback
    """
    if len(bars) < max(REG_WINDOW, ATR_PERIOD):
        return {"mode": "insufficient", "stop_pct": np.nan, "atan_slope": np.nan, "atr_pct": np.nan}

    recent = bars["close"].iloc[-REG_WINDOW:].astype(float)
    x = np.arange(len(recent), dtype=float)

    # quadratic fit
    a, b, c = np.polyfit(x, recent.values, 2)
    # normalized slope (as SME): slope at last x divided by last price
    slope = (2 * a * x[-1] + b) / recent.iloc[-1]
    acceleration = (2 * a)

    atan_slope = float(np.arctan(slope))  # for visual interpretation

    # ATR% of price
    atr = bars["ATR"].iloc[-1]
    px = bars["close"].iloc[-1]
    atr_pct = float(atr / px) if (pd.notna(atr) and atr > 0 and px > 0) else np.nan

    # trend regime
    if abs() > ATAN_THRESHOLD and pd.notna(atan_slope):
        stop_distance = abs(slope) * SENSITIVITY * (1.0 + abs(acceleration))
        # interpret as pct distance already (unitless)
        stop_pct = float(stop_distance)
        # clamp to sane bounds (optional, but prevents crazy outliers)
        stop_pct = float(np.clip(stop_pct, MIN_STOP_PCT, MAX_STOP_PCT))
        return {"mode": "trend_fit", "stop_pct": stop_pct, "atan_slope": atan_slope, "atr_pct": atr_pct}

    # range regime fallback
    if pd.isna(atr_pct):
        return {"mode": "atr_missing", "stop_pct": np.nan, "atan_slope": atan_slope, "atr_pct": atr_pct}

    stop_pct = float(np.clip(atr_pct * ATR_FALLBACK_MULT, MIN_STOP_PCT, MAX_STOP_PCT))
    return {"mode": "atr_fallback", "stop_pct": stop_pct, "atan_slope": atan_slope, "atr_pct": atr_pct}

# ============================================================
# Trailing simulation (CAPPED)
# ============================================================

@dataclass
class TrailResult:
    exit_time: pd.Timestamp
    exit_price: float
    exit_reason: str

def direction_aware_improvement(direction: str, new_exit: float, old_exit: float) -> float:
    d = normalize_direction(direction)
    return float(new_exit - old_exit) if d == "LONG" else float(old_exit - new_exit)

def simulate_sme_capped(tr: pd.Series, rs: pd.DataFrame, debug: bool=False):
    """
    Trail stop where stop distance adapts each bar based on market conditions.
    - For LONG:
        stop = max(stop, best_close * (1 - stop_pct))
      For SHORT:
        stop = min(stop, best_close * (1 + stop_pct))
    Uses best_close since entry (chandelier-close style), but distance is adaptive.
    """
    entry_date = pd.to_datetime(tr["EntryDate"])
    exit_date  = pd.to_datetime(tr["ExitDate_Original"])
    entry_px   = float(tr["EntryPrice"])
    orig_exit_px = float(tr["ExitPrice_Original"])

    direction = normalize_direction(tr["Direction"])
    is_long = (direction == "LONG")

    start_dt = (entry_date + timedelta(days=1)) if APPLY_FROM_NEXT_DAY else entry_date
    end_dt   = exit_date + timedelta(days=1)

    w = rs[(rs["_dt"] >= start_dt) & (rs["_dt"] < end_dt)].copy()
    if w.empty:
        return TrailResult(exit_date, orig_exit_px, "NoRSDataInWindow"), None

    best_close = entry_px
    stop = -np.inf if is_long else np.inf
    dbg_rows = []

    for i in range(len(w)):
        sub = w.iloc[:i+1].copy()
        row = w.iloc[i]
        dt = row["_dt"]

        close = float(row["close"])
        high = float(row["high"])
        low  = float(row["low"])

        # chandelier close tracking
        if is_long:
            best_close = max(best_close, close)
        else:
            best_close = min(best_close, close)

        # compute adaptive stop pct using recent window
        info = adaptive_stop_distance_pct(sub, is_long=is_long)
        stop_pct = info["stop_pct"]

        if pd.isna(stop_pct):
            continue

        # update stop level
        if is_long:
            stop = max(stop, best_close * (1.0 - stop_pct))
            hit_val = close if TRIGGER_ON_CLOSE else low
            if hit_val <= stop:
                if debug:
                    dbg_rows.append({"dt": dt, "close": close, "best_close": best_close, "stop": stop, **info})
                return TrailResult(dt, float(stop), "TrailingSL"), pd.DataFrame(dbg_rows)
        else:
            stop = min(stop, best_close * (1.0 + stop_pct))
            hit_val = close if TRIGGER_ON_CLOSE else high
            if hit_val >= stop:
                if debug:
                    dbg_rows.append({"dt": dt, "close": close, "best_close": best_close, "stop": stop, **info})
                return TrailResult(dt, float(stop), "TrailingSL"), pd.DataFrame(dbg_rows)

        if debug and (i % 3 == 0):  # sample debug rows
            dbg_rows.append({"dt": dt, "close": close, "best_close": best_close, "stop": stop, **info})

    return TrailResult(exit_date, orig_exit_px, "OriginalExit"), pd.DataFrame(dbg_rows) if debug else None

# ============================================================
# Summary
# ============================================================

def summarize(out: pd.DataFrame) -> pd.DataFrame:
    df = out.copy()
    df["TriggeredFlag"] = df["ExitReason"].astype(str).eq("TrailingSL")
    df["ImprovedFlag"] = df["PriceImprovement"] > 0
    df["WorseFlag"] = df["PriceImprovement"] < 0
    df["UnchangedFlag"] = (df["PriceImprovement"] == 0) | df["PriceImprovement"].isna()

    def agg(g):
        n = len(g)
        trig = int(g["TriggeredFlag"].sum())
        return {
            "Trades": n,
            "TrailingTriggered": trig,
            "PctTriggered": trig / n if n else np.nan,
            "Improved": int(g["ImprovedFlag"].sum()),
            "Worse": int(g["WorseFlag"].sum()),
            "Unchanged": int(g["UnchangedFlag"].sum()),
            "AvgPctImprovement": float(g["PctImprovement_vs_OriginalExit"].mean(skipna=True)),
            "Triggered_PctImproved": float(g.loc[g["TriggeredFlag"], "ImprovedFlag"].mean()) if trig else np.nan,
            "Triggered_AvgPctImprovement": float(g.loc[g["TriggeredFlag"], "PctImprovement_vs_OriginalExit"].mean(skipna=True)) if trig else np.nan,
        }

    rows = [{"Group": "ALL", **agg(df)}]
    for d, g in df.groupby(df["Direction"].astype(str).str.upper().str.strip()):
        rows.append({"Group": f"Direction={d}", **agg(g)})
    return pd.DataFrame(rows)

# ============================================================
# MAIN
# ============================================================

def main():
    print("SME Adaptive Trailing | CAPPED | market-hours only | resample:", RESAMPLE_RULE)
    print("REG_WINDOW:", REG_WINDOW, "ATR_PERIOD:", ATR_PERIOD, "ATAN_THRESHOLD:", ATAN_THRESHOLD)
    print("ATR_FALLBACK_MULT:", ATR_FALLBACK_MULT, "STOP_PCT bounds:", (MIN_STOP_PCT, MAX_STOP_PCT))
    print("Delay after open:", DELAY_MINUTES_AFTER_OPEN)
    print("Output:", OUT_DIR)

    raw = pd.read_excel(TRADE_XLSX_PATH)
    trades, missing_df, coverage_df = build_trade_summary(raw)

    missing_df.to_csv(os.path.join(OUT_DIR, "trade_summary_missing_reasons.csv"), index=False)
    coverage_df.to_csv(os.path.join(OUT_DIR, "coverage_report.csv"), index=False)

    if RUN_ALL_TRADES:
        sample = trades.copy()
    else:
        sample = trades.sample(n=min(N_SAMPLE_TRADES, len(trades)), random_state=RANDOM_SEED).copy()

    sample = sample[sample["HasAllCoreFields"]].reset_index(drop=True)
    print("Trades to evaluate:", len(sample))

    # Cache RS data per ticker
    rs_cache = {}
    for tkr in sorted(sample["TickerNorm"].unique()):
        if tkr not in M5_TICKERS:
            rs_cache[tkr] = None
        else:
            rs_cache[tkr] = prepare_m5_to_rs_market_only(tkr)

    out_rows = []
    debug_pick = []  # collect a small debug set
    total = len(sample)
    done = 0

    for tkr, grp in sample.groupby("TickerNorm"):
        rs = rs_cache.get(tkr)
        if rs is None or rs.empty:
            done += len(grp)
            continue

        for _, tr in grp.iterrows():
            want_debug = (len(debug_pick) < 30)  # debug only first 30 trades
            res, dbg_df = simulate_sme_capped(tr, rs, debug=want_debug)

            old_exit = float(tr["ExitPrice_Original"])
            new_exit = float(res.exit_price)
            impr = direction_aware_improvement(tr["Direction"], new_exit, old_exit)

            out_rows.append({
                "TradeID": tr["TradeID"],
                "TickerNorm": tr["TickerNorm"],
                "Direction": tr["Direction"],
                "EntryDate": tr["EntryDate"],
                "EntryPrice": float(tr["EntryPrice"]),
                "ExitDate_Original": tr["ExitDate_Original"],
                "ExitPrice_Original": old_exit,
                "ExitTime_Trailing": res.exit_time,
                "ExitPrice_Trailing": new_exit,
                "ExitReason": res.exit_reason,
                "PriceImprovement": impr,
                "PctImprovement_vs_OriginalExit": (impr / old_exit) if old_exit else np.nan,
            })

            if want_debug and dbg_df is not None and not dbg_df.empty:
                dbg_df = dbg_df.copy()
                dbg_df["TradeID"] = tr["TradeID"]
                dbg_df["TickerNorm"] = tr["TickerNorm"]
                dbg_df["Direction"] = tr["Direction"]
                debug_pick.append(dbg_df)

        done += len(grp)
        if done % 2000 < len(grp):
            print(f"Processed {done}/{total} trades...")

    out = pd.DataFrame(out_rows)
    summ = summarize(out)

    out_path = os.path.join(OUT_DIR, "trades_trailing_capped_market_only_sme_adaptive.csv")
    summ_path = os.path.join(OUT_DIR, "summary_trailing_capped_market_only_sme_adaptive.csv")
    out.to_csv(out_path, index=False)
    summ.to_csv(summ_path, index=False)

    if debug_pick:
        dbg = pd.concat(debug_pick, ignore_index=True)
        dbg_path = os.path.join(OUT_DIR, "debug_sme_adaptive_samples.csv")
        dbg.to_csv(dbg_path, index=False)
        print("Saved debug:", dbg_path)

    print("\nSaved:")
    print(out_path)
    print(summ_path)

    print("\n=== SUMMARY ===")
    print(summ.to_string(index=False))

if __name__ == "__main__":
    main()


SME Adaptive Trailing | CAPPED | market-hours only | resample: 30T
REG_WINDOW: 20 ATR_PERIOD: 20 ATAN_THRESHOLD: 0.002
ATR_FALLBACK_MULT: 4.0 STOP_PCT bounds: (0.001, 0.015)
Delay after open: 30
Output: D:/work/Client/Maatra/Trade Level Data\TrailingSL_CAPPED_MKT1430_2100_SME_ADAPTIVE
Trades to evaluate: 11578


C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3591791946.py:149: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3591791946.py:149: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3591791946.py:149: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3591791946.py:149: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3591791946.py:149: 

Processed 2091/11578 trades...
Processed 4278/11578 trades...
Processed 6166/11578 trades...
Processed 8052/11578 trades...
Processed 10193/11578 trades...
Saved debug: D:/work/Client/Maatra/Trade Level Data\TrailingSL_CAPPED_MKT1430_2100_SME_ADAPTIVE\debug_sme_adaptive_samples.csv

Saved:
D:/work/Client/Maatra/Trade Level Data\TrailingSL_CAPPED_MKT1430_2100_SME_ADAPTIVE\trades_trailing_capped_market_only_sme_adaptive.csv
D:/work/Client/Maatra/Trade Level Data\TrailingSL_CAPPED_MKT1430_2100_SME_ADAPTIVE\summary_trailing_capped_market_only_sme_adaptive.csv

=== SUMMARY ===
          Group  Trades  TrailingTriggered  PctTriggered  Improved  Worse  Unchanged  AvgPctImprovement  Triggered_PctImproved  Triggered_AvgPctImprovement
            ALL   11578               2526      0.218172      1626    900       9052           0.001835               0.643705                     0.008412
 Direction=LONG   10922               2346      0.214796      1504    842       8576           0.001826      

In [2]:
import os
import numpy as np
import pandas as pd
from dataclasses import dataclass
from datetime import timedelta

# ============================================================
# PATHS (EDIT)
# ============================================================
TRADE_XLSX_PATH      = r"D:/work/Client/Maatra/Trade Level Data/3 Month vol 14 data with sharpe prob Fnl.xlsx"
M5_DIR               = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data"
M5_FILE_LIST_PATH    = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data/m5_file_list.csv"
MAPPING_XLSX_PATH    = r"D:/work/Client/Maatra/Trade Level Data/Instrument Mapping.xlsx"

OUT_DIR = os.path.join(os.path.dirname(TRADE_XLSX_PATH), "TrailingSL_CAPPED_MKT1430_2100_SME_GRID_STEP2")
os.makedirs(OUT_DIR, exist_ok=True)

# ============================================================
# RUN MODE
# ============================================================
RUN_ALL_TRADES = True      # <--- HIGHER SAMPLE / FULL RUN
N_SAMPLE_TRADES = 5000     # used only if RUN_ALL_TRADES=False
RANDOM_SEED = 42

# ============================================================
# MARKET HOURS (IST)
# ============================================================
MARKET_START = "14:30"
MARKET_END   = "21:00"

APPLY_FROM_NEXT_DAY = True

# ============================================================
# Helpers
# ============================================================

def normalize_ticker(x: str) -> str:
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return ""
    x = str(x).strip().upper()
    return "".join([ch for ch in x if ch.isalnum()])

def trade_base_from_currency(currency: str) -> str:
    if currency is None or (isinstance(currency, float) and np.isnan(currency)):
        return ""
    s = str(currency).strip().upper()
    base = s.split("/")[0].strip() if "/" in s else s
    return normalize_ticker(base)

def normalize_direction(x) -> str:
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return "UNKNOWN"
    s = str(x).strip().upper()
    if s in ["LONG", "BUY", "B", "1", "1.0", "+1", "+1.0"]:
        return "LONG"
    if s in ["SHORT", "SELL", "S", "-1", "-1.0"]:
        return "SHORT"
    try:
        v = float(s)
        if v > 0: return "LONG"
        if v < 0: return "SHORT"
    except Exception:
        pass
    return "UNKNOWN"

def load_trade_to_m5_mapping(mapping_xlsx_path: str) -> dict:
    mp = pd.read_excel(mapping_xlsx_path)
    mp.columns = [c.strip() for c in mp.columns]
    if "org_symbol" not in mp.columns or "Symbol" not in mp.columns:
        raise ValueError("Mapping file must contain columns: org_symbol, Symbol")
    mp["m5_ticker"] = mp["org_symbol"].apply(normalize_ticker)
    mp["trade_base"] = mp["Symbol"].astype(str).str.upper().str.strip().str.split("/").str[0].apply(normalize_ticker)
    mp = mp[(mp["trade_base"] != "") & (mp["m5_ticker"] != "")]
    mp = mp.drop_duplicates(subset=["trade_base"], keep="first")
    return dict(zip(mp["trade_base"], mp["m5_ticker"]))

TRADE_TO_M5 = load_trade_to_m5_mapping(MAPPING_XLSX_PATH)

def map_trade_base_to_m5(trade_base: str) -> str:
    t = normalize_ticker(trade_base)
    return TRADE_TO_M5.get(t, t)

def load_m5_file_map(m5_dir: str, file_list_path: str) -> dict:
    fl = pd.read_csv(file_list_path)
    fl.columns = [c.strip().lower() for c in fl.columns]
    if "ticker" not in fl.columns or "filename" not in fl.columns:
        raise ValueError("m5_file_list.csv must have columns: ticker, filename")
    fl["ticker_norm"] = fl["ticker"].apply(normalize_ticker)
    fl["path"] = fl["filename"].apply(lambda f: os.path.join(m5_dir, f))
    return dict(zip(fl["ticker_norm"], fl["path"]))

M5_MAP = load_m5_file_map(M5_DIR, M5_FILE_LIST_PATH)
M5_TICKERS = set(M5_MAP.keys())

def filter_market_hours(df: pd.DataFrame) -> pd.DataFrame:
    if df.empty:
        return df
    dfi = df.set_index("_dt", drop=False).sort_index()
    dfi = dfi.between_time(MARKET_START, MARKET_END, inclusive="both")
    return dfi.reset_index(drop=True)

def apply_delay_filter(window: pd.DataFrame, delay_minutes: int) -> pd.DataFrame:
    if delay_minutes <= 0 or window.empty:
        return window
    w = window.copy()
    w["d"] = w["_dt"].dt.normalize()
    thr = w["d"] + pd.to_timedelta(MARKET_START + ":00")
    w = w[w["_dt"] >= (thr + pd.to_timedelta(delay_minutes, unit="m"))]
    return w.drop(columns=["d"])

def resample_ohlc(df: pd.DataFrame, rule: str) -> pd.DataFrame:
    if df.empty:
        return df
    dfi = df.set_index("_dt").sort_index()
    ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
        "open": "first",
        "high": "max",
        "low": "min",
        "close": "last",
    }).dropna()
    return ohlc.reset_index()

def compute_atr(df: pd.DataFrame, period: int) -> pd.Series:
    high = df["high"]
    low = df["low"]
    close = df["close"]
    tr = pd.concat([
        high - low,
        (high - close.shift(1)).abs(),
        (low - close.shift(1)).abs()
    ], axis=1).max(axis=1)
    return tr.rolling(period, min_periods=period).mean()

def prepare_m5_to_rs_market_only(ticker: str, resample_rule: str, atr_period: int, delay_mins: int) -> pd.DataFrame | None:
    fp = M5_MAP.get(ticker)
    if not fp or not os.path.exists(fp):
        return None

    df = pd.read_csv(fp)
    df.columns = [c.strip().lower() for c in df.columns]
    needed = ["date", "open", "high", "low", "close"]
    if not all(c in df.columns for c in needed):
        return None

    df["_dt"] = pd.to_datetime(df["date"], errors="coerce")
    df = df.dropna(subset=["_dt"]).sort_values("_dt").reset_index(drop=True)

    for c in ["open", "high", "low", "close"]:
        df[c] = pd.to_numeric(df[c], errors="coerce")
    df = df.dropna(subset=["open", "high", "low", "close"])

    df = filter_market_hours(df)
    if df.empty:
        return None

    rs = resample_ohlc(df, resample_rule)
    if rs.empty:
        return None

    rs = apply_delay_filter(rs, delay_mins)
    if rs.empty:
        return None

    rs["ATR"] = compute_atr(rs, atr_period)
    return rs

def build_trade_summary(raw: pd.DataFrame):
    df = raw.copy()
    df.columns = [c.strip() for c in df.columns]

    required = ["TradeID", "Currency", "Direction", "date", "price", "Closing Date", "DayStatus"]
    missing = [c for c in required if c not in df.columns]
    if missing:
        raise ValueError(f"Trade file missing required columns: {missing}")

    df["date"] = pd.to_datetime(df["date"], errors="coerce")
    df["Closing Date"] = pd.to_datetime(df["Closing Date"], errors="coerce")
    df["price"] = pd.to_numeric(df["price"], errors="coerce")
    df["DayStatusU"] = df["DayStatus"].astype(str).str.upper().str.strip()

    df["TradeBase"] = df["Currency"].apply(trade_base_from_currency)
    df["TickerNorm"] = df["TradeBase"].apply(map_trade_base_to_m5)
    df["DirectionNorm"] = df["Direction"].apply(normalize_direction)

    rows = []
    for tid, g in df.groupby("TradeID", dropna=True):
        g = g.sort_values("date")
        direction = g["DirectionNorm"].dropna().iloc[0] if g["DirectionNorm"].notna().any() else "UNKNOWN"
        trade_base = g["TradeBase"].dropna().iloc[0] if g["TradeBase"].notna().any() else ""
        ticker = g["TickerNorm"].dropna().iloc[0] if g["TickerNorm"].notna().any() else ""

        open_mask = g["DayStatusU"].eq("OPEN")
        entry_date = g.loc[open_mask, "date"].dropna().min() if open_mask.any() else g["date"].dropna().min()
        exit_date = g["Closing Date"].dropna().max()

        entry_px = np.nan
        if pd.notna(entry_date):
            day = entry_date.normalize()
            day_rows = g[g["date"].dt.normalize() == day]
            if day_rows["price"].notna().any():
                entry_px = float(day_rows["price"].dropna().iloc[-1])

        exit_px = np.nan
        if pd.notna(exit_date):
            day = exit_date.normalize()
            day_rows = g[g["date"].dt.normalize() == day]
            if day_rows["price"].notna().any():
                exit_px = float(day_rows["price"].dropna().iloc[-1])

        has_core = (pd.notna(entry_date) and pd.notna(exit_date) and pd.notna(entry_px) and pd.notna(exit_px)
                    and ticker != "" and (ticker in M5_TICKERS) and direction != "UNKNOWN")

        rows.append({
            "TradeID": tid,
            "TradeBase": trade_base,
            "TickerNorm": ticker,
            "Direction": direction,
            "EntryDate": entry_date,
            "ExitDate_Original": exit_date,
            "EntryPrice": entry_px,
            "ExitPrice_Original": exit_px,
            "HasAllCoreFields": has_core
        })
    return pd.DataFrame(rows)

def adaptive_stop_distance_pct(bars: pd.DataFrame, reg_window: int, atan_threshold: float,
                              atr_fallback_mult: float, min_stop_pct: float, max_stop_pct: float,
                              sensitivity: float) -> float:
    if len(bars) < reg_window or bars["ATR"].dropna().empty:
        return np.nan

    recent = bars["close"].iloc[-reg_window:].astype(float)
    x = np.arange(len(recent), dtype=float)

    a, b, c = np.polyfit(x, recent.values, 2)
    slope = (2 * a * x[-1] + b) / recent.iloc[-1]
    acceleration = (2 * a)
    atan_slope = float(np.arctan(slope))

    atr = bars["ATR"].iloc[-1]
    px = bars["close"].iloc[-1]
    atr_pct = float(atr / px) if (pd.notna(atr) and atr > 0 and px > 0) else np.nan
    if pd.isna(atr_pct):
        return np.nan

    if abs(atan_slope) > atan_threshold:
        stop_pct = abs(slope) * sensitivity * (1.0 + abs(acceleration))
        return float(np.clip(stop_pct, min_stop_pct, max_stop_pct))

    stop_pct = atr_pct * atr_fallback_mult
    return float(np.clip(stop_pct, min_stop_pct, max_stop_pct))

@dataclass
class TrailResult:
    exit_time: pd.Timestamp
    exit_price: float
    exit_reason: str

def simulate_one_trade(tr: pd.Series, rs: pd.DataFrame,
                       resample_rule: str, atr_period: int, reg_window: int,
                       atan_threshold: float, atr_fallback_mult: float,
                       min_stop_pct: float, max_stop_pct: float,
                       sensitivity: float, trigger_on_close: bool) -> TrailResult:

    entry_date = pd.to_datetime(tr["EntryDate"])
    exit_date  = pd.to_datetime(tr["ExitDate_Original"])
    entry_px   = float(tr["EntryPrice"])
    orig_exit_px = float(tr["ExitPrice_Original"])
    direction = normalize_direction(tr["Direction"])
    is_long = (direction == "LONG")

    start_dt = (entry_date + timedelta(days=1)) if APPLY_FROM_NEXT_DAY else entry_date
    end_dt   = exit_date + timedelta(days=1)

    w = rs[(rs["_dt"] >= start_dt) & (rs["_dt"] < end_dt)].copy()
    if w.empty:
        return TrailResult(exit_date, orig_exit_px, "NoRSDataInWindow")

    best_close = entry_px
    stop = -np.inf if is_long else np.inf

    for i in range(len(w)):
        sub = w.iloc[:i+1].copy()
        row = w.iloc[i]
        dt = row["_dt"]

        close = float(row["close"])
        high = float(row["high"])
        low  = float(row["low"])

        if is_long:
            best_close = max(best_close, close)
        else:
            best_close = min(best_close, close)

        stop_pct = adaptive_stop_distance_pct(
            sub, reg_window, atan_threshold,
            atr_fallback_mult, min_stop_pct, max_stop_pct,
            sensitivity
        )
        if pd.isna(stop_pct):
            continue

        if is_long:
            stop = max(stop, best_close * (1.0 - stop_pct))
            hit_val = close if trigger_on_close else low
            if hit_val <= stop:
                return TrailResult(dt, float(stop), "TrailingSL")
        else:
            stop = min(stop, best_close * (1.0 + stop_pct))
            hit_val = close if trigger_on_close else high
            if hit_val >= stop:
                return TrailResult(dt, float(stop), "TrailingSL")

    return TrailResult(exit_date, orig_exit_px, "OriginalExit")

def improvement(direction: str, new_exit: float, old_exit: float) -> float:
    d = normalize_direction(direction)
    return (new_exit - old_exit) if d == "LONG" else (old_exit - new_exit)

def run_grid():
    raw = pd.read_excel(TRADE_XLSX_PATH)
    trades = build_trade_summary(raw)
    trades = trades[trades["HasAllCoreFields"]].reset_index(drop=True)

    if not RUN_ALL_TRADES:
        trades = trades.sample(n=min(N_SAMPLE_TRADES, len(trades)), random_state=RANDOM_SEED).reset_index(drop=True)

    # Small grid focused on “increase triggers, preserve hit-rate”
    grid = [
        # resample, atr_period, reg_window, atan_thr, atr_mult, max_stop, delay
        ("30T", 20, 20, 0.0020, 4.0, 0.0150, 30),  # baseline (your SME run)
        ("30T", 20, 20, 0.0015, 4.0, 0.0150, 30),  # lower threshold
        ("30T", 14, 16, 0.0015, 4.0, 0.0150, 30),  # faster ATR + shorter window
        ("30T", 14, 16, 0.0015, 3.5, 0.0120, 30),  # tighten fallback
        ("30T", 14, 16, 0.0015, 3.0, 0.0120, 15),  # tighter + less delay
        ("15T", 20, 20, 0.0018, 3.5, 0.0120, 15),  # more bars, moderate
        ("15T", 14, 16, 0.0015, 3.0, 0.0120, 0),   # aggressive trigger booster
    ]

    MIN_STOP_PCT = 0.0010
    SENSITIVITY = 1.0
    TRIGGER_ON_CLOSE = True

    results = []

    # Cache RS data per ticker per (rule, atr_period, delay) to avoid re-reading
    cache = {}

    for (rule, atrp, regw, atan_thr, atr_mult, max_stop, delay) in grid:
        key = (rule, atrp, delay)
        if key not in cache:
            cache[key] = {}
            for tkr in sorted(trades["TickerNorm"].unique()):
                if tkr in M5_TICKERS:
                    cache[key][tkr] = prepare_m5_to_rs_market_only(tkr, rule, atrp, delay)
                else:
                    cache[key][tkr] = None

        out_rows = []
        for tkr, grp in trades.groupby("TickerNorm"):
            rs = cache[key].get(tkr)
            if rs is None or rs.empty:
                continue
            for _, tr in grp.iterrows():
                res = simulate_one_trade(
                    tr, rs,
                    rule, atrp, regw,
                    atan_thr, atr_mult,
                    MIN_STOP_PCT, max_stop,
                    SENSITIVITY, TRIGGER_ON_CLOSE
                )
                old_exit = float(tr["ExitPrice_Original"])
                new_exit = float(res.exit_price)
                impr = improvement(tr["Direction"], new_exit, old_exit)
                out_rows.append({
                    "Triggered": (res.exit_reason == "TrailingSL"),
                    "Improved": (impr > 0),
                    "PctImpact": (impr / old_exit) if old_exit else np.nan
                })

        out = pd.DataFrame(out_rows)
        if out.empty:
            continue

        trig = out["Triggered"].mean()
        trig_impr = out.loc[out["Triggered"], "Improved"].mean() if out["Triggered"].any() else np.nan
        avg_all = out["PctImpact"].mean()
        avg_trig = out.loc[out["Triggered"], "PctImpact"].mean() if out["Triggered"].any() else np.nan

        results.append({
            "RESAMPLE": rule,
            "ATR_PERIOD": atrp,
            "REG_WINDOW": regw,
            "ATAN_THRESHOLD": atan_thr,
            "ATR_FALLBACK_MULT": atr_mult,
            "MAX_STOP_PCT": max_stop,
            "DELAY_MIN": delay,
            "PctTriggered": trig,
            "Triggered_PctImproved": trig_impr,
            "AvgPctImpact_All": avg_all,
            "AvgPctImpact_Triggered": avg_trig
        })

        print("Done config:", results[-1])

    resdf = pd.DataFrame(results).sort_values(
        ["Triggered_PctImproved", "PctTriggered", "AvgPctImpact_All"],
        ascending=[False, False, False]
    )

    out_path = os.path.join(OUT_DIR, "grid_results_step2.csv")
    resdf.to_csv(out_path, index=False)
    print("\nSaved grid:", out_path)
    print(resdf.head(10).to_string(index=False))

if __name__ == "__main__":
    run_grid()


C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: 

Done config: {'RESAMPLE': '30T', 'ATR_PERIOD': 20, 'REG_WINDOW': 20, 'ATAN_THRESHOLD': 0.002, 'ATR_FALLBACK_MULT': 4.0, 'MAX_STOP_PCT': 0.015, 'DELAY_MIN': 30, 'PctTriggered': np.float64(0.21817239592330281), 'Triggered_PctImproved': np.float64(0.6437054631828979), 'AvgPctImpact_All': np.float64(0.0018352410211166911), 'AvgPctImpact_Triggered': np.float64(0.008411884616979035)}
Done config: {'RESAMPLE': '30T', 'ATR_PERIOD': 20, 'REG_WINDOW': 20, 'ATAN_THRESHOLD': 0.0015, 'ATR_FALLBACK_MULT': 4.0, 'MAX_STOP_PCT': 0.015, 'DELAY_MIN': 30, 'PctTriggered': np.float64(0.2404560373121437), 'Triggered_PctImproved': np.float64(0.6724137931034483), 'AvgPctImpact_All': np.float64(0.0021519239886302124), 'AvgPctImpact_Triggered': np.float64(0.008949344806164009)}


C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: 

Done config: {'RESAMPLE': '30T', 'ATR_PERIOD': 14, 'REG_WINDOW': 16, 'ATAN_THRESHOLD': 0.0015, 'ATR_FALLBACK_MULT': 4.0, 'MAX_STOP_PCT': 0.015, 'DELAY_MIN': 30, 'PctTriggered': np.float64(0.26628087752634305), 'Triggered_PctImproved': np.float64(0.6509892961401232), 'AvgPctImpact_All': np.float64(0.002126274558800682), 'AvgPctImpact_Triggered': np.float64(0.007985081687250825)}
Done config: {'RESAMPLE': '30T', 'ATR_PERIOD': 14, 'REG_WINDOW': 16, 'ATAN_THRESHOLD': 0.0015, 'ATR_FALLBACK_MULT': 3.5, 'MAX_STOP_PCT': 0.012, 'DELAY_MIN': 30, 'PctTriggered': np.float64(0.2693038521333564), 'Triggered_PctImproved': np.float64(0.6536241180243746), 'AvgPctImpact_All': np.float64(0.00219119845977207), 'AvgPctImpact_Triggered': np.float64(0.008136528469288334)}


C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: 

Done config: {'RESAMPLE': '30T', 'ATR_PERIOD': 14, 'REG_WINDOW': 16, 'ATAN_THRESHOLD': 0.0015, 'ATR_FALLBACK_MULT': 3.0, 'MAX_STOP_PCT': 0.012, 'DELAY_MIN': 15, 'PctTriggered': np.float64(0.27370875798929), 'Triggered_PctImproved': np.float64(0.652571789207952), 'AvgPctImpact_All': np.float64(0.0021882582925172654), 'AvgPctImpact_Triggered': np.float64(0.007994842067139444)}


C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: 

Done config: {'RESAMPLE': '15T', 'ATR_PERIOD': 20, 'REG_WINDOW': 20, 'ATAN_THRESHOLD': 0.0018, 'ATR_FALLBACK_MULT': 3.5, 'MAX_STOP_PCT': 0.012, 'DELAY_MIN': 15, 'PctTriggered': np.float64(0.5978580065641734), 'Triggered_PctImproved': np.float64(0.5917364923432534), 'AvgPctImpact_All': np.float64(0.002345167540434259), 'AvgPctImpact_Triggered': np.float64(0.003922616264540284)}


C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3737031938.py:115: 

Done config: {'RESAMPLE': '15T', 'ATR_PERIOD': 14, 'REG_WINDOW': 16, 'ATAN_THRESHOLD': 0.0015, 'ATR_FALLBACK_MULT': 3.0, 'MAX_STOP_PCT': 0.012, 'DELAY_MIN': 0, 'PctTriggered': np.float64(0.7418379685610641), 'Triggered_PctImproved': np.float64(0.6133426475724765), 'AvgPctImpact_All': np.float64(0.003157414208616486), 'AvgPctImpact_Triggered': np.float64(0.004256204646333878)}

Saved grid: D:/work/Client/Maatra/Trade Level Data\TrailingSL_CAPPED_MKT1430_2100_SME_GRID_STEP2\grid_results_step2.csv
RESAMPLE  ATR_PERIOD  REG_WINDOW  ATAN_THRESHOLD  ATR_FALLBACK_MULT  MAX_STOP_PCT  DELAY_MIN  PctTriggered  Triggered_PctImproved  AvgPctImpact_All  AvgPctImpact_Triggered
     30T          20          20          0.0015                4.0         0.015         30      0.240456               0.672414          0.002152                0.008949
     30T          14          16          0.0015                3.5         0.012         30      0.269304               0.653624          0.002191         

In [3]:
import os
import numpy as np
import pandas as pd
from dataclasses import dataclass
from datetime import timedelta

# ============================================================
# PATHS (EDIT)
# ============================================================
TRADE_XLSX_PATH      = r"D:/work/Client/Maatra/Trade Level Data/3 Month vol 14 data with sharpe prob Fnl.xlsx"
M5_DIR               = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data"
M5_FILE_LIST_PATH    = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data/m5_file_list.csv"
MAPPING_XLSX_PATH    = r"D:/work/Client/Maatra/Trade Level Data/Instrument Mapping.xlsx"

OUT_DIR = os.path.join(os.path.dirname(TRADE_XLSX_PATH), "TrailingSL_CAPPED_MKT1430_2100_SME_15T_STEP7")
os.makedirs(OUT_DIR, exist_ok=True)

# ============================================================
# RUN MODE
# ============================================================
RUN_ALL_TRADES = True           # full run
N_SAMPLE_TRADES = 6000          # used only if RUN_ALL_TRADES=False
RANDOM_SEED = 42

# ============================================================
# MARKET HOURS (IST)
# ============================================================
MARKET_START = "14:30"
MARKET_END   = "21:00"

# ============================================================
# TRADE TIMING
# ============================================================
APPLY_FROM_NEXT_DAY = True   # entry at EOD; start from next day
TRIGGER_ON_CLOSE = True      # close-based trigger reduces wick noise

# ============================================================
# SME BASELINE (Option 1 chosen)
# ============================================================
BASE_RESAMPLE_RULE = "15T"
BASE_ATR_PERIOD    = 14
BASE_REG_WINDOW    = 16
BASE_ATR_FALLBACK_MULT = 3.0
BASE_MAX_STOP_PCT  = 0.012
BASE_MIN_STOP_PCT  = 0.0010
BASE_SENSITIVITY   = 1.0

# SME “atan threshold” baseline (we will sweep around it)
BASE_ATAN_THRESHOLD = 0.0015

# Delay after open baseline (we will sweep it)
BASE_DELAY_MIN = 0

# ============================================================
# STEP-7 SWEEP (Precision tuning on 15T)
# Goal: keep coverage high, lift hit-rate from ~61% to ~63–66% if possible
# ============================================================
ATAN_THRESHOLDS = [0.0015, 0.0017, 0.0019]
DELAY_MINS      = [0, 15, 30]
MAX_STOP_PCTS   = [0.012, 0.013]    # slightly looser cap can reduce premature stop-outs

# Optional SME knob sweep (keep small first)
SENSITIVITIES   = [0.85, 1.00, 1.15]  # controls aggressiveness of slope+acceleration stop

# ============================================================
# Helpers
# ============================================================

def normalize_ticker(x: str) -> str:
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return ""
    x = str(x).strip().upper()
    return "".join([ch for ch in x if ch.isalnum()])

def trade_base_from_currency(currency: str) -> str:
    if currency is None or (isinstance(currency, float) and np.isnan(currency)):
        return ""
    s = str(currency).strip().upper()
    base = s.split("/")[0].strip() if "/" in s else s
    return normalize_ticker(base)

def normalize_direction(x) -> str:
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return "UNKNOWN"
    s = str(x).strip().upper()
    if s in ["LONG", "BUY", "B", "1", "1.0", "+1", "+1.0"]:
        return "LONG"
    if s in ["SHORT", "SELL", "S", "-1", "-1.0"]:
        return "SHORT"
    try:
        v = float(s)
        if v > 0: return "LONG"
        if v < 0: return "SHORT"
    except Exception:
        pass
    return "UNKNOWN"

def load_trade_to_m5_mapping(mapping_xlsx_path: str) -> dict:
    mp = pd.read_excel(mapping_xlsx_path)
    mp.columns = [c.strip() for c in mp.columns]
    if "org_symbol" not in mp.columns or "Symbol" not in mp.columns:
        raise ValueError("Mapping file must contain columns: org_symbol, Symbol")
    mp["m5_ticker"] = mp["org_symbol"].apply(normalize_ticker)
    mp["trade_base"] = mp["Symbol"].astype(str).str.upper().str.strip().str.split("/").str[0].apply(normalize_ticker)
    mp = mp[(mp["trade_base"] != "") & (mp["m5_ticker"] != "")]
    mp = mp.drop_duplicates(subset=["trade_base"], keep="first")
    return dict(zip(mp["trade_base"], mp["m5_ticker"]))

TRADE_TO_M5 = load_trade_to_m5_mapping(MAPPING_XLSX_PATH)

def map_trade_base_to_m5(trade_base: str) -> str:
    t = normalize_ticker(trade_base)
    return TRADE_TO_M5.get(t, t)

def load_m5_file_map(m5_dir: str, file_list_path: str) -> dict:
    fl = pd.read_csv(file_list_path)
    fl.columns = [c.strip().lower() for c in fl.columns]
    if "ticker" not in fl.columns or "filename" not in fl.columns:
        raise ValueError("m5_file_list.csv must have columns: ticker, filename")
    fl["ticker_norm"] = fl["ticker"].apply(normalize_ticker)
    fl["path"] = fl["filename"].apply(lambda f: os.path.join(m5_dir, f))
    return dict(zip(fl["ticker_norm"], fl["path"]))

M5_MAP = load_m5_file_map(M5_DIR, M5_FILE_LIST_PATH)
M5_TICKERS = set(M5_MAP.keys())

def filter_market_hours(df: pd.DataFrame) -> pd.DataFrame:
    if df.empty:
        return df
    dfi = df.set_index("_dt", drop=False).sort_index()
    dfi = dfi.between_time(MARKET_START, MARKET_END, inclusive="both")
    return dfi.reset_index(drop=True)

def apply_delay_filter(window: pd.DataFrame, delay_minutes: int) -> pd.DataFrame:
    if delay_minutes <= 0 or window.empty:
        return window
    w = window.copy()
    w["d"] = w["_dt"].dt.normalize()
    thr = w["d"] + pd.to_timedelta(MARKET_START + ":00")
    w = w[w["_dt"] >= (thr + pd.to_timedelta(delay_minutes, unit="m"))]
    return w.drop(columns=["d"])

def resample_ohlc(df: pd.DataFrame, rule: str) -> pd.DataFrame:
    if df.empty:
        return df
    dfi = df.set_index("_dt").sort_index()
    ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
        "open": "first",
        "high": "max",
        "low": "min",
        "close": "last",
    }).dropna()
    return ohlc.reset_index()

def compute_atr(df: pd.DataFrame, period: int) -> pd.Series:
    high = df["high"]
    low = df["low"]
    close = df["close"]
    tr = pd.concat([
        high - low,
        (high - close.shift(1)).abs(),
        (low - close.shift(1)).abs()
    ], axis=1).max(axis=1)
    return tr.rolling(period, min_periods=period).mean()

def prepare_m5_to_rs_market_only(ticker: str, resample_rule: str, atr_period: int, delay_mins: int) -> pd.DataFrame | None:
    fp = M5_MAP.get(ticker)
    if not fp or not os.path.exists(fp):
        return None

    df = pd.read_csv(fp)
    df.columns = [c.strip().lower() for c in df.columns]
    needed = ["date", "open", "high", "low", "close"]
    if not all(c in df.columns for c in needed):
        return None

    df["_dt"] = pd.to_datetime(df["date"], errors="coerce")
    df = df.dropna(subset=["_dt"]).sort_values("_dt").reset_index(drop=True)

    for c in ["open", "high", "low", "close"]:
        df[c] = pd.to_numeric(df[c], errors="coerce")
    df = df.dropna(subset=["open", "high", "low", "close"])

    df = filter_market_hours(df)
    if df.empty:
        return None

    rs = resample_ohlc(df, resample_rule)
    if rs.empty:
        return None

    rs = apply_delay_filter(rs, delay_mins)
    if rs.empty:
        return None

    rs["ATR"] = compute_atr(rs, atr_period)
    return rs

def build_trade_summary(raw: pd.DataFrame):
    df = raw.copy()
    df.columns = [c.strip() for c in df.columns]

    required = ["TradeID", "Currency", "Direction", "date", "price", "Closing Date", "DayStatus"]
    missing = [c for c in required if c not in df.columns]
    if missing:
        raise ValueError(f"Trade file missing required columns: {missing}")

    df["date"] = pd.to_datetime(df["date"], errors="coerce")
    df["Closing Date"] = pd.to_datetime(df["Closing Date"], errors="coerce")
    df["price"] = pd.to_numeric(df["price"], errors="coerce")
    df["DayStatusU"] = df["DayStatus"].astype(str).str.upper().str.strip()

    df["TradeBase"] = df["Currency"].apply(trade_base_from_currency)
    df["TickerNorm"] = df["TradeBase"].apply(map_trade_base_to_m5)
    df["DirectionNorm"] = df["Direction"].apply(normalize_direction)

    rows = []
    for tid, g in df.groupby("TradeID", dropna=True):
        g = g.sort_values("date")
        direction = g["DirectionNorm"].dropna().iloc[0] if g["DirectionNorm"].notna().any() else "UNKNOWN"
        ticker = g["TickerNorm"].dropna().iloc[0] if g["TickerNorm"].notna().any() else ""

        open_mask = g["DayStatusU"].eq("OPEN")
        entry_date = g.loc[open_mask, "date"].dropna().min() if open_mask.any() else g["date"].dropna().min()
        exit_date = g["Closing Date"].dropna().max()

        entry_px = np.nan
        if pd.notna(entry_date):
            day = entry_date.normalize()
            day_rows = g[g["date"].dt.normalize() == day]
            if day_rows["price"].notna().any():
                entry_px = float(day_rows["price"].dropna().iloc[-1])

        exit_px = np.nan
        if pd.notna(exit_date):
            day = exit_date.normalize()
            day_rows = g[g["date"].dt.normalize() == day]
            if day_rows["price"].notna().any():
                exit_px = float(day_rows["price"].dropna().iloc[-1])

        has_core = (pd.notna(entry_date) and pd.notna(exit_date) and pd.notna(entry_px) and pd.notna(exit_px)
                    and ticker != "" and (ticker in M5_TICKERS) and direction != "UNKNOWN")

        rows.append({
            "TradeID": tid,
            "Currency": g["Currency"].dropna().iloc[0] if g["Currency"].notna().any() else np.nan,
            "TickerNorm": ticker,
            "Direction": direction,
            "EntryDate": entry_date,
            "ExitDate_Original": exit_date,
            "EntryPrice": entry_px,
            "ExitPrice_Original": exit_px,
            "HasAllCoreFields": has_core
        })
    return pd.DataFrame(rows)

# ============================================================
# SME stop distance (polyfit slope/accel OR ATR% fallback)
# ============================================================

def adaptive_stop_distance_pct(bars: pd.DataFrame,
                              reg_window: int,
                              atan_threshold: float,
                              atr_fallback_mult: float,
                              min_stop_pct: float,
                              max_stop_pct: float,
                              sensitivity: float) -> dict:
    """
    Returns dict with:
      stop_pct: percentage distance (unitless)
      mode: "trend_fit" or "atr_fallback"
      atan_slope, atr_pct, slope_norm, accel
    """
    if len(bars) < max(reg_window, 2) or bars["ATR"].dropna().empty:
        return {"stop_pct": np.nan, "mode": "insufficient", "atan_slope": np.nan, "atr_pct": np.nan,
                "slope_norm": np.nan, "accel": np.nan}

    recent = bars["close"].iloc[-reg_window:].astype(float)
    if len(recent) < reg_window:
        return {"stop_pct": np.nan, "mode": "insufficient", "atan_slope": np.nan, "atr_pct": np.nan,
                "slope_norm": np.nan, "accel": np.nan}

    x = np.arange(len(recent), dtype=float)
    a, b, c = np.polyfit(x, recent.values, 2)

    # SME-style: slope at last point, normalized by price
    slope_norm = (2 * a * x[-1] + b) / recent.iloc[-1]
    accel = (2 * a)
    atan_slope = float(np.arctan(slope_norm))

    atr = float(bars["ATR"].iloc[-1])
    px = float(bars["close"].iloc[-1])
    atr_pct = (atr / px) if (atr > 0 and px > 0) else np.nan

    # trend regime
    if pd.notna(atan_slope) and abs(atan_slope) > atan_threshold:
        stop_pct = abs(slope_norm) * sensitivity * (1.0 + abs(accel))
        stop_pct = float(np.clip(stop_pct, min_stop_pct, max_stop_pct))
        return {"stop_pct": stop_pct, "mode": "trend_fit", "atan_slope": atan_slope, "atr_pct": atr_pct,
                "slope_norm": slope_norm, "accel": accel}

    # range regime fallback
    if pd.isna(atr_pct):
        return {"stop_pct": np.nan, "mode": "atr_missing", "atan_slope": atan_slope, "atr_pct": atr_pct,
                "slope_norm": slope_norm, "accel": accel}

    stop_pct = float(np.clip(atr_pct * atr_fallback_mult, min_stop_pct, max_stop_pct))
    return {"stop_pct": stop_pct, "mode": "atr_fallback", "atan_slope": atan_slope, "atr_pct": atr_pct,
            "slope_norm": slope_norm, "accel": accel}

# ============================================================
# Trailing simulation (CAPPED)
# ============================================================

@dataclass
class TrailResult:
    exit_time: pd.Timestamp
    exit_price: float
    exit_reason: str
    triggered: bool

def improvement(direction: str, new_exit: float, old_exit: float) -> float:
    d = normalize_direction(direction)
    return (new_exit - old_exit) if d == "LONG" else (old_exit - new_exit)

def simulate_trade_sme_capped(tr: pd.Series,
                             rs: pd.DataFrame,
                             reg_window: int,
                             atan_threshold: float,
                             atr_fallback_mult: float,
                             min_stop_pct: float,
                             max_stop_pct: float,
                             sensitivity: float,
                             trigger_on_close: bool,
                             debug: bool=False):
    """
    Chandelier(close) framework:
      LONG: stop = max(stop, best_close * (1 - stop_pct))
      SHORT: stop = min(stop, best_close * (1 + stop_pct))
    stop_pct is adaptive per bar (trend-fit or atr% fallback)
    """
    entry_date = pd.to_datetime(tr["EntryDate"])
    exit_date  = pd.to_datetime(tr["ExitDate_Original"])
    entry_px   = float(tr["EntryPrice"])
    orig_exit_px = float(tr["ExitPrice_Original"])

    direction = normalize_direction(tr["Direction"])
    is_long = (direction == "LONG")

    start_dt = (entry_date + timedelta(days=1)) if APPLY_FROM_NEXT_DAY else entry_date
    end_dt   = exit_date + timedelta(days=1)

    w = rs[(rs["_dt"] >= start_dt) & (rs["_dt"] < end_dt)].copy()
    if w.empty:
        return TrailResult(exit_date, orig_exit_px, "NoRSDataInWindow", False), None

    best_close = entry_px
    stop = -np.inf if is_long else np.inf
    dbg = []

    for i in range(len(w)):
        sub = w.iloc[:i+1]
        row = w.iloc[i]
        dt = row["_dt"]
        close = float(row["close"])
        high = float(row["high"])
        low  = float(row["low"])

        # update best_close
        if is_long:
            best_close = max(best_close, close)
        else:
            best_close = min(best_close, close)

        info = adaptive_stop_distance_pct(
            sub, reg_window, atan_threshold,
            atr_fallback_mult, min_stop_pct, max_stop_pct,
            sensitivity
        )
        stop_pct = info["stop_pct"]
        if pd.isna(stop_pct):
            continue

        if is_long:
            stop = max(stop, best_close * (1.0 - stop_pct))
            hit_val = close if trigger_on_close else low
            if debug:
                dbg.append({"dt": dt, "close": close, "best_close": best_close, "stop": stop, **info})
            if hit_val <= stop:
                return TrailResult(dt, float(stop), "TrailingSL", True), pd.DataFrame(dbg) if debug else None
        else:
            stop = min(stop, best_close * (1.0 + stop_pct))
            hit_val = close if trigger_on_close else high
            if debug:
                dbg.append({"dt": dt, "close": close, "best_close": best_close, "stop": stop, **info})
            if hit_val >= stop:
                return TrailResult(dt, float(stop), "TrailingSL", True), pd.DataFrame(dbg) if debug else None

    return TrailResult(exit_date, orig_exit_px, "OriginalExit", False), pd.DataFrame(dbg) if debug else None

def summarize(trades_out: pd.DataFrame) -> pd.DataFrame:
    df = trades_out.copy()
    df["TriggeredFlag"] = df["ExitReason"].eq("TrailingSL")
    df["ImprovedFlag"] = df["PriceImprovement"] > 0
    df["WorseFlag"] = df["PriceImprovement"] < 0
    df["UnchangedFlag"] = (df["PriceImprovement"] == 0) | df["PriceImprovement"].isna()

    def agg(g):
        n = len(g)
        trig = int(g["TriggeredFlag"].sum())
        return {
            "Trades": n,
            "TrailingTriggered": trig,
            "PctTriggered": trig / n if n else np.nan,
            "Improved": int(g["ImprovedFlag"].sum()),
            "Worse": int(g["WorseFlag"].sum()),
            "Unchanged": int(g["UnchangedFlag"].sum()),
            "Triggered_PctImproved": float(g.loc[g["TriggeredFlag"], "ImprovedFlag"].mean()) if trig else np.nan,
            "AvgPctImpact_All": float(g["PctImprovement_vs_OriginalExit"].mean(skipna=True)),
            "AvgPctImpact_Triggered": float(g.loc[g["TriggeredFlag"], "PctImprovement_vs_OriginalExit"].mean(skipna=True)) if trig else np.nan,
        }

    rows = [{"Group":"ALL", **agg(df)}]
    for d, g in df.groupby(df["Direction"].astype(str).str.upper().str.strip()):
        rows.append({"Group": f"Direction={d}", **agg(g)})
    return pd.DataFrame(rows)

# ============================================================
# Grid runner
# ============================================================

def run_config(trades: pd.DataFrame,
               resample_rule: str,
               atr_period: int,
               delay_min: int,
               reg_window: int,
               atan_threshold: float,
               atr_fallback_mult: float,
               min_stop_pct: float,
               max_stop_pct: float,
               sensitivity: float,
               trigger_on_close: bool,
               want_trade_output: bool = False):

    # cache RS per ticker for this config
    rs_cache = {}
    for tkr in sorted(trades["TickerNorm"].unique()):
        rs_cache[tkr] = prepare_m5_to_rs_market_only(tkr, resample_rule, atr_period, delay_min)

    out_rows = []
    debug_pick = []

    for tkr, grp in trades.groupby("TickerNorm"):
        rs = rs_cache.get(tkr)
        if rs is None or rs.empty:
            continue

        for _, tr in grp.iterrows():
            debug = (want_trade_output and len(debug_pick) < 20)
            res, dbg = simulate_trade_sme_capped(
                tr, rs,
                reg_window=reg_window,
                atan_threshold=atan_threshold,
                atr_fallback_mult=atr_fallback_mult,
                min_stop_pct=min_stop_pct,
                max_stop_pct=max_stop_pct,
                sensitivity=sensitivity,
                trigger_on_close=trigger_on_close,
                debug=debug
            )

            old_exit = float(tr["ExitPrice_Original"])
            new_exit = float(res.exit_price)
            impr = improvement(tr["Direction"], new_exit, old_exit)

            out_rows.append({
                "TradeID": tr["TradeID"],
                "TickerNorm": tr["TickerNorm"],
                "Direction": tr["Direction"],
                "EntryDate": tr["EntryDate"],
                "EntryPrice": float(tr["EntryPrice"]),
                "ExitDate_Original": tr["ExitDate_Original"],
                "ExitPrice_Original": old_exit,
                "ExitTime_Trailing": res.exit_time,
                "ExitPrice_Trailing": new_exit,
                "ExitReason": res.exit_reason,
                "Triggered": res.triggered,
                "PriceImprovement": impr,
                "PctImprovement_vs_OriginalExit": (impr / old_exit) if old_exit else np.nan,
            })

            if debug and dbg is not None and not dbg.empty:
                dbg = dbg.copy()
                dbg["TradeID"] = tr["TradeID"]
                dbg["TickerNorm"] = tr["TickerNorm"]
                dbg["Direction"] = tr["Direction"]
                debug_pick.append(dbg)

    out_df = pd.DataFrame(out_rows)
    summ_df = summarize(out_df)

    metrics = summ_df.loc[summ_df["Group"]=="ALL"].iloc[0].to_dict()
    metrics.update({
        "RESAMPLE": resample_rule,
        "ATR_PERIOD": atr_period,
        "REG_WINDOW": reg_window,
        "ATAN_THRESHOLD": atan_threshold,
        "ATR_FALLBACK_MULT": atr_fallback_mult,
        "MIN_STOP_PCT": min_stop_pct,
        "MAX_STOP_PCT": max_stop_pct,
        "DELAY_MIN": delay_min,
        "SENSITIVITY": sensitivity,
        "TRIGGER_ON_CLOSE": trigger_on_close
    })

    dbg_df = pd.concat(debug_pick, ignore_index=True) if debug_pick else pd.DataFrame()
    return metrics, out_df, summ_df, dbg_df

def main():
    print("Running SME 15T Step-7 grid...")
    raw = pd.read_excel(TRADE_XLSX_PATH)
    trades = build_trade_summary(raw)
    trades = trades[trades["HasAllCoreFields"]].reset_index(drop=True)

    if not RUN_ALL_TRADES:
        trades = trades.sample(n=min(N_SAMPLE_TRADES, len(trades)), random_state=RANDOM_SEED).reset_index(drop=True)

    print("Trades:", len(trades), "| Unique tickers:", trades["TickerNorm"].nunique())
    print("Base:", BASE_RESAMPLE_RULE, BASE_ATR_PERIOD, BASE_REG_WINDOW, BASE_ATAN_THRESHOLD, BASE_ATR_FALLBACK_MULT, BASE_MAX_STOP_PCT, BASE_DELAY_MIN)

    grid_results = []
    best = None

    # Run grid (small, targeted)
    for atan_thr in ATAN_THRESHOLDS:
        for delay in DELAY_MINS:
            for max_stop in MAX_STOP_PCTS:
                for sens in SENSITIVITIES:
                    metrics, _, _, _ = run_config(
                        trades=trades,
                        resample_rule=BASE_RESAMPLE_RULE,
                        atr_period=BASE_ATR_PERIOD,
                        delay_min=delay,
                        reg_window=BASE_REG_WINDOW,
                        atan_threshold=atan_thr,
                        atr_fallback_mult=BASE_ATR_FALLBACK_MULT,
                        min_stop_pct=BASE_MIN_STOP_PCT,
                        max_stop_pct=max_stop,
                        sensitivity=sens,
                        trigger_on_close=TRIGGER_ON_CLOSE,
                        want_trade_output=False
                    )
                    grid_results.append(metrics)
                    print("Done:", {k: metrics[k] for k in ["ATAN_THRESHOLD","DELAY_MIN","MAX_STOP_PCT","SENSITIVITY","PctTriggered","Triggered_PctImproved","AvgPctImpact_All"]})

    grid_df = pd.DataFrame(grid_results)

    # Choose “best” by: (1) Triggered_PctImproved, (2) PctTriggered, (3) AvgPctImpact_All
    grid_df = grid_df.sort_values(
        ["Triggered_PctImproved", "PctTriggered", "AvgPctImpact_All"],
        ascending=[False, False, False]
    ).reset_index(drop=True)

    grid_path = os.path.join(OUT_DIR, "grid_results_15T_step7.csv")
    grid_df.to_csv(grid_path, index=False)
    print("\nSaved grid:", grid_path)
    print("\nTop 10:")
    print(grid_df.head(10)[["ATAN_THRESHOLD","DELAY_MIN","MAX_STOP_PCT","SENSITIVITY","PctTriggered","Triggered_PctImproved","AvgPctImpact_All","AvgPctImpact_Triggered"]].to_string(index=False))

    # Now run trade-level output for best config
    best_row = grid_df.iloc[0].to_dict()
    best_path = os.path.join(OUT_DIR, "best_config.csv")
    pd.DataFrame([best_row]).to_csv(best_path, index=False)
    print("\nBest config saved:", best_path)

    metrics, out_df, summ_df, dbg_df = run_config(
        trades=trades,
        resample_rule=best_row["RESAMPLE"],
        atr_period=int(best_row["ATR_PERIOD"]),
        delay_min=int(best_row["DELAY_MIN"]),
        reg_window=int(best_row["REG_WINDOW"]),
        atan_threshold=float(best_row["ATAN_THRESHOLD"]),
        atr_fallback_mult=float(best_row["ATR_FALLBACK_MULT"]),
        min_stop_pct=float(best_row["MIN_STOP_PCT"]),
        max_stop_pct=float(best_row["MAX_STOP_PCT"]),
        sensitivity=float(best_row["SENSITIVITY"]),
        trigger_on_close=bool(best_row["TRIGGER_ON_CLOSE"]),
        want_trade_output=True
    )

    out_path = os.path.join(OUT_DIR, "trades_trailing_capped_market_only_sme_15T_best.csv")
    summ_path = os.path.join(OUT_DIR, "summary_trailing_capped_market_only_sme_15T_best.csv")
    dbg_path = os.path.join(OUT_DIR, "debug_samples_best.csv")

    out_df.to_csv(out_path, index=False)
    summ_df.to_csv(summ_path, index=False)
    if not dbg_df.empty:
        dbg_df.to_csv(dbg_path, index=False)

    print("\nSaved best trade output:", out_path)
    print("Saved best summary:", summ_path)
    if not dbg_df.empty:
        print("Saved debug samples:", dbg_path)

    print("\n=== BEST SUMMARY ===")
    print(summ_df.to_string(index=False))

if __name__ == "__main__":
    main()


Running SME 15T Step-7 grid...
Trades: 11578 | Unique tickers: 124
Base: 15T 14 16 0.0015 3.0 0.012 0


C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: Futur

Done: {'ATAN_THRESHOLD': 0.0015, 'DELAY_MIN': 0, 'MAX_STOP_PCT': 0.012, 'SENSITIVITY': 0.85, 'PctTriggered': 0.7436517533252721, 'Triggered_PctImproved': 0.6200929152148664, 'AvgPctImpact_All': 0.0032360594489737977}


C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: Futur

Done: {'ATAN_THRESHOLD': 0.0015, 'DELAY_MIN': 0, 'MAX_STOP_PCT': 0.012, 'SENSITIVITY': 1.0, 'PctTriggered': 0.7418379685610641, 'Triggered_PctImproved': 0.6133426475724765, 'AvgPctImpact_All': 0.003157414208616486}


...

Done: {'ATAN_THRESHOLD': 0.0019, 'DELAY_MIN': 30, 'MAX_STOP_PCT': 0.013, 'SENSITIVITY': 1.0, 'PctTriggered': 0.6963206080497495, 'Triggered_PctImproved': 0.5850905482510543, 'AvgPctImpact_All': 0.0024351679735984586}


C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: Futur

Done: {'ATAN_THRESHOLD': 0.0019, 'DELAY_MIN': 30, 'MAX_STOP_PCT': 0.013, 'SENSITIVITY': 1.15, 'PctTriggered': 0.6943340818794265, 'Triggered_PctImproved': 0.5819131732802587, 'AvgPctImpact_All': 0.0024007586844727075}

Saved grid: D:/work/Client/Maatra/Trade Level Data\TrailingSL_CAPPED_MKT1430_2100_SME_15T_STEP7\grid_results_15T_step7.csv

Top 10:
 ATAN_THRESHOLD  DELAY_MIN  MAX_STOP_PCT  SENSITIVITY  PctTriggered  Triggered_PctImproved  AvgPctImpact_All  AvgPctImpact_Triggered
         0.0015         15         0.012         0.85      0.731646               0.624956          0.003123                0.004269
         0.0015         15         0.013         0.85      0.731560               0.624675          0.003098                0.004235
         0.0015         30         0.012         0.85      0.719986               0.624160          0.002971                0.004126
         0.0015         30         0.013         0.85      0.719900               0.622795          0.002941         

C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\832953786.py:147: Futur


Saved best trade output: D:/work/Client/Maatra/Trade Level Data\TrailingSL_CAPPED_MKT1430_2100_SME_15T_STEP7\trades_trailing_capped_market_only_sme_15T_best.csv
Saved best summary: D:/work/Client/Maatra/Trade Level Data\TrailingSL_CAPPED_MKT1430_2100_SME_15T_STEP7\summary_trailing_capped_market_only_sme_15T_best.csv
Saved debug samples: D:/work/Client/Maatra/Trade Level Data\TrailingSL_CAPPED_MKT1430_2100_SME_15T_STEP7\debug_samples_best.csv

=== BEST SUMMARY ===
          Group  Trades  TrailingTriggered  PctTriggered  Improved  Worse  Unchanged  Triggered_PctImproved  AvgPctImpact_All  AvgPctImpact_Triggered
            ALL   11578               8471      0.731646      5294   3177       3107               0.624956          0.003123                0.004269
 Direction=LONG   10922               7959      0.728713      4963   2996       2963               0.623571          0.003171                0.004351
Direction=SHORT     656                512      0.780488       331    181        

In [ ]:
### step 8 

In [4]:
import os
import numpy as np
import pandas as pd
from dataclasses import dataclass
from datetime import timedelta

# ============================================================
# PATHS (EDIT)
# ============================================================
TRADE_XLSX_PATH      = r"D:/work/Client/Maatra/Trade Level Data/3 Month vol 14 data with sharpe prob Fnl.xlsx"
M5_DIR               = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data"
M5_FILE_LIST_PATH    = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data/m5_file_list.csv"
MAPPING_XLSX_PATH    = r"D:/work/Client/Maatra/Trade Level Data/Instrument Mapping.xlsx"

OUT_DIR = os.path.join(os.path.dirname(TRADE_XLSX_PATH), "TrailingSL_CAPPED_MKT1430_2100_SME_15T_STEP8_DIRSPEC")
os.makedirs(OUT_DIR, exist_ok=True)

# ============================================================
# RUN MODE
# ============================================================
RUN_ALL_TRADES = True
N_SAMPLE_TRADES = 8000        # used only if RUN_ALL_TRADES=False
RANDOM_SEED = 42

# ============================================================
# MARKET HOURS (IST)
# ============================================================
MARKET_START = "14:30"
MARKET_END   = "21:00"

# ============================================================
# CORE MODEL (LOCKED to Step-7 Baseline)
# ============================================================
RESAMPLE_RULE = "15T"
ATR_PERIOD    = 14
REG_WINDOW    = 16
DELAY_MIN     = 0

APPLY_FROM_NEXT_DAY = True
TRIGGER_ON_CLOSE = True

ATR_FALLBACK_MULT = 3.0
MIN_STOP_PCT = 0.0010
SENSITIVITY  = 1.0

# ============================================================
# STEP-8 GRID (Direction-specific knobs)
# Tune only these:
# ============================================================
ATAN_LONG_GRID  = [0.0015, 0.0017, 0.0019]
ATAN_SHORT_GRID = [0.0013, 0.0015, 0.0017]  # often shorts like slightly diff threshold

MAX_STOP_LONG_GRID  = [0.012, 0.013]
MAX_STOP_SHORT_GRID = [0.012, 0.013]

# If runtime is too high, reduce grids above.

# ============================================================
# Helpers
# ============================================================

def normalize_ticker(x: str) -> str:
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return ""
    x = str(x).strip().upper()
    return "".join([ch for ch in x if ch.isalnum()])

def trade_base_from_currency(currency: str) -> str:
    if currency is None or (isinstance(currency, float) and np.isnan(currency)):
        return ""
    s = str(currency).strip().upper()
    base = s.split("/")[0].strip() if "/" in s else s
    return normalize_ticker(base)

def normalize_direction(x) -> str:
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return "UNKNOWN"
    s = str(x).strip().upper()
    if s in ["LONG", "BUY", "B", "1", "1.0", "+1", "+1.0"]:
        return "LONG"
    if s in ["SHORT", "SELL", "S", "-1", "-1.0"]:
        return "SHORT"
    try:
        v = float(s)
        if v > 0: return "LONG"
        if v < 0: return "SHORT"
    except Exception:
        pass
    return "UNKNOWN"

def load_trade_to_m5_mapping(mapping_xlsx_path: str) -> dict:
    mp = pd.read_excel(mapping_xlsx_path)
    mp.columns = [c.strip() for c in mp.columns]
    if "org_symbol" not in mp.columns or "Symbol" not in mp.columns:
        raise ValueError("Mapping file must contain columns: org_symbol, Symbol")
    mp["m5_ticker"] = mp["org_symbol"].apply(normalize_ticker)
    mp["trade_base"] = mp["Symbol"].astype(str).str.upper().str.strip().str.split("/").str[0].apply(normalize_ticker)
    mp = mp[(mp["trade_base"] != "") & (mp["m5_ticker"] != "")]
    mp = mp.drop_duplicates(subset=["trade_base"], keep="first")
    return dict(zip(mp["trade_base"], mp["m5_ticker"]))

TRADE_TO_M5 = load_trade_to_m5_mapping(MAPPING_XLSX_PATH)

def map_trade_base_to_m5(trade_base: str) -> str:
    t = normalize_ticker(trade_base)
    return TRADE_TO_M5.get(t, t)

def load_m5_file_map(m5_dir: str, file_list_path: str) -> dict:
    fl = pd.read_csv(file_list_path)
    fl.columns = [c.strip().lower() for c in fl.columns]
    if "ticker" not in fl.columns or "filename" not in fl.columns:
        raise ValueError("m5_file_list.csv must have columns: ticker, filename")
    fl["ticker_norm"] = fl["ticker"].apply(normalize_ticker)
    fl["path"] = fl["filename"].apply(lambda f: os.path.join(m5_dir, f))
    return dict(zip(fl["ticker_norm"], fl["path"]))

M5_MAP = load_m5_file_map(M5_DIR, M5_FILE_LIST_PATH)
M5_TICKERS = set(M5_MAP.keys())

def filter_market_hours(df: pd.DataFrame) -> pd.DataFrame:
    if df.empty:
        return df
    dfi = df.set_index("_dt", drop=False).sort_index()
    dfi = dfi.between_time(MARKET_START, MARKET_END, inclusive="both")
    return dfi.reset_index(drop=True)

def apply_delay_filter(window: pd.DataFrame, delay_minutes: int) -> pd.DataFrame:
    if delay_minutes <= 0 or window.empty:
        return window
    w = window.copy()
    w["d"] = w["_dt"].dt.normalize()
    thr = w["d"] + pd.to_timedelta(MARKET_START + ":00")
    w = w[w["_dt"] >= (thr + pd.to_timedelta(delay_minutes, unit="m"))]
    return w.drop(columns=["d"])

def resample_ohlc(df: pd.DataFrame, rule: str) -> pd.DataFrame:
    if df.empty:
        return df
    dfi = df.set_index("_dt").sort_index()
    ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
        "open": "first",
        "high": "max",
        "low": "min",
        "close": "last",
    }).dropna()
    return ohlc.reset_index()

def compute_atr(df: pd.DataFrame, period: int) -> pd.Series:
    high = df["high"]
    low = df["low"]
    close = df["close"]
    tr = pd.concat([
        high - low,
        (high - close.shift(1)).abs(),
        (low - close.shift(1)).abs()
    ], axis=1).max(axis=1)
    return tr.rolling(period, min_periods=period).mean()

def prepare_rs_for_ticker(ticker: str) -> pd.DataFrame | None:
    fp = M5_MAP.get(ticker)
    if not fp or not os.path.exists(fp):
        return None

    df = pd.read_csv(fp)
    df.columns = [c.strip().lower() for c in df.columns]
    needed = ["date", "open", "high", "low", "close"]
    if not all(c in df.columns for c in needed):
        return None

    df["_dt"] = pd.to_datetime(df["date"], errors="coerce")
    df = df.dropna(subset=["_dt"]).sort_values("_dt").reset_index(drop=True)

    for c in ["open", "high", "low", "close"]:
        df[c] = pd.to_numeric(df[c], errors="coerce")
    df = df.dropna(subset=["open", "high", "low", "close"])

    df = filter_market_hours(df)
    if df.empty:
        return None

    rs = resample_ohlc(df, RESAMPLE_RULE)
    if rs.empty:
        return None

    rs = apply_delay_filter(rs, DELAY_MIN)
    if rs.empty:
        return None

    rs["ATR"] = compute_atr(rs, ATR_PERIOD)
    return rs

def build_trade_summary(raw: pd.DataFrame):
    df = raw.copy()
    df.columns = [c.strip() for c in df.columns]

    required = ["TradeID", "Currency", "Direction", "date", "price", "Closing Date", "DayStatus"]
    missing = [c for c in required if c not in df.columns]
    if missing:
        raise ValueError(f"Trade file missing required columns: {missing}")

    df["date"] = pd.to_datetime(df["date"], errors="coerce")
    df["Closing Date"] = pd.to_datetime(df["Closing Date"], errors="coerce")
    df["price"] = pd.to_numeric(df["price"], errors="coerce")
    df["DayStatusU"] = df["DayStatus"].astype(str).str.upper().str.strip()

    df["TradeBase"] = df["Currency"].apply(trade_base_from_currency)
    df["TickerNorm"] = df["TradeBase"].apply(map_trade_base_to_m5)
    df["DirectionNorm"] = df["Direction"].apply(normalize_direction)

    rows = []
    for tid, g in df.groupby("TradeID", dropna=True):
        g = g.sort_values("date")
        direction = g["DirectionNorm"].dropna().iloc[0] if g["DirectionNorm"].notna().any() else "UNKNOWN"
        ticker = g["TickerNorm"].dropna().iloc[0] if g["TickerNorm"].notna().any() else ""

        open_mask = g["DayStatusU"].eq("OPEN")
        entry_date = g.loc[open_mask, "date"].dropna().min() if open_mask.any() else g["date"].dropna().min()
        exit_date = g["Closing Date"].dropna().max()

        entry_px = np.nan
        if pd.notna(entry_date):
            day = entry_date.normalize()
            day_rows = g[g["date"].dt.normalize() == day]
            if day_rows["price"].notna().any():
                entry_px = float(day_rows["price"].dropna().iloc[-1])

        exit_px = np.nan
        if pd.notna(exit_date):
            day = exit_date.normalize()
            day_rows = g[g["date"].dt.normalize() == day]
            if day_rows["price"].notna().any():
                exit_px = float(day_rows["price"].dropna().iloc[-1])

        has_core = (pd.notna(entry_date) and pd.notna(exit_date) and pd.notna(entry_px) and pd.notna(exit_px)
                    and ticker != "" and (ticker in M5_TICKERS) and direction != "UNKNOWN")

        rows.append({
            "TradeID": tid,
            "TickerNorm": ticker,
            "Direction": direction,
            "EntryDate": entry_date,
            "ExitDate_Original": exit_date,
            "EntryPrice": entry_px,
            "ExitPrice_Original": exit_px,
            "HasAllCoreFields": has_core
        })
    return pd.DataFrame(rows)

# ============================================================
# SME adaptive stop distance
# ============================================================

def adaptive_stop_distance_pct(bars: pd.DataFrame,
                              atan_threshold: float,
                              atr_fallback_mult: float,
                              min_stop_pct: float,
                              max_stop_pct: float,
                              sensitivity: float) -> float:
    if len(bars) < REG_WINDOW or bars["ATR"].dropna().empty:
        return np.nan

    recent = bars["close"].iloc[-REG_WINDOW:].astype(float)
    if len(recent) < REG_WINDOW:
        return np.nan

    x = np.arange(len(recent), dtype=float)
    a, b, c = np.polyfit(x, recent.values, 2)

    slope_norm = (2 * a * x[-1] + b) / recent.iloc[-1]
    accel = (2 * a)
    atan_slope = float(np.arctan(slope_norm))

    atr = bars["ATR"].iloc[-1]
    px = bars["close"].iloc[-1]
    atr_pct = float(atr / px) if (pd.notna(atr) and atr > 0 and px > 0) else np.nan
    if pd.isna(atr_pct):
        return np.nan

    if abs(atan_slope) > atan_threshold:
        stop_pct = abs(slope_norm) * sensitivity * (1.0 + abs(accel))
        return float(np.clip(stop_pct, min_stop_pct, max_stop_pct))

    stop_pct = atr_pct * atr_fallback_mult
    return float(np.clip(stop_pct, min_stop_pct, max_stop_pct))

@dataclass
class TrailResult:
    exit_time: pd.Timestamp
    exit_price: float
    exit_reason: str
    triggered: bool

def improvement(direction: str, new_exit: float, old_exit: float) -> float:
    d = normalize_direction(direction)
    return (new_exit - old_exit) if d == "LONG" else (old_exit - new_exit)

def simulate_trade(tr: pd.Series,
                   rs: pd.DataFrame,
                   atan_long: float,
                   atan_short: float,
                   max_stop_long: float,
                   max_stop_short: float,
                   debug: bool=False):
    entry_date = pd.to_datetime(tr["EntryDate"])
    exit_date  = pd.to_datetime(tr["ExitDate_Original"])
    entry_px   = float(tr["EntryPrice"])
    orig_exit_px = float(tr["ExitPrice_Original"])

    direction = normalize_direction(tr["Direction"])
    is_long = (direction == "LONG")

    atan_thr = atan_long if is_long else atan_short
    max_stop = max_stop_long if is_long else max_stop_short

    start_dt = (entry_date + timedelta(days=1)) if APPLY_FROM_NEXT_DAY else entry_date
    end_dt   = exit_date + timedelta(days=1)

    w = rs[(rs["_dt"] >= start_dt) & (rs["_dt"] < end_dt)].copy()
    if w.empty:
        return TrailResult(exit_date, orig_exit_px, "NoRSDataInWindow", False), None

    best_close = entry_px
    stop = -np.inf if is_long else np.inf
    dbg = []

    for i in range(len(w)):
        sub = w.iloc[:i+1]
        row = w.iloc[i]
        dt = row["_dt"]

        close = float(row["close"])
        high = float(row["high"])
        low  = float(row["low"])

        if is_long:
            best_close = max(best_close, close)
        else:
            best_close = min(best_close, close)

        stop_pct = adaptive_stop_distance_pct(
            sub,
            atan_threshold=atan_thr,
            atr_fallback_mult=ATR_FALLBACK_MULT,
            min_stop_pct=MIN_STOP_PCT,
            max_stop_pct=max_stop,
            sensitivity=SENSITIVITY
        )
        if pd.isna(stop_pct):
            continue

        if is_long:
            stop = max(stop, best_close * (1.0 - stop_pct))
            hit_val = close if TRIGGER_ON_CLOSE else low
            if debug:
                dbg.append({"dt": dt, "close": close, "best_close": best_close, "stop": stop,
                            "atan_thr": atan_thr, "max_stop": max_stop, "stop_pct": stop_pct})
            if hit_val <= stop:
                return TrailResult(dt, float(stop), "TrailingSL", True), pd.DataFrame(dbg) if debug else None
        else:
            stop = min(stop, best_close * (1.0 + stop_pct))
            hit_val = close if TRIGGER_ON_CLOSE else high
            if debug:
                dbg.append({"dt": dt, "close": close, "best_close": best_close, "stop": stop,
                            "atan_thr": atan_thr, "max_stop": max_stop, "stop_pct": stop_pct})
            if hit_val >= stop:
                return TrailResult(dt, float(stop), "TrailingSL", True), pd.DataFrame(dbg) if debug else None

    return TrailResult(exit_date, orig_exit_px, "OriginalExit", False), pd.DataFrame(dbg) if debug else None

def summarize(out: pd.DataFrame) -> pd.DataFrame:
    df = out.copy()
    df["TriggeredFlag"] = df["ExitReason"].eq("TrailingSL")
    df["ImprovedFlag"] = df["PriceImprovement"] > 0
    df["WorseFlag"] = df["PriceImprovement"] < 0
    df["UnchangedFlag"] = (df["PriceImprovement"] == 0) | df["PriceImprovement"].isna()

    def agg(g):
        n = len(g)
        trig = int(g["TriggeredFlag"].sum())
        return {
            "Trades": n,
            "TrailingTriggered": trig,
            "PctTriggered": trig / n if n else np.nan,
            "Improved": int(g["ImprovedFlag"].sum()),
            "Worse": int(g["WorseFlag"].sum()),
            "Unchanged": int(g["UnchangedFlag"].sum()),
            "Triggered_PctImproved": float(g.loc[g["TriggeredFlag"], "ImprovedFlag"].mean()) if trig else np.nan,
            "AvgPctImpact_All": float(g["PctImprovement_vs_OriginalExit"].mean(skipna=True)),
            "AvgPctImpact_Triggered": float(g.loc[g["TriggeredFlag"], "PctImprovement_vs_OriginalExit"].mean(skipna=True)) if trig else np.nan,
        }

    rows = [{"Group":"ALL", **agg(df)}]
    for d, g in df.groupby(df["Direction"].astype(str).str.upper().str.strip()):
        rows.append({"Group": f"Direction={d}", **agg(g)})
    return pd.DataFrame(rows)

def main():
    print("STEP-8 Direction-specific calibration | 15T | CAPPED | Market-only")
    raw = pd.read_excel(TRADE_XLSX_PATH)
    trades = build_trade_summary(raw)
    trades = trades[trades["HasAllCoreFields"]].reset_index(drop=True)

    if not RUN_ALL_TRADES:
        trades = trades.sample(n=min(N_SAMPLE_TRADES, len(trades)), random_state=RANDOM_SEED).reset_index(drop=True)

    print("Trades:", len(trades), "| Tickers:", trades["TickerNorm"].nunique())

    # cache RS once
    rs_cache = {}
    for tkr in sorted(trades["TickerNorm"].unique()):
        rs_cache[tkr] = prepare_rs_for_ticker(tkr)

    grid_rows = []

    for atanL in ATAN_LONG_GRID:
        for atanS in ATAN_SHORT_GRID:
            for maxL in MAX_STOP_LONG_GRID:
                for maxS in MAX_STOP_SHORT_GRID:

                    out_rows = []
                    for tkr, grp in trades.groupby("TickerNorm"):
                        rs = rs_cache.get(tkr)
                        if rs is None or rs.empty:
                            continue
                        for _, tr in grp.iterrows():
                            res, _ = simulate_trade(tr, rs, atanL, atanS, maxL, maxS, debug=False)
                            old_exit = float(tr["ExitPrice_Original"])
                            new_exit = float(res.exit_price)
                            impr = improvement(tr["Direction"], new_exit, old_exit)
                            out_rows.append({
                                "Triggered": (res.exit_reason == "TrailingSL"),
                                "Improved": (impr > 0),
                                "PctImpact": (impr / old_exit) if old_exit else np.nan
                            })

                    tmp = pd.DataFrame(out_rows)
                    if tmp.empty:
                        continue

                    pct_trig = tmp["Triggered"].mean()
                    trig_hit = tmp.loc[tmp["Triggered"], "Improved"].mean() if tmp["Triggered"].any() else np.nan
                    avg_all  = tmp["PctImpact"].mean()
                    avg_trig = tmp.loc[tmp["Triggered"], "PctImpact"].mean() if tmp["Triggered"].any() else np.nan

                    grid_rows.append({
                        "ATAN_LONG": atanL,
                        "ATAN_SHORT": atanS,
                        "MAX_STOP_LONG": maxL,
                        "MAX_STOP_SHORT": maxS,
                        "PctTriggered": pct_trig,
                        "Triggered_PctImproved": trig_hit,
                        "AvgPctImpact_All": avg_all,
                        "AvgPctImpact_Triggered": avg_trig
                    })

                    print("Done:", {"ATAN_LONG":atanL,"ATAN_SHORT":atanS,"MAXL":maxL,"MAXS":maxS,
                                  "PctTrig":round(pct_trig,4),
                                  "TrigHit":round(float(trig_hit),4) if pd.notna(trig_hit) else None,
                                  "AvgAll":round(avg_all,6)})

    grid_df = pd.DataFrame(grid_rows).sort_values(
        ["Triggered_PctImproved","PctTriggered","AvgPctImpact_All"],
        ascending=[False, False, False]
    ).reset_index(drop=True)

    grid_path = os.path.join(OUT_DIR, "grid_step8_dir_specific.csv")
    grid_df.to_csv(grid_path, index=False)
    print("\nSaved grid:", grid_path)
    print("\nTop 10:")
    print(grid_df.head(10).to_string(index=False))

    best = grid_df.iloc[0].to_dict()
    pd.DataFrame([best]).to_csv(os.path.join(OUT_DIR, "best_config_step8.csv"), index=False)

    # full trade-level output for best
    out_rows = []
    debug_pick = []

    for tkr, grp in trades.groupby("TickerNorm"):
        rs = rs_cache.get(tkr)
        if rs is None or rs.empty:
            continue
        for _, tr in grp.iterrows():
            want_dbg = len(debug_pick) < 20
            res, dbg = simulate_trade(tr, rs,
                                      best["ATAN_LONG"], best["ATAN_SHORT"],
                                      best["MAX_STOP_LONG"], best["MAX_STOP_SHORT"],
                                      debug=want_dbg)

            old_exit = float(tr["ExitPrice_Original"])
            new_exit = float(res.exit_price)
            impr = improvement(tr["Direction"], new_exit, old_exit)

            out_rows.append({
                "TradeID": tr["TradeID"],
                "TickerNorm": tr["TickerNorm"],
                "Direction": tr["Direction"],
                "EntryDate": tr["EntryDate"],
                "EntryPrice": float(tr["EntryPrice"]),
                "ExitDate_Original": tr["ExitDate_Original"],
                "ExitPrice_Original": old_exit,
                "ExitTime_Trailing": res.exit_time,
                "ExitPrice_Trailing": new_exit,
                "ExitReason": res.exit_reason,
                "PriceImprovement": impr,
                "PctImprovement_vs_OriginalExit": (impr / old_exit) if old_exit else np.nan,
            })

            if want_dbg and dbg is not None and not dbg.empty:
                dbg = dbg.copy()
                dbg["TradeID"] = tr["TradeID"]
                dbg["TickerNorm"] = tr["TickerNorm"]
                dbg["Direction"] = tr["Direction"]
                debug_pick.append(dbg)

    out_df = pd.DataFrame(out_rows)
    summ_df = summarize(out_df)

    out_path = os.path.join(OUT_DIR, "trades_step8_best.csv")
    summ_path = os.path.join(OUT_DIR, "summary_step8_best.csv")
    dbg_path = os.path.join(OUT_DIR, "debug_step8_best_samples.csv")

    out_df.to_csv(out_path, index=False)
    summ_df.to_csv(summ_path, index=False)
    if debug_pick:
        pd.concat(debug_pick, ignore_index=True).to_csv(dbg_path, index=False)

    print("\nSaved best trade output:", out_path)
    print("Saved best summary:", summ_path)
    if debug_pick:
        print("Saved debug:", dbg_path)

    print("\n=== BEST SUMMARY (STEP 8) ===")
    print(summ_df.to_string(index=False))

if __name__ == "__main__":
    main()


STEP-8 Direction-specific calibration | 15T | CAPPED | Market-only
Trades: 11578 | Tickers: 124


C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3653308635.py:140: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3653308635.py:140: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3653308635.py:140: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3653308635.py:140: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_3488\3653308635.py:140: 

Done: {'ATAN_LONG': 0.0015, 'ATAN_SHORT': 0.0013, 'MAXL': 0.012, 'MAXS': 0.012, 'PctTrig': np.float64(0.7421), 'TrigHit': 0.6137, 'AvgAll': np.float64(0.003163)}
Done: {'ATAN_LONG': 0.0015, 'ATAN_SHORT': 0.0013, 'MAXL': 0.012, 'MAXS': 0.013, 'PctTrig': np.float64(0.7421), 'TrigHit': 0.6137, 'AvgAll': np.float64(0.003162)}
Done: {'ATAN_LONG': 0.0015, 'ATAN_SHORT': 0.0013, 'MAXL': 0.013, 'MAXS': 0.012, 'PctTrig': np.float64(0.742), 'TrigHit': 0.6132, 'AvgAll': np.float64(0.003138)}
Done: {'ATAN_LONG': 0.0015, 'ATAN_SHORT': 0.0013, 'MAXL': 0.013, 'MAXS': 0.013, 'PctTrig': np.float64(0.742), 'TrigHit': 0.6132, 'AvgAll': np.float64(0.003137)}
Done: {'ATAN_LONG': 0.0015, 'ATAN_SHORT': 0.0015, 'MAXL': 0.012, 'MAXS': 0.012, 'PctTrig': np.float64(0.7418), 'TrigHit': 0.6133, 'AvgAll': np.float64(0.003157)}
Done: {'ATAN_LONG': 0.0015, 'ATAN_SHORT': 0.0015, 'MAXL': 0.012, 'MAXS': 0.013, 'PctTrig': np.float64(0.7418), 'TrigHit': 0.6133, 'AvgAll': np.float64(0.003156)}
Done: {'ATAN_LONG': 0.0015, 'A

In [ ]:
step 9 

In [4]:
import os
import numpy as np
import pandas as pd
from dataclasses import dataclass
from datetime import timedelta

# ============================================================
# CONFIG (EDIT THESE PATHS)
# ============================================================

TRADE_CSV_PATH = r"D:/work/Client/Maatra/Trade Level Data/Equities 14 vol trade data (Jan 2021 to Nov 2025).csv"

M5_DIR            = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data"
M5_FILE_LIST_PATH = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data/m5_file_list.csv"
MAPPING_XLSX_PATH = r"D:/work/Client/Maatra/Trade Level Data/Instrument Mapping.xlsx"

# Step 8 base params (dir-specific)
STEP8_DIR = r"D:/work/Client/Maatra/Trade Level Data/TrailingSL_CAPPED_MKT1430_2100_SME_15T_STEP8_DIRSPEC"
BEST_STEP8_PATH = os.path.join(STEP8_DIR, "best_config_step8.csv")

# Step 9 sensitivity
STEP9_DIR = r"D:/work/Client/Maatra/Trade Level Data/TrailingSL_CAPPED_MKT1430_2100_SME_15T_STEP9_SENSITIVITY"
BEST_STEP9_PATH = os.path.join(STEP9_DIR, "best_config_step9.csv")

YEAR_FILTER = 2025

OUT_DIR = os.path.join(os.path.dirname(TRADE_CSV_PATH), f"TrailingSL_OOS_{YEAR_FILTER}_FULLYEAR_STEP8STEP9_NEXTDAY_ONLY")
os.makedirs(OUT_DIR, exist_ok=True)

# ============================================================
# Locked settings (same as pilot)
# ============================================================
MARKET_START = "14:30"
MARKET_END   = "21:00"
RESAMPLE_RULE = "15T"

ATR_PERIOD = 14
REG_WINDOW = 16
DELAY_MIN = 0

TRIGGER_ON_CLOSE = True
ATR_FALLBACK_MULT = 3.0
MIN_STOP_PCT = 0.0010

# YOUR RULE
APPLY_FROM_NEXT_DAY_ONLY = True

# Progress printing frequency
PRINT_EVERY = 500

# ============================================================
# Robust CSV reader
# ============================================================
def read_trade_csv(path: str) -> pd.DataFrame:
    for enc in ["utf-8", "cp1252", "latin1"]:
        try:
            return pd.read_csv(path, encoding=enc, low_memory=False)
        except UnicodeDecodeError:
            continue
    return pd.read_csv(path, encoding="utf-8", encoding_errors="ignore", low_memory=False)

# ============================================================
# Helpers
# ============================================================
def normalize_ticker(x: str) -> str:
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return ""
    x = str(x).strip().upper()
    return "".join([ch for ch in x if ch.isalnum()])

def trade_base_from_currency(currency: str) -> str:
    if currency is None or (isinstance(currency, float) and np.isnan(currency)):
        return ""
    s = str(currency).strip().upper()
    base = s.split("/")[0].strip() if "/" in s else s
    return normalize_ticker(base)

def normalize_direction(x) -> str:
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return "UNKNOWN"
    s = str(x).strip().upper()
    if s in ["LONG", "BUY", "B", "1", "1.0", "+1", "+1.0"]:
        return "LONG"
    if s in ["SHORT", "SELL", "S", "-1", "-1.0"]:
        return "SHORT"
    try:
        v = float(s)
        if v > 0: return "LONG"
        if v < 0: return "SHORT"
    except Exception:
        pass
    return "UNKNOWN"

# ============================================================
# Load mapping file
# ============================================================
def load_trade_to_m5_mapping(mapping_xlsx_path: str) -> dict:
    mp = pd.read_excel(mapping_xlsx_path)
    mp.columns = [c.strip() for c in mp.columns]
    if "org_symbol" not in mp.columns or "Symbol" not in mp.columns:
        raise ValueError("Mapping file must contain columns: org_symbol, Symbol")
    mp["m5_ticker"] = mp["org_symbol"].apply(normalize_ticker)
    mp["trade_base"] = mp["Symbol"].astype(str).str.upper().str.strip().str.split("/").str[0].apply(normalize_ticker)
    mp = mp[(mp["trade_base"] != "") & (mp["m5_ticker"] != "")]
    mp = mp.drop_duplicates(subset=["trade_base"], keep="first")
    return dict(zip(mp["trade_base"], mp["m5_ticker"]))

TRADE_TO_M5 = load_trade_to_m5_mapping(MAPPING_XLSX_PATH)

def map_trade_base_to_m5(trade_base: str) -> str:
    t = normalize_ticker(trade_base)
    return TRADE_TO_M5.get(t, t)

# ============================================================
# Load M5 file list
# ============================================================
def load_m5_file_map(m5_dir: str, file_list_path: str) -> dict:
    fl = pd.read_csv(file_list_path)
    fl.columns = [c.strip().lower() for c in fl.columns]
    if "ticker" not in fl.columns or "filename" not in fl.columns:
        raise ValueError("m5_file_list.csv must have columns: ticker, filename")
    fl["ticker_norm"] = fl["ticker"].apply(normalize_ticker)
    fl["path"] = fl["filename"].apply(lambda f: os.path.join(m5_dir, f))
    return dict(zip(fl["ticker_norm"], fl["path"]))

M5_MAP = load_m5_file_map(M5_DIR, M5_FILE_LIST_PATH)
M5_TICKERS = set(M5_MAP.keys())

# ============================================================
# M5 preparation (market hours + resample + ATR) with caching
# ============================================================
def filter_market_hours(df: pd.DataFrame) -> pd.DataFrame:
    if df.empty:
        return df
    dfi = df.set_index("_dt", drop=False).sort_index()
    dfi = dfi.between_time(MARKET_START, MARKET_END, inclusive="both")
    return dfi.reset_index(drop=True)

def apply_delay_filter(window: pd.DataFrame, delay_minutes: int) -> pd.DataFrame:
    if delay_minutes <= 0 or window.empty:
        return window
    w = window.copy()
    w["d"] = w["_dt"].dt.normalize()
    thr = w["d"] + pd.to_timedelta(MARKET_START + ":00")
    w = w[w["_dt"] >= (thr + pd.to_timedelta(delay_minutes, unit="m"))]
    return w.drop(columns=["d"])

def resample_ohlc(df: pd.DataFrame, rule: str) -> pd.DataFrame:
    if df.empty:
        return df
    dfi = df.set_index("_dt").sort_index()
    ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
        "open": "first",
        "high": "max",
        "low": "min",
        "close": "last",
    }).dropna()
    return ohlc.reset_index()

def compute_atr(df: pd.DataFrame, period: int) -> pd.Series:
    high = df["high"]
    low = df["low"]
    close = df["close"]
    tr = pd.concat([
        high - low,
        (high - close.shift(1)).abs(),
        (low - close.shift(1)).abs()
    ], axis=1).max(axis=1)
    return tr.rolling(period, min_periods=period).mean()

_RS_CACHE = {}

def prepare_rs_for_ticker(ticker: str) -> pd.DataFrame | None:
    if ticker in _RS_CACHE:
        return _RS_CACHE[ticker]

    fp = M5_MAP.get(ticker)
    if not fp or not os.path.exists(fp):
        _RS_CACHE[ticker] = None
        return None

    df = pd.read_csv(fp)
    df.columns = [c.strip().lower() for c in df.columns]
    needed = ["date", "open", "high", "low", "close"]
    if not all(c in df.columns for c in needed):
        _RS_CACHE[ticker] = None
        return None

    df["_dt"] = pd.to_datetime(df["date"], errors="coerce")
    df = df.dropna(subset=["_dt"]).sort_values("_dt").reset_index(drop=True)

    for c in ["open", "high", "low", "close"]:
        df[c] = pd.to_numeric(df[c], errors="coerce")
    df = df.dropna(subset=["open", "high", "low", "close"])

    df = filter_market_hours(df)
    if df.empty:
        _RS_CACHE[ticker] = None
        return None

    rs = resample_ohlc(df, RESAMPLE_RULE)
    if rs.empty:
        _RS_CACHE[ticker] = None
        return None

    rs = apply_delay_filter(rs, DELAY_MIN)
    if rs.empty:
        _RS_CACHE[ticker] = None
        return None

    rs["ATR"] = compute_atr(rs, ATR_PERIOD)

    _RS_CACHE[ticker] = rs
    return rs

# ============================================================
# Load & merge config (Step8 base + Step9 sensitivity)
# ============================================================
def load_best_step8(path: str) -> dict:
    b8 = pd.read_csv(path).iloc[0].to_dict()
    need = ["ATAN_LONG","ATAN_SHORT","MAX_STOP_LONG","MAX_STOP_SHORT"]
    miss = [k for k in need if k not in b8 or pd.isna(b8.get(k))]
    if miss:
        raise ValueError(f"best_config_step8.csv missing/NaN keys: {miss}")
    return {k: float(b8[k]) for k in need}

def load_best_step9(path: str) -> dict:
    b9 = pd.read_csv(path).iloc[0].to_dict()
    return {
        "SENS_LONG": float(b9.get("SENS_LONG", 1.0)),
        "SENS_SHORT": float(b9.get("SENS_SHORT", 1.0)),
    }

def load_merged_config() -> dict:
    base = load_best_step8(BEST_STEP8_PATH)
    sens = load_best_step9(BEST_STEP9_PATH)
    cfg = {**base, **sens}
    print("Merged config:", cfg)
    return cfg

# ============================================================
# Trade extraction (NEW CSV schema)
# ============================================================
def build_trade_summary(raw: pd.DataFrame) -> pd.DataFrame:
    df = raw.copy()
    df.columns = [c.strip() for c in df.columns]

    required = ["TradeID","Currency","Direction","date","price","Opening Date","Closing Date"]
    missing = [c for c in required if c not in df.columns]
    if missing:
        raise ValueError(f"Trade file missing required columns: {missing}")

    df["date"] = pd.to_datetime(df["date"], errors="coerce")
    df["Opening Date"] = pd.to_datetime(df["Opening Date"], errors="coerce")
    df["Closing Date"] = pd.to_datetime(df["Closing Date"], errors="coerce")
    df["price"] = pd.to_numeric(df["price"], errors="coerce")

    df = df[df["date"].dt.year == YEAR_FILTER].copy()

    df["TradeBase"] = df["Currency"].apply(trade_base_from_currency)
    df["TickerNorm"] = df["TradeBase"].apply(map_trade_base_to_m5)
    df["DirectionNorm"] = df["Direction"].apply(normalize_direction)

    rows = []
    for tid, g in df.groupby("TradeID", dropna=True):
        g = g.sort_values("date")

        entry_date = g["Opening Date"].dropna().iloc[0] if g["Opening Date"].notna().any() else pd.NaT
        exit_date  = g["Closing Date"].dropna().iloc[0] if g["Closing Date"].notna().any() else pd.NaT

        direction = g["DirectionNorm"].dropna().iloc[0] if g["DirectionNorm"].notna().any() else "UNKNOWN"
        ticker = g["TickerNorm"].dropna().iloc[0] if g["TickerNorm"].notna().any() else ""

        entry_px = np.nan
        if pd.notna(entry_date):
            day_rows = g[g["date"].dt.normalize() == entry_date.normalize()]
            if day_rows["price"].notna().any():
                entry_px = float(day_rows["price"].dropna().iloc[-1])

        exit_px = np.nan
        if pd.notna(exit_date):
            day_rows = g[g["date"].dt.normalize() == exit_date.normalize()]
            if day_rows["price"].notna().any():
                exit_px = float(day_rows["price"].dropna().iloc[-1])

        valid_window = pd.notna(entry_date) and pd.notna(exit_date) and (exit_date.normalize() > entry_date.normalize())
        core_ok = (ticker != "" and ticker in M5_TICKERS and direction != "UNKNOWN" and
                   pd.notna(entry_date) and pd.notna(exit_date) and pd.notna(entry_px) and pd.notna(exit_px))

        rows.append({
            "TradeID": tid,
            "TickerNorm": ticker,
            "Direction": direction,
            "EntryDate": entry_date,
            "ExitDate_Original": exit_date,
            "EntryPrice": entry_px,
            "ExitPrice_Original": exit_px,
            "HasAllCoreFields": bool(core_ok),
            "HasValidTrailingWindow": bool(valid_window)
        })
    return pd.DataFrame(rows)

# ============================================================
# Trailing simulation
# ============================================================
def adaptive_stop_distance_pct(bars: pd.DataFrame,
                               atan_threshold: float,
                               atr_fallback_mult: float,
                               min_stop_pct: float,
                               max_stop_pct: float,
                               sensitivity: float) -> float:
    if len(bars) < REG_WINDOW or bars["ATR"].dropna().empty:
        return np.nan

    recent = bars["close"].iloc[-REG_WINDOW:].astype(float)
    if len(recent) < REG_WINDOW:
        return np.nan

    x = np.arange(len(recent), dtype=float)
    a, b, c = np.polyfit(x, recent.values, 2)

    slope_norm = (2 * a * x[-1] + b) / recent.iloc[-1]
    accel = (2 * a)
    atan_slope = float(np.arctan(slope_norm))

    atr = bars["ATR"].iloc[-1]
    px = bars["close"].iloc[-1]
    atr_pct = float(atr / px) if (pd.notna(atr) and atr > 0 and px > 0) else np.nan
    if pd.isna(atr_pct):
        return np.nan

    if abs(atan_slope) > atan_threshold:
        stop_pct = abs(slope_norm) * sensitivity * (1.0 + abs(accel))
        return float(np.clip(stop_pct, min_stop_pct, max_stop_pct))

    stop_pct = atr_pct * atr_fallback_mult
    return float(np.clip(stop_pct, min_stop_pct, max_stop_pct))

@dataclass
class TrailResult:
    exit_time: pd.Timestamp
    exit_price: float
    exit_reason: str

def price_improvement(direction: str, new_exit: float, old_exit: float) -> float:
    d = normalize_direction(direction)
    return (new_exit - old_exit) if d == "LONG" else (old_exit - new_exit)

def simulate_trade(tr: pd.Series, rs: pd.DataFrame, cfg: dict) -> TrailResult:
    entry_date = pd.to_datetime(tr["EntryDate"])
    exit_date  = pd.to_datetime(tr["ExitDate_Original"])
    entry_px   = float(tr["EntryPrice"])
    orig_exit_px = float(tr["ExitPrice_Original"])

    # next-day only trailing; skip same-day or invalid
    if exit_date.normalize() <= entry_date.normalize():
        return TrailResult(exit_date, orig_exit_px, "SameDayOrInvalidWindow")

    direction = normalize_direction(tr["Direction"])
    is_long = (direction == "LONG")

    atan_thr = cfg["ATAN_LONG"] if is_long else cfg["ATAN_SHORT"]
    max_stop = cfg["MAX_STOP_LONG"] if is_long else cfg["MAX_STOP_SHORT"]
    sens     = cfg["SENS_LONG"] if is_long else cfg["SENS_SHORT"]

    start_dt = entry_date + timedelta(days=1)
    end_dt   = exit_date + timedelta(days=1)

    w = rs[(rs["_dt"] >= start_dt) & (rs["_dt"] < end_dt)].copy()
    if w.empty:
        return TrailResult(exit_date, orig_exit_px, "NoRSDataInWindow")

    best_close = entry_px
    stop = -np.inf if is_long else np.inf

    for i in range(len(w)):
        sub = w.iloc[:i+1]
        row = w.iloc[i]
        dt = row["_dt"]

        close = float(row["close"])
        high = float(row["high"])
        low  = float(row["low"])

        if is_long:
            best_close = max(best_close, close)
        else:
            best_close = min(best_close, close)

        stop_pct = adaptive_stop_distance_pct(sub, atan_thr, ATR_FALLBACK_MULT, MIN_STOP_PCT, max_stop, sens)
        if pd.isna(stop_pct):
            continue

        if is_long:
            stop = max(stop, best_close * (1.0 - stop_pct))
            hit_val = close if TRIGGER_ON_CLOSE else low
            if hit_val <= stop:
                return TrailResult(dt, float(stop), "TrailingSL")
        else:
            stop = min(stop, best_close * (1.0 + stop_pct))
            hit_val = close if TRIGGER_ON_CLOSE else high
            if hit_val >= stop:
                return TrailResult(dt, float(stop), "TrailingSL")

    return TrailResult(exit_date, orig_exit_px, "OriginalExit")

def summarize(out: pd.DataFrame) -> pd.DataFrame:
    df = out.copy()
    df["TriggeredFlag"] = df["ExitReason"].eq("TrailingSL")
    df["ImprovedFlag"] = df["PriceImprovement"] > 0

    def agg(g):
        n = len(g)
        trig = int(g["TriggeredFlag"].sum())
        return {
            "Trades": n,
            "TrailingTriggered": trig,
            "PctTriggered": trig / n if n else np.nan,
            "Triggered_PctImproved": float(g.loc[g["TriggeredFlag"], "ImprovedFlag"].mean()) if trig else np.nan,
            "AvgPctImpact_All": float(g["PctImprovement_vs_OriginalExit"].mean(skipna=True)),
            "AvgPctImpact_Triggered": float(g.loc[g["TriggeredFlag"], "PctImprovement_vs_OriginalExit"].mean(skipna=True)) if trig else np.nan,
        }

    rows = [{"Group":"ALL", **agg(df)}]
    for d, g in df.groupby(df["Direction"].astype(str).str.upper().str.strip()):
        rows.append({"Group": f"Direction={d}", **agg(g)})
    return pd.DataFrame(rows)

# ============================================================
# MAIN (FULL YEAR)
# ============================================================
def main():
    cfg = load_merged_config()

    raw = read_trade_csv(TRADE_CSV_PATH)
    trades = build_trade_summary(raw)

    print("\nTradeIDs in year (pre-filter):", trades["TradeID"].nunique())
    print("Trades with core fields OK:", int(trades["HasAllCoreFields"].sum()))
    print("Trades with valid trailing window:", int(trades["HasValidTrailingWindow"].sum()))

    eligible = trades[(trades["HasAllCoreFields"]) & (trades["HasValidTrailingWindow"])].copy()
    if eligible.empty:
        raise RuntimeError("No eligible trades after filtering (core fields + exit>entry).")

    eligible = eligible.sort_values(["TickerNorm", "EntryDate", "TradeID"]).reset_index(drop=True)
    print("\nEligible trades to process:", len(eligible))
    print("Unique tickers in eligible:", eligible["TickerNorm"].nunique())

    # Preload RS for all tickers (ensures early errors show up)
    tickers = sorted(eligible["TickerNorm"].unique())
    print("\nPreloading resampled market-hours data for tickers:", len(tickers))
    for i, tkr in enumerate(tickers, 1):
        prepare_rs_for_ticker(tkr)
        if i % 25 == 0:
            print(f"  Loaded {i}/{len(tickers)} tickers...")

    out_rows = []
    dbg_rows = []

    for i, tr in eligible.iterrows():
        rs = prepare_rs_for_ticker(tr["TickerNorm"])
        if rs is None or rs.empty:
            dbg_rows.append({"TradeID": tr["TradeID"], "Reason": "MissingRSData"})
            continue

        res = simulate_trade(tr, rs, cfg)

        old_exit = float(tr["ExitPrice_Original"])
        new_exit = float(res.exit_price)
        impr = price_improvement(tr["Direction"], new_exit, old_exit)

        out_rows.append({
            "TradeID": tr["TradeID"],
            "TickerNorm": tr["TickerNorm"],
            "Direction": tr["Direction"],
            "EntryDate": tr["EntryDate"],
            "ExitDate_Original": tr["ExitDate_Original"],
            "ExitPrice_Original": old_exit,
            "ExitTime_Trailing": res.exit_time,
            "ExitPrice_Trailing": new_exit,
            "ExitReason": res.exit_reason,
            "PriceImprovement": impr,
            "PctImprovement_vs_OriginalExit": (impr / old_exit) if old_exit else np.nan
        })
        dbg_rows.append({"TradeID": tr["TradeID"], "Reason": res.exit_reason})

        if (i + 1) % PRINT_EVERY == 0:
            print(f"Processed {i+1}/{len(eligible)} trades...")

    out_df = pd.DataFrame(out_rows)
    summ_df = summarize(out_df)
    dbg_df = pd.DataFrame(dbg_rows)

    # QC: reason distribution and missing count
    reason_counts = dbg_df["Reason"].value_counts(dropna=False)

    out_path = os.path.join(OUT_DIR, f"trades_full_{YEAR_FILTER}.csv")
    summ_path = os.path.join(OUT_DIR, f"summary_full_{YEAR_FILTER}.csv")
    dbg_path = os.path.join(OUT_DIR, f"debug_reasons_full_{YEAR_FILTER}.csv")
    reason_path = os.path.join(OUT_DIR, f"reason_counts_full_{YEAR_FILTER}.csv")

    out_df.to_csv(out_path, index=False)
    summ_df.to_csv(summ_path, index=False)
    dbg_df.to_csv(dbg_path, index=False)
    reason_counts.rename_axis("Reason").reset_index(name="Count").to_csv(reason_path, index=False)

    print("\nSaved:", out_path)
    print("Saved:", summ_path)
    print("Saved:", dbg_path)
    print("Saved:", reason_path)

    print("\n=== FULL YEAR SUMMARY ===")
    print(summ_df.to_string(index=False))

    print("\n=== EXIT REASONS (full year) ===")
    print(reason_counts.to_string())

if __name__ == "__main__":
    main()


Merged config: {'ATAN_LONG': 0.0015, 'ATAN_SHORT': 0.0013, 'MAX_STOP_LONG': 0.012, 'MAX_STOP_SHORT': 0.012, 'SENS_LONG': 0.9, 'SENS_SHORT': 0.9}

TradeIDs in year (pre-filter): 45543
Trades with core fields OK: 38149
Trades with valid trailing window: 45371

Eligible trades to process: 38005
Unique tickers in eligible: 127

Preloading resampled market-hours data for tickers: 127


C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: 

  Loaded 25/127 tickers...


C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: 

  Loaded 50/127 tickers...


...

  Loaded 75/127 tickers...


C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: 

  Loaded 100/127 tickers...


C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_22704\668106968.py:152: 

  Loaded 125/127 tickers...
Processed 500/38005 trades...
Processed 1000/38005 trades...
Processed 1500/38005 trades...
Processed 2000/38005 trades...
Processed 2500/38005 trades...
Processed 3000/38005 trades...
Processed 3500/38005 trades...
Processed 4000/38005 trades...
Processed 4500/38005 trades...
Processed 5000/38005 trades...
Processed 5500/38005 trades...
Processed 6000/38005 trades...
Processed 6500/38005 trades...
Processed 7000/38005 trades...
Processed 7500/38005 trades...
Processed 8000/38005 trades...
Processed 8500/38005 trades...
Processed 9000/38005 trades...
Processed 9500/38005 trades...
Processed 10000/38005 trades...
Processed 10500/38005 trades...
Processed 11000/38005 trades...
Processed 11500/38005 trades...
Processed 12000/38005 trades...
Processed 12500/38005 trades...
Processed 13000/38005 trades...
Processed 13500/38005 trades...
Processed 14000/38005 trades...
Processed 14500/38005 trades...
Processed 15000/38005 trades...
Processed 15500/38005 trades...


In [4]:
import os
import numpy as np
import pandas as pd
from dataclasses import dataclass
from datetime import timedelta

# ============================================================
# CONFIG (EDIT THESE PATHS)
# ============================================================

TRADE_CSV_PATH = r"D:/work/Client/Maatra/Trade Level Data/Equities 14 vol trade data (Jan 2021 to Nov 2025).csv"

M5_DIR            = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data"
M5_FILE_LIST_PATH = r"D:/work/Client/Maatra/Trade Level Data/M5 Raw data/m5_file_list.csv"
MAPPING_XLSX_PATH = r"D:/work/Client/Maatra/Trade Level Data/Instrument Mapping.xlsx"

# Step 8 base params (dir-specific)
STEP8_DIR = r"D:/work/Client/Maatra/Trade Level Data/TrailingSL_CAPPED_MKT1430_2100_SME_15T_STEP8_DIRSPEC"
BEST_STEP8_PATH = os.path.join(STEP8_DIR, "best_config_step8.csv")

# Step 9 sensitivity
STEP9_DIR = r"D:/work/Client/Maatra/Trade Level Data/TrailingSL_CAPPED_MKT1430_2100_SME_15T_STEP9_SENSITIVITY"
BEST_STEP9_PATH = os.path.join(STEP9_DIR, "best_config_step9.csv")

YEAR_FILTER = 2025

OUT_DIR = os.path.join(os.path.dirname(TRADE_CSV_PATH), f"TrailingSL_OOS_{YEAR_FILTER}_FULLYEAR_STEP8STEP9_NEXTDAY_ONLY_INITIALSL")
os.makedirs(OUT_DIR, exist_ok=True)

# ============================================================
# Locked settings (same as pilot)
# ============================================================
MARKET_START = "14:30"
MARKET_END   = "21:00"
RESAMPLE_RULE = "15T"

ATR_PERIOD = 14
REG_WINDOW = 16
DELAY_MIN = 0

TRIGGER_ON_CLOSE = True
ATR_FALLBACK_MULT = 3.0

# --- Your new requirement: Initial SL must be >= 1% ---
INITIAL_MIN_STOP_PCT = 0.01   # 1%
# Keep trailing minimum as before (can be tighter later)
MIN_STOP_PCT = 0.0010         # 0.10%

# YOUR RULE
APPLY_FROM_NEXT_DAY_ONLY = True

# Progress printing frequency
PRINT_EVERY = 500

# ============================================================
# Robust CSV reader
# ============================================================
def read_trade_csv(path: str) -> pd.DataFrame:
    for enc in ["utf-8", "cp1252", "latin1"]:
        try:
            return pd.read_csv(path, encoding=enc, low_memory=False)
        except UnicodeDecodeError:
            continue
    return pd.read_csv(path, encoding="utf-8", encoding_errors="ignore", low_memory=False)

# ============================================================
# Helpers
# ============================================================
def normalize_ticker(x: str) -> str:
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return ""
    x = str(x).strip().upper()
    return "".join([ch for ch in x if ch.isalnum()])

def trade_base_from_currency(currency: str) -> str:
    if currency is None or (isinstance(currency, float) and np.isnan(currency)):
        return ""
    s = str(currency).strip().upper()
    base = s.split("/")[0].strip() if "/" in s else s
    return normalize_ticker(base)

def normalize_direction(x) -> str:
    if x is None or (isinstance(x, float) and np.isnan(x)):
        return "UNKNOWN"
    s = str(x).strip().upper()
    if s in ["LONG", "BUY", "B", "1", "1.0", "+1", "+1.0"]:
        return "LONG"
    if s in ["SHORT", "SELL", "S", "-1", "-1.0"]:
        return "SHORT"
    try:
        v = float(s)
        if v > 0: return "LONG"
        if v < 0: return "SHORT"
    except Exception:
        pass
    return "UNKNOWN"

def _todelta_hhmm(hhmm: str) -> pd.Timedelta:
    return pd.to_timedelta(hhmm + ":00")

# ============================================================
# Load mapping file
# ============================================================
def load_trade_to_m5_mapping(mapping_xlsx_path: str) -> dict:
    mp = pd.read_excel(mapping_xlsx_path)
    mp.columns = [c.strip() for c in mp.columns]
    if "org_symbol" not in mp.columns or "Symbol" not in mp.columns:
        raise ValueError("Mapping file must contain columns: org_symbol, Symbol")
    mp["m5_ticker"] = mp["org_symbol"].apply(normalize_ticker)
    mp["trade_base"] = mp["Symbol"].astype(str).str.upper().str.strip().str.split("/").str[0].apply(normalize_ticker)
    mp = mp[(mp["trade_base"] != "") & (mp["m5_ticker"] != "")]
    mp = mp.drop_duplicates(subset=["trade_base"], keep="first")
    return dict(zip(mp["trade_base"], mp["m5_ticker"]))

TRADE_TO_M5 = load_trade_to_m5_mapping(MAPPING_XLSX_PATH)

def map_trade_base_to_m5(trade_base: str) -> str:
    t = normalize_ticker(trade_base)
    return TRADE_TO_M5.get(t, t)

# ============================================================
# Load M5 file list
# ============================================================
def load_m5_file_map(m5_dir: str, file_list_path: str) -> dict:
    fl = pd.read_csv(file_list_path)
    fl.columns = [c.strip().lower() for c in fl.columns]
    if "ticker" not in fl.columns or "filename" not in fl.columns:
        raise ValueError("m5_file_list.csv must have columns: ticker, filename")
    fl["ticker_norm"] = fl["ticker"].apply(normalize_ticker)
    fl["path"] = fl["filename"].apply(lambda f: os.path.join(m5_dir, f))
    return dict(zip(fl["ticker_norm"], fl["path"]))

M5_MAP = load_m5_file_map(M5_DIR, M5_FILE_LIST_PATH)
M5_TICKERS = set(M5_MAP.keys())

# ============================================================
# M5 preparation (market hours + resample + ATR) with caching
# ============================================================
def filter_market_hours(df: pd.DataFrame) -> pd.DataFrame:
    if df.empty:
        return df
    dfi = df.set_index("_dt", drop=False).sort_index()
    dfi = dfi.between_time(MARKET_START, MARKET_END, inclusive="both")
    return dfi.reset_index(drop=True)

def apply_delay_filter(window: pd.DataFrame, delay_minutes: int) -> pd.DataFrame:
    if delay_minutes <= 0 or window.empty:
        return window
    w = window.copy()
    w["d"] = w["_dt"].dt.normalize()
    thr = w["d"] + pd.to_timedelta(MARKET_START + ":00")
    w = w[w["_dt"] >= (thr + pd.to_timedelta(delay_minutes, unit="m"))]
    return w.drop(columns=["d"])

def resample_ohlc(df: pd.DataFrame, rule: str) -> pd.DataFrame:
    if df.empty:
        return df
    dfi = df.set_index("_dt").sort_index()
    ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
        "open": "first",
        "high": "max",
        "low": "min",
        "close": "last",
    }).dropna()
    return ohlc.reset_index()

def compute_atr(df: pd.DataFrame, period: int) -> pd.Series:
    high = df["high"]
    low = df["low"]
    close = df["close"]
    tr = pd.concat([
        high - low,
        (high - close.shift(1)).abs(),
        (low - close.shift(1)).abs()
    ], axis=1).max(axis=1)
    return tr.rolling(period, min_periods=period).mean()

_RS_CACHE = {}

def prepare_rs_for_ticker(ticker: str):
    if ticker in _RS_CACHE:
        return _RS_CACHE[ticker]

    fp = M5_MAP.get(ticker)
    if not fp or not os.path.exists(fp):
        _RS_CACHE[ticker] = None
        return None

    df = pd.read_csv(fp)
    df.columns = [c.strip().lower() for c in df.columns]
    needed = ["date", "open", "high", "low", "close"]
    if not all(c in df.columns for c in needed):
        _RS_CACHE[ticker] = None
        return None

    df["_dt"] = pd.to_datetime(df["date"], errors="coerce")
    df = df.dropna(subset=["_dt"]).sort_values("_dt").reset_index(drop=True)

    for c in ["open", "high", "low", "close"]:
        df[c] = pd.to_numeric(df[c], errors="coerce")
    df = df.dropna(subset=["open", "high", "low", "close"])

    df = filter_market_hours(df)
    if df.empty:
        _RS_CACHE[ticker] = None
        return None

    rs = resample_ohlc(df, RESAMPLE_RULE)
    if rs.empty:
        _RS_CACHE[ticker] = None
        return None

    rs = apply_delay_filter(rs, DELAY_MIN)
    if rs.empty:
        _RS_CACHE[ticker] = None
        return None

    rs["ATR"] = compute_atr(rs, ATR_PERIOD)

    _RS_CACHE[ticker] = rs
    return rs

# ============================================================
# Load & merge config (Step8 base + Step9 sensitivity)
# ============================================================
def load_best_step8(path: str) -> dict:
    b8 = pd.read_csv(path).iloc[0].to_dict()
    need = ["ATAN_LONG","ATAN_SHORT","MAX_STOP_LONG","MAX_STOP_SHORT"]
    miss = [k for k in need if k not in b8 or pd.isna(b8.get(k))]
    if miss:
        raise ValueError(f"best_config_step8.csv missing/NaN keys: {miss}")
    return {k: float(b8[k]) for k in need}

def load_best_step9(path: str) -> dict:
    b9 = pd.read_csv(path).iloc[0].to_dict()
    return {
        "SENS_LONG": float(b9.get("SENS_LONG", 1.0)),
        "SENS_SHORT": float(b9.get("SENS_SHORT", 1.0)),
    }

def load_merged_config() -> dict:
    base = load_best_step8(BEST_STEP8_PATH)
    sens = load_best_step9(BEST_STEP9_PATH)
    cfg = {**base, **sens}
    print("Merged config:", cfg)
    return cfg

# ============================================================
# Trade extraction (NEW CSV schema)
# ============================================================
def build_trade_summary(raw: pd.DataFrame) -> pd.DataFrame:
    df = raw.copy()
    df.columns = [c.strip() for c in df.columns]

    required = ["TradeID","Currency","Direction","date","price","Opening Date","Closing Date"]
    missing = [c for c in required if c not in df.columns]
    if missing:
        raise ValueError(f"Trade file missing required columns: {missing}")

    df["date"] = pd.to_datetime(df["date"], errors="coerce")
    df["Opening Date"] = pd.to_datetime(df["Opening Date"], errors="coerce")
    df["Closing Date"] = pd.to_datetime(df["Closing Date"], errors="coerce")
    df["price"] = pd.to_numeric(df["price"], errors="coerce")

    df = df[df["date"].dt.year == YEAR_FILTER].copy()

    df["TradeBase"] = df["Currency"].apply(trade_base_from_currency)
    df["TickerNorm"] = df["TradeBase"].apply(map_trade_base_to_m5)
    df["DirectionNorm"] = df["Direction"].apply(normalize_direction)

    rows = []
    for tid, g in df.groupby("TradeID", dropna=True):
        g = g.sort_values("date")

        entry_date = g["Opening Date"].dropna().iloc[0] if g["Opening Date"].notna().any() else pd.NaT
        exit_date  = g["Closing Date"].dropna().iloc[0] if g["Closing Date"].notna().any() else pd.NaT

        direction = g["DirectionNorm"].dropna().iloc[0] if g["DirectionNorm"].notna().any() else "UNKNOWN"
        ticker = g["TickerNorm"].dropna().iloc[0] if g["TickerNorm"].notna().any() else ""

        entry_px = np.nan
        if pd.notna(entry_date):
            day_rows = g[g["date"].dt.normalize() == entry_date.normalize()]
            if day_rows["price"].notna().any():
                entry_px = float(day_rows["price"].dropna().iloc[-1])

        exit_px = np.nan
        if pd.notna(exit_date):
            day_rows = g[g["date"].dt.normalize() == exit_date.normalize()]
            if day_rows["price"].notna().any():
                exit_px = float(day_rows["price"].dropna().iloc[-1])

        valid_window = pd.notna(entry_date) and pd.notna(exit_date) and (exit_date.normalize() > entry_date.normalize())
        core_ok = (ticker != "" and ticker in M5_TICKERS and direction != "UNKNOWN" and
                   pd.notna(entry_date) and pd.notna(exit_date) and pd.notna(entry_px) and pd.notna(exit_px))

        rows.append({
            "TradeID": tid,
            "TickerNorm": ticker,
            "Direction": direction,
            "EntryDate": entry_date,
            "ExitDate_Original": exit_date,
            "EntryPrice": entry_px,
            "ExitPrice_Original": exit_px,
            "HasAllCoreFields": bool(core_ok),
            "HasValidTrailingWindow": bool(valid_window)
        })
    return pd.DataFrame(rows)

# ============================================================
# Trailing simulation
# ============================================================
def adaptive_stop_distance_pct(bars: pd.DataFrame,
                               atan_threshold: float,
                               atr_fallback_mult: float,
                               min_stop_pct: float,
                               max_stop_pct: float,
                               sensitivity: float) -> float:
    if len(bars) < REG_WINDOW or bars["ATR"].dropna().empty:
        return np.nan

    recent = bars["close"].iloc[-REG_WINDOW:].astype(float)
    if len(recent) < REG_WINDOW:
        return np.nan

    x = np.arange(len(recent), dtype=float)
    a, b, c = np.polyfit(x, recent.values, 2)

    slope_norm = (2 * a * x[-1] + b) / recent.iloc[-1]
    accel = (2 * a)
    atan_slope = float(np.arctan(slope_norm))

    atr = bars["ATR"].iloc[-1]
    px = bars["close"].iloc[-1]
    atr_pct = float(atr / px) if (pd.notna(atr) and atr > 0 and px > 0) else np.nan
    if pd.isna(atr_pct):
        return np.nan

    if abs(atan_slope) > atan_threshold:
        stop_pct = abs(slope_norm) * sensitivity * (1.0 + abs(accel))
        return float(np.clip(stop_pct, min_stop_pct, max_stop_pct))

    stop_pct = atr_pct * atr_fallback_mult
    return float(np.clip(stop_pct, min_stop_pct, max_stop_pct))

def compute_initial_stop_pct(rs: pd.DataFrame,
                             entry_date: pd.Timestamp,
                             entry_px: float,
                             direction: str,
                             cfg: dict) -> float:
    """
    Initial SL at ENTRY CLOSE:
    - Must be >= INITIAL_MIN_STOP_PCT (>=1%)
    - Can be wider, but capped by MAX_STOP_* for direction.
    Priority:
      1) adaptive_stop_distance_pct on history up to entry close (if available)
      2) ATR% * ATR_FALLBACK_MULT (if ATR available)
      3) INITIAL_MIN_STOP_PCT
    """
    direction = normalize_direction(direction)
    is_long = (direction == "LONG")

    atan_thr = cfg["ATAN_LONG"] if is_long else cfg["ATAN_SHORT"]
    max_stop = cfg["MAX_STOP_LONG"] if is_long else cfg["MAX_STOP_SHORT"]
    sens     = cfg["SENS_LONG"] if is_long else cfg["SENS_SHORT"]

    entry_close_dt = entry_date.normalize() + _todelta_hhmm(MARKET_END)

    hist = rs[rs["_dt"] <= entry_close_dt].copy()
    if hist.empty:
        return float(np.clip(INITIAL_MIN_STOP_PCT, INITIAL_MIN_STOP_PCT, max_stop))

    stop_pct = adaptive_stop_distance_pct(
        hist, atan_thr, ATR_FALLBACK_MULT, INITIAL_MIN_STOP_PCT, max_stop, sens
    )
    if pd.notna(stop_pct):
        return float(stop_pct)

    last = hist.iloc[-1]
    atr = last.get("ATR", np.nan)
    px  = last.get("close", np.nan)
    if pd.notna(atr) and atr > 0 and pd.notna(px) and px > 0:
        atr_pct = float(atr / px)
        stop_pct = atr_pct * ATR_FALLBACK_MULT
        return float(np.clip(stop_pct, INITIAL_MIN_STOP_PCT, max_stop))

    return float(np.clip(INITIAL_MIN_STOP_PCT, INITIAL_MIN_STOP_PCT, max_stop))

@dataclass
class TrailResult:
    exit_time: pd.Timestamp
    exit_price: float
    exit_reason: str
    initial_stop_pct: float
    initial_stop_price: float

def price_improvement(direction: str, new_exit: float, old_exit: float) -> float:
    d = normalize_direction(direction)
    return (new_exit - old_exit) if d == "LONG" else (old_exit - new_exit)

def simulate_trade(tr: pd.Series, rs: pd.DataFrame, cfg: dict) -> TrailResult:
    entry_date = pd.to_datetime(tr["EntryDate"])
    exit_date  = pd.to_datetime(tr["ExitDate_Original"])
    entry_px   = float(tr["EntryPrice"])
    orig_exit_px = float(tr["ExitPrice_Original"])

    if exit_date.normalize() <= entry_date.normalize():
        return TrailResult(exit_date, orig_exit_px, "SameDayOrInvalidWindow",
                           np.nan, np.nan)

    direction = normalize_direction(tr["Direction"])
    is_long = (direction == "LONG")

    # ----------------------------
    # Initial SL placed at entry close (>= 1%)
    # ----------------------------
    init_stop_pct = compute_initial_stop_pct(rs, entry_date, entry_px, direction, cfg)
    if is_long:
        stop = entry_px * (1.0 - init_stop_pct)
    else:
        stop = entry_px * (1.0 + init_stop_pct)

    initial_stop_price = float(stop)
    best_close = entry_px
    stop_source = "Initial"  # becomes "Trailing" once adaptive updates

    # Monitoring starts from next day market open
    start_dt = entry_date.normalize() + timedelta(days=1) + _todelta_hhmm(MARKET_START)
    end_dt   = exit_date + timedelta(days=1)

    w = rs[(rs["_dt"] >= start_dt) & (rs["_dt"] < end_dt)].copy()
    if w.empty:
        return TrailResult(exit_date, orig_exit_px, "NoRSDataInWindow",
                           float(init_stop_pct), float(initial_stop_price))

    for i in range(len(w)):
        sub = w.iloc[:i+1]
        row = w.iloc[i]
        dt = row["_dt"]

        close = float(row["close"])
        high = float(row["high"])
        low  = float(row["low"])

        if is_long:
            best_close = max(best_close, close)
        else:
            best_close = min(best_close, close)

        # 1) Check current stop first (so Initial SL can trigger immediately)
        if is_long:
            hit_val = close if TRIGGER_ON_CLOSE else low
            if hit_val <= stop:
                reason = "InitialSL" if stop_source == "Initial" else "TrailingSL"
                return TrailResult(dt, float(stop), reason,
                                   float(init_stop_pct), float(initial_stop_price))
        else:
            hit_val = close if TRIGGER_ON_CLOSE else high
            if hit_val >= stop:
                reason = "InitialSL" if stop_source == "Initial" else "TrailingSL"
                return TrailResult(dt, float(stop), reason,
                                   float(init_stop_pct), float(initial_stop_price))

        # 2) Then try to tighten via adaptive logic (may be NaN early)
        atan_thr = cfg["ATAN_LONG"] if is_long else cfg["ATAN_SHORT"]
        max_stop = cfg["MAX_STOP_LONG"] if is_long else cfg["MAX_STOP_SHORT"]
        sens     = cfg["SENS_LONG"] if is_long else cfg["SENS_SHORT"]

        stop_pct = adaptive_stop_distance_pct(
            sub, atan_thr, ATR_FALLBACK_MULT, MIN_STOP_PCT, max_stop, sens
        )
        if pd.isna(stop_pct):
            continue

        if is_long:
            stop = max(stop, best_close * (1.0 - stop_pct))
        else:
            stop = min(stop, best_close * (1.0 + stop_pct))

        stop_source = "Trailing"

    return TrailResult(exit_date, orig_exit_px, "OriginalExit",
                       float(init_stop_pct), float(initial_stop_price))

def summarize(out: pd.DataFrame) -> pd.DataFrame:
    df = out.copy()
    df["TriggeredFlag"] = df["ExitReason"].isin(["TrailingSL", "InitialSL"])
    df["ImprovedFlag"] = df["PriceImprovement"] > 0

    def agg(g):
        n = len(g)
        trig = int(g["TriggeredFlag"].sum())
        return {
            "Trades": n,
            "SLTriggered": trig,
            "PctTriggered": trig / n if n else np.nan,
            "Triggered_PctImproved": float(g.loc[g["TriggeredFlag"], "ImprovedFlag"].mean()) if trig else np.nan,
            "AvgPctImpact_All": float(g["PctImprovement_vs_OriginalExit"].mean(skipna=True)),
            "AvgPctImpact_Triggered": float(g.loc[g["TriggeredFlag"], "PctImprovement_vs_OriginalExit"].mean(skipna=True)) if trig else np.nan,
        }

    rows = [{"Group":"ALL", **agg(df)}]
    for d, g in df.groupby(df["Direction"].astype(str).str.upper().str.strip()):
        rows.append({"Group": f"Direction={d}", **agg(g)})
    return pd.DataFrame(rows)

# ============================================================
# MAIN (FULL YEAR)
# ============================================================
def main():
    cfg = load_merged_config()

    raw = read_trade_csv(TRADE_CSV_PATH)
    trades = build_trade_summary(raw)

    print("\nTradeIDs in year (pre-filter):", trades["TradeID"].nunique())
    print("Trades with core fields OK:", int(trades["HasAllCoreFields"].sum()))
    print("Trades with valid trailing window:", int(trades["HasValidTrailingWindow"].sum()))

    eligible = trades[(trades["HasAllCoreFields"]) & (trades["HasValidTrailingWindow"])].copy()
    if eligible.empty:
        raise RuntimeError("No eligible trades after filtering (core fields + exit>entry).")

    eligible = eligible.sort_values(["TickerNorm", "EntryDate", "TradeID"]).reset_index(drop=True)
    print("\nEligible trades to process:", len(eligible))
    print("Unique tickers in eligible:", eligible["TickerNorm"].nunique())

    # Preload RS for all tickers
    tickers = sorted(eligible["TickerNorm"].unique())
    print("\nPreloading resampled market-hours data for tickers:", len(tickers))
    for i, tkr in enumerate(tickers, 1):
        prepare_rs_for_ticker(tkr)
        if i % 25 == 0:
            print(f"  Loaded {i}/{len(tickers)} tickers...")

    out_rows = []
    dbg_rows = []

    for i, tr in eligible.iterrows():
        rs = prepare_rs_for_ticker(tr["TickerNorm"])
        if rs is None or rs.empty:
            dbg_rows.append({"TradeID": tr["TradeID"], "Reason": "MissingRSData"})
            continue

        res = simulate_trade(tr, rs, cfg)

        old_exit = float(tr["ExitPrice_Original"])
        new_exit = float(res.exit_price)
        impr = price_improvement(tr["Direction"], new_exit, old_exit)

        out_rows.append({
            "TradeID": tr["TradeID"],
            "TickerNorm": tr["TickerNorm"],
            "Direction": tr["Direction"],
            "EntryDate": tr["EntryDate"],
            "ExitDate_Original": tr["ExitDate_Original"],
            "EntryPrice": float(tr["EntryPrice"]),
            "InitialStopPct": res.initial_stop_pct,
            "InitialStopPrice": res.initial_stop_price,
            "ExitPrice_Original": old_exit,
            "ExitTime_Trailing": res.exit_time,
            "ExitPrice_Trailing": new_exit,
            "ExitReason": res.exit_reason,
            "PriceImprovement": impr,
            "PctImprovement_vs_OriginalExit": (impr / old_exit) if old_exit else np.nan
        })
        dbg_rows.append({"TradeID": tr["TradeID"], "Reason": res.exit_reason})

        if (i + 1) % PRINT_EVERY == 0:
            print(f"Processed {i+1}/{len(eligible)} trades...")

    out_df = pd.DataFrame(out_rows)
    summ_df = summarize(out_df)
    dbg_df = pd.DataFrame(dbg_rows)

    reason_counts = dbg_df["Reason"].value_counts(dropna=False)

    out_path = os.path.join(OUT_DIR, f"trades_full_{YEAR_FILTER}.csv")
    summ_path = os.path.join(OUT_DIR, f"summary_full_{YEAR_FILTER}.csv")
    dbg_path = os.path.join(OUT_DIR, f"debug_reasons_full_{YEAR_FILTER}.csv")
    reason_path = os.path.join(OUT_DIR, f"reason_counts_full_{YEAR_FILTER}.csv")

    out_df.to_csv(out_path, index=False)
    summ_df.to_csv(summ_path, index=False)
    dbg_df.to_csv(dbg_path, index=False)
    reason_counts.rename_axis("Reason").reset_index(name="Count").to_csv(reason_path, index=False)

    print("\nSaved:", out_path)
    print("Saved:", summ_path)
    print("Saved:", dbg_path)
    print("Saved:", reason_path)

    print("\n=== FULL YEAR SUMMARY ===")
    print(summ_df.to_string(index=False))

    print("\n=== EXIT REASONS (full year) ===")
    print(reason_counts.to_string())

if __name__ == "__main__":
    main()


Merged config: {'ATAN_LONG': 0.0015, 'ATAN_SHORT': 0.0013, 'MAX_STOP_LONG': 0.012, 'MAX_STOP_SHORT': 0.012, 'SENS_LONG': 0.9, 'SENS_SHORT': 0.9}

TradeIDs in year (pre-filter): 45543
Trades with core fields OK: 38149
Trades with valid trailing window: 45371

Eligible trades to process: 38005
Unique tickers in eligible: 127

Preloading resampled market-hours data for tickers: 127


C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:159: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:159: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:159: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:159: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:

  Loaded 25/127 tickers...


C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:159: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:159: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:159: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:159: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:

  Loaded 50/127 tickers...


...

  Loaded 75/127 tickers...


C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:159: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:159: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:159: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:159: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:

  Loaded 100/127 tickers...


C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:159: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:159: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:159: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:159: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  ohlc = dfi[["open","high","low","close"]].resample(rule).agg({
C:\Users\avina\AppData\Local\Temp\ipykernel_37676\1330883266.py:

  Loaded 125/127 tickers...
Processed 500/38005 trades...
Processed 1000/38005 trades...
Processed 1500/38005 trades...
Processed 2000/38005 trades...
Processed 2500/38005 trades...
Processed 3000/38005 trades...
Processed 3500/38005 trades...
Processed 4000/38005 trades...
Processed 4500/38005 trades...
Processed 5000/38005 trades...
Processed 5500/38005 trades...
Processed 6000/38005 trades...
Processed 6500/38005 trades...
Processed 7000/38005 trades...
Processed 7500/38005 trades...
Processed 8000/38005 trades...
Processed 8500/38005 trades...
Processed 9000/38005 trades...
Processed 9500/38005 trades...
Processed 10000/38005 trades...
Processed 10500/38005 trades...
Processed 11000/38005 trades...
Processed 11500/38005 trades...
Processed 12000/38005 trades...
Processed 12500/38005 trades...
Processed 13000/38005 trades...
Processed 13500/38005 trades...
Processed 14000/38005 trades...
Processed 14500/38005 trades...
Processed 15000/38005 trades...
Processed 15500/38005 trades...
